In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn import linear_model, metrics
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import Lasso
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split

import warnings
warnings.filterwarnings('ignore')

In [2]:
#load the dataset
df = pd.read_csv("train.csv")
df.head()

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0   1          60       RL         65.0     8450   Pave   NaN      Reg   
1   2          20       RL         80.0     9600   Pave   NaN      Reg   
2   3          60       RL         68.0    11250   Pave   NaN      IR1   
3   4          70       RL         60.0     9550   Pave   NaN      IR1   
4   5          60       RL         84.0    14260   Pave   NaN      IR1   

  LandContour Utilities  ... PoolArea PoolQC Fence MiscFeature MiscVal MoSold  \
0         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      2   
1         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      5   
2         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      9   
3         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      2   
4         Lvl    AllPub  ...        0    NaN   NaN         NaN       0     12   

  YrSold  SaleType  SaleCondition  SalePrice  
0   2008        WD         Normal     208500  
1   2007        WD         Normal     181500  
2   2008        WD         Normal     223500  
3   2006        WD        Abnorml     140000  
4   2008        WD         Normal     250000  

[5 rows x 81 columns]

In [3]:
#Find out columns which are having null values
df.isna().any()[lambda x: x]

LotFrontage     True
Alley           True
MasVnrType      True
MasVnrArea      True
BsmtQual        True
BsmtCond        True
BsmtExposure    True
BsmtFinType1    True
BsmtFinType2    True
Electrical      True
FireplaceQu     True
GarageType      True
GarageYrBlt     True
GarageFinish    True
GarageQual      True
GarageCond      True
PoolQC          True
Fence           True
MiscFeature     True
dtype: bool

In [4]:
#impute null values with meaningfully applicable data
df['LotFrontage'] = df['LotFrontage'].apply(lambda x:float(str(x).replace('nan','0.0')))
df['MasVnrArea'] = df['MasVnrArea'].apply(lambda x:float(str(x).replace('nan','0.0')))
avgYear = int(df['GarageYrBlt'].sum()/(len(df.index)-df['GarageYrBlt'].isnull().sum()))
df['GarageYrBlt'] = df['GarageYrBlt'].apply(lambda x:float(str(x).replace('nan','0.0')))
df['GarageYrBlt'] = df['GarageYrBlt'].astype(int)

In [5]:
df['Electrical'] = df['Electrical'].apply(lambda x:str(x).replace('na','None'))
df['Alley'] = df['Alley'].apply(lambda x:str(x).replace('na','None'))
df['MasVnrType'] = df['MasVnrType'].apply(lambda x:str(x).replace('na','None'))
df['BsmtQual'] = df['BsmtQual'].apply(lambda x:str(x).replace('na','None'))
df['BsmtCond'] = df['BsmtCond'].apply(lambda x:str(x).replace('na','None'))
df['BsmtExposure'] = df['BsmtExposure'].apply(lambda x:str(x).replace('na','None'))
df['BsmtFinType1'] = df['BsmtFinType1'].apply(lambda x:str(x).replace('na','None'))
df['BsmtFinType2'] = df['BsmtFinType2'].apply(lambda x:str(x).replace('na','None'))
df['FireplaceQu'] = df['FireplaceQu'].apply(lambda x:str(x).replace('na','None'))
df['GarageType'] = df['GarageType'].apply(lambda x:str(x).replace('na','None'))
df['GarageFinish'] = df['GarageFinish'].apply(lambda x:str(x).replace('na','None'))
df['GarageQual'] = df['GarageQual'].apply(lambda x:str(x).replace('na','None'))
df['GarageCond'] = df['GarageCond'].apply(lambda x:str(x).replace('na','None'))
df['PoolQC'] = df['PoolQC'].apply(lambda x:str(x).replace('na','None'))
df['Fence'] = df['Fence'].apply(lambda x:str(x).replace('na','None'))
df['MiscFeature'] = df['MiscFeature'].apply(lambda x:str(x).replace('na','None'))

In [6]:
df['Alley'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 1460 entries, 0 to 1459
Series name: Alley
Non-Null Count  Dtype 
--------------  ----- 
1460 non-null   object
dtypes: object(1)
memory usage: 11.5+ KB


In [7]:
df.isna().any()[lambda x: x]

Series([], dtype: bool)

In [8]:
df.head()

Id  MSSubClass MSZoning  LotFrontage  LotArea Street  Alley LotShape  \
0   1          60       RL         65.0     8450   Pave  Nonen      Reg   
1   2          20       RL         80.0     9600   Pave  Nonen      Reg   
2   3          60       RL         68.0    11250   Pave  Nonen      IR1   
3   4          70       RL         60.0     9550   Pave  Nonen      IR1   
4   5          60       RL         84.0    14260   Pave  Nonen      IR1   

  LandContour Utilities  ... PoolArea PoolQC  Fence MiscFeature MiscVal  \
0         Lvl    AllPub  ...        0  Nonen  Nonen       Nonen       0   
1         Lvl    AllPub  ...        0  Nonen  Nonen       Nonen       0   
2         Lvl    AllPub  ...        0  Nonen  Nonen       Nonen       0   
3         Lvl    AllPub  ...        0  Nonen  Nonen       Nonen       0   
4         Lvl    AllPub  ...        0  Nonen  Nonen       Nonen       0   

  MoSold YrSold  SaleType  SaleCondition  SalePrice  
0      2   2008        WD         Normal     208500  
1      5   2007        WD         Normal     181500  
2      9   2008        WD         Normal     223500  
3      2   2006        WD        Abnorml     140000  
4     12   2008        WD         Normal     250000  

[5 rows x 81 columns]

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1460 entries, 0 to 1459
Data columns (total 81 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Id             1460 non-null   int64  
 1   MSSubClass     1460 non-null   int64  
 2   MSZoning       1460 non-null   object 
 3   LotFrontage    1460 non-null   float64
 4   LotArea        1460 non-null   int64  
 5   Street         1460 non-null   object 
 6   Alley          1460 non-null   object 
 7   LotShape       1460 non-null   object 
 8   LandContour    1460 non-null   object 
 9   Utilities      1460 non-null   object 
 10  LotConfig      1460 non-null   object 
 11  LandSlope      1460 non-null   object 
 12  Neighborhood   1460 non-null   object 
 13  Condition1     1460 non-null   object 
 14  Condition2     1460 non-null   object 
 15  BldgType       1460 non-null   object 
 16  HouseStyle     1460 non-null   object 
 17  OverallQual    1460 non-null   int64  
 18  OverallC

In [10]:
df=df.drop('Id',axis=1)

#Add the dummies
dummy_columns = ['MSZoning','Street','LotShape','LandContour','Utilities','LotConfig','LandSlope','Neighborhood','Condition1','Condition2',
               'BldgType','HouseStyle','RoofStyle','RoofMatl','Exterior1st','Exterior2nd','MasVnrType','ExterQual','ExterCond','Foundation',
               'BsmtQual','BsmtCond','BsmtExposure','BsmtFinType1','BsmtFinType2','Heating','HeatingQC','CentralAir','Electrical','KitchenQual',
               'Functional','FireplaceQu','GarageType','GarageFinish','GarageQual','GarageCond','PavedDrive','PoolQC','Fence','MiscFeature',
               'SaleType','SaleCondition','Alley']

dummy = pd.get_dummies(df[dummy_columns], drop_first=True)
df = pd.concat([df,dummy],axis=1)
df = df.drop(dummy_columns,axis=1)
df.head()

MSSubClass  LotFrontage  LotArea  OverallQual  OverallCond  YearBuilt  \
0          60         65.0     8450            7            5       2003   
1          20         80.0     9600            6            8       1976   
2          60         68.0    11250            7            5       2001   
3          70         60.0     9550            7            5       1915   
4          60         84.0    14260            8            5       2000   

   YearRemodAdd  MasVnrArea  BsmtFinSF1  BsmtFinSF2  ...  SaleType_New  \
0          2003       196.0         706           0  ...             0   
1          1976         0.0         978           0  ...             0   
2          2002       162.0         486           0  ...             0   
3          1970         0.0         216           0  ...             0   
4          2000       350.0         655           0  ...             0   

   SaleType_Oth  SaleType_WD  SaleCondition_AdjLand  SaleCondition_Alloca  \
0             0            1                      0                     0   
1             0            1                      0                     0   
2             0            1                      0                     0   
3             0            1                      0                     0   
4             0            1                      0                     0   

   SaleCondition_Family  SaleCondition_Normal  SaleCondition_Partial  \
0                     0                     1                      0   
1                     0                     1                      0   
2                     0                     1                      0   
3                     0                     0                      0   
4                     0                     1                      0   

   Alley_Nonen  Alley_Pave  
0            1           0  
1            1           0  
2            1           0  
3            1           0  
4            1           0  

[5 rows x 262 columns]

In [11]:
df.info(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1460 entries, 0 to 1459
Data columns (total 262 columns):
 #    Column                 Dtype  
---   ------                 -----  
 0    MSSubClass             int64  
 1    LotFrontage            float64
 2    LotArea                int64  
 3    OverallQual            int64  
 4    OverallCond            int64  
 5    YearBuilt              int64  
 6    YearRemodAdd           int64  
 7    MasVnrArea             float64
 8    BsmtFinSF1             int64  
 9    BsmtFinSF2             int64  
 10   BsmtUnfSF              int64  
 11   TotalBsmtSF            int64  
 12   1stFlrSF               int64  
 13   2ndFlrSF               int64  
 14   LowQualFinSF           int64  
 15   GrLivArea              int64  
 16   BsmtFullBath           int64  
 17   BsmtHalfBath           int64  
 18   FullBath               int64  
 19   HalfBath               int64  
 20   BedroomAbvGr           int64  
 21   KitchenAbvGr           int64  
 22 

In [12]:
from sklearn.preprocessing import PolynomialFeatures, MinMaxScaler
scaler = MinMaxScaler()
col_to_scale = ['MSSubClass','OverallQual','LotArea','OverallCond','KitchenAbvGr','TotRmsAbvGrd','MasVnrArea','BsmtFinSF1']
df[df.columns] = scaler.fit_transform(df[df.columns])
df.head()

MSSubClass  LotFrontage   LotArea  OverallQual  OverallCond  YearBuilt  \
0    0.235294     0.207668  0.033420     0.666667        0.500   0.949275   
1    0.000000     0.255591  0.038795     0.555556        0.875   0.753623   
2    0.235294     0.217252  0.046507     0.666667        0.500   0.934783   
3    0.294118     0.191693  0.038561     0.666667        0.500   0.311594   
4    0.235294     0.268371  0.060576     0.777778        0.500   0.927536   

   YearRemodAdd  MasVnrArea  BsmtFinSF1  BsmtFinSF2  ...  SaleType_New  \
0      0.883333     0.12250    0.125089         0.0  ...           0.0   
1      0.433333     0.00000    0.173281         0.0  ...           0.0   
2      0.866667     0.10125    0.086109         0.0  ...           0.0   
3      0.333333     0.00000    0.038271         0.0  ...           0.0   
4      0.833333     0.21875    0.116052         0.0  ...           0.0   

   SaleType_Oth  SaleType_WD  SaleCondition_AdjLand  SaleCondition_Alloca  \
0           0.0          1.0                    0.0                   0.0   
1           0.0          1.0                    0.0                   0.0   
2           0.0          1.0                    0.0                   0.0   
3           0.0          1.0                    0.0                   0.0   
4           0.0          1.0                    0.0                   0.0   

   SaleCondition_Family  SaleCondition_Normal  SaleCondition_Partial  \
0                   0.0                   1.0                    0.0   
1                   0.0                   1.0                    0.0   
2                   0.0                   1.0                    0.0   
3                   0.0                   0.0                    0.0   
4                   0.0                   1.0                    0.0   

   Alley_Nonen  Alley_Pave  
0          1.0         0.0  
1          1.0         0.0  
2          1.0         0.0  
3          1.0         0.0  
4          1.0         0.0  

[5 rows x 262 columns]

In [13]:
y = df.pop('SalePrice')
X = df
y.head()

0    0.241078
1    0.203583
2    0.261908
3    0.145952
4    0.298709
Name: SalePrice, dtype: float64

In [14]:
#Split the data into train & test sets.
X_tr,X_te,y_tr,y_te = train_test_split(X,y, train_size=0.7,random_state=100)

In [15]:
X_tr.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1021 entries, 318 to 792
Columns: 261 entries, MSSubClass to Alley_Pave
dtypes: float64(261)
memory usage: 2.0 MB


In [16]:
from sklearn.linear_model import LinearRegression
from sklearn.feature_selection import RFE
lr = LinearRegression()
rfe = RFE(lr, step=30)
rfe = rfe.fit(X_tr, y_tr)

In [17]:
list(zip(X_tr.columns, rfe.support_, rfe.ranking_))

[('MSSubClass', False, 5),
 ('LotFrontage', False, 4),
 ('LotArea', True, 1),
 ('OverallQual', True, 1),
 ('OverallCond', True, 1),
 ('YearBuilt', True, 1),
 ('YearRemodAdd', True, 1),
 ('MasVnrArea', True, 1),
 ('BsmtFinSF1', True, 1),
 ('BsmtFinSF2', True, 1),
 ('BsmtUnfSF', True, 1),
 ('TotalBsmtSF', True, 1),
 ('1stFlrSF', True, 1),
 ('2ndFlrSF', True, 1),
 ('LowQualFinSF', True, 1),
 ('GrLivArea', True, 1),
 ('BsmtFullBath', True, 1),
 ('BsmtHalfBath', False, 6),
 ('FullBath', False, 5),
 ('HalfBath', True, 1),
 ('BedroomAbvGr', True, 1),
 ('KitchenAbvGr', True, 1),
 ('TotRmsAbvGrd', False, 6),
 ('Fireplaces', False, 4),
 ('GarageYrBlt', True, 1),
 ('GarageCars', True, 1),
 ('GarageArea', True, 1),
 ('WoodDeckSF', True, 1),
 ('OpenPorchSF', False, 4),
 ('EnclosedPorch', True, 1),
 ('3SsnPorch', False, 4),
 ('ScreenPorch', False, 2),
 ('PoolArea', True, 1),
 ('MiscVal', True, 1),
 ('MoSold', False, 4),
 ('YrSold', False, 4),
 ('MSZoning_FV', True, 1),
 ('MSZoning_RH', True, 1),
 ('

In [18]:
#Selecting columns suggested by rfe. 
col = X_tr.columns[rfe.support_]
col

Index(['LotArea', 'OverallQual', 'OverallCond', 'YearBuilt', 'YearRemodAdd',
       'MasVnrArea', 'BsmtFinSF1', 'BsmtFinSF2', 'BsmtUnfSF', 'TotalBsmtSF',
       ...
       'PoolQC_Gd', 'PoolQC_Nonen', 'MiscFeature_Nonen', 'MiscFeature_Othr',
       'MiscFeature_Shed', 'SaleType_Con', 'SaleType_New',
       'SaleCondition_AdjLand', 'SaleCondition_Alloca',
       'SaleCondition_Partial'],
      dtype='object', length=130)

In [19]:
X_tr = X_tr[col]
X_te = X_te[col]
y_train = y_tr
y_test = y_te

In [20]:
X_tr.head()

LotArea  OverallQual  OverallCond  YearBuilt  YearRemodAdd  MasVnrArea  \
318   0.040197     0.666667        0.500   0.876812      0.716667        0.16   
239   0.034780     0.555556        0.375   0.528986      0.000000        0.00   
986   0.018743     0.555556        0.875   0.275362      0.883333        0.00   
1416  0.046928     0.333333        0.625   0.094203      0.000000        0.00   
390   0.033209     0.444444        0.875   0.202899      0.000000        0.00   

      BsmtFinSF1  BsmtFinSF2  BsmtUnfSF  TotalBsmtSF  ...  PoolQC_Gd  \
318     0.174876    0.000000   0.154110     0.220458  ...        0.0   
239     0.016655    0.000000   0.274401     0.120295  ...        0.0   
986     0.000000    0.000000   0.207620     0.079378  ...        0.0   
1416    0.000000    0.000000   0.332620     0.127169  ...        0.0   
390     0.042700    0.265265   0.098031     0.140917  ...        0.0   

      PoolQC_Nonen  MiscFeature_Nonen  MiscFeature_Othr  MiscFeature_Shed  \
318            1.0                1.0               0.0               0.0   
239            1.0                1.0               0.0               0.0   
986            1.0                1.0               0.0               0.0   
1416           1.0                1.0               0.0               0.0   
390            1.0                1.0               0.0               0.0   

      SaleType_Con  SaleType_New  SaleCondition_AdjLand  SaleCondition_Alloca  \
318            0.0           0.0                    0.0                   0.0   
239            0.0           0.0                    0.0                   0.0   
986            0.0           0.0                    0.0                   0.0   
1416           0.0           0.0                    0.0                   0.0   
390            0.0           0.0                    0.0                   0.0   

      SaleCondition_Partial  
318                     0.0  
239                     0.0  
986                     0.0  
1416                    0.0  
390                     0.0  

[5 rows x 130 columns]

In [21]:
# LM value for this data is 
# R2 - Training : 0.9456798856254166
# R2 - Test     : 1.2594062741158006e+23
# Clearly model overfitting is a problem.

lm = LinearRegression()

# Fit a line
lm.fit(X_tr, y_tr)

LinearRegression()

In [22]:
from sklearn.metrics import r2_score, mean_squared_error
y_pred_train = lm.predict(X_tr)
y_pred_test = lm.predict(X_te)

metric = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric.append(mse_test_lr**0.5)

0.9456798856254166
-1.2594062741158006e+23
0.6685318285275208
6.862939117710612e+23
0.0006547814187341046
1.563311871915857e+21


In [23]:

from sklearn.model_selection import GridSearchCV

params = {'alpha': [0.0001, 0.001, 0.01, 0.05, 0.1, 
 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 2.0, 3.0, 
 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 20, 50, 100, 500, 1000 ]}

ridge = Ridge()

# cross validation
folds = 10
model_cv = GridSearchCV(estimator = ridge, 
                        param_grid = params, 
                        scoring= 'neg_mean_absolute_error',  
                        cv = folds, 
                        return_train_score=True,
                        verbose = 1)            
model_cv.fit(X_tr, y_tr)

print(model_cv.best_params_)


Fitting 10 folds for each of 28 candidates, totalling 280 fits
{'alpha': 0.3}


In [24]:

alpha = 0.2
ridge = Ridge(alpha=alpha)

ridge.fit(X_tr, y_tr)
print(ridge.coef_)

[ 1.22945129e-01  9.08148118e-02  5.77855212e-02  7.54739863e-02
  1.29318666e-02  3.57822937e-02  1.23719768e-01  2.27000306e-02
  1.85700563e-02  1.26859880e-01  1.85539933e-01  1.13664161e-01
 -8.70634121e-03  1.95614072e-01  2.12797671e-02 -1.31344717e-02
 -4.92728604e-02 -1.02414818e-01  9.01706006e-03  3.77786547e-02
  1.28403102e-02  1.14875762e-02 -3.45418417e-03  8.26138643e-02
  5.85205783e-03  1.77049147e-02  2.62813617e-02  2.41097439e-02
  1.91848915e-02  4.58991585e-02 -1.48994930e-03 -3.13526303e-02
  1.30756016e-02 -8.59857681e-03  1.12581440e-02  1.07034095e-02
  3.90953289e-02 -1.68472363e-02  2.28724194e-02  5.53421686e-02
  3.08464244e-02  2.88874954e-02  3.84175375e-02  1.56749445e-02
  1.71285952e-02  8.04177133e-02 -4.66005972e-01 -2.90735602e-02
 -1.14555700e-02  1.08566522e-02 -3.55232060e-02 -2.42777114e-02
  1.17312585e-02 -2.55179540e-02 -9.75943622e-03  1.18406431e-02
  1.95674488e-02  4.10427585e-02  7.70298288e-02  1.24904357e-01
  7.70110208e-02  6.12042

In [25]:
# Lets calculate some metrics such as R2 score, RSS and RMSE
y_test = y_te
y_train = y_tr
y_pred_train = ridge.predict(X_tr)
y_pred_test = ridge.predict(X_te)

metric2 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric2.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric2.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric2.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric2.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric2.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric2.append(mse_test_lr**0.5)

0.9364716044406161
0.6940980311428007
0.7818605490014722
1.666965324377708
0.0007657791860935085
0.0037971875270562828


In [26]:
import statsmodels.api as sm
X_tr_sm = sm.add_constant(X_tr) #adds const=1 column .. useful in intercept calc
X_te_sm = sm.add_constant(X_te)
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     138.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:09   Log-Likelihood:                 2295.0
No. Observations:                1021   AIC:                            -4360.
Df Residuals:                     906   BIC:                            -3793.
Df Model:                         114                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0361      0.484     -8.341      0.000      -4.986      -3.086
LotArea                   0.2032      0.028      7.259      0.000       0.148       0.258
OverallQual               0.0826      0.012      7.158      0.000       0.060       0.105
OverallCond               0.0560      0.009      6.264      0.000       0.038       0.074
YearBuilt                 0.0725      0.011      6.311      0.000       0.050       0.095
YearRemodAdd              0.0151      0.004      3.437      0.001       0.006       0.024
MasVnrArea                0.0435      0.009      4.636      0.000       0.025       0.062
BsmtFinSF1                0.1744      0.018      9.907      0.000       0.140       0.209
BsmtFinSF2                0.0283      0.009      3.152      0.002       0.011       0.046
BsmtUnfSF                 0.0250      0.008      3.176      0.002       0.010       0.040
TotalBsmtSF               0.1775      0.019      9.507      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.269      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.816      0.000       0.112       0.143
LowQualFinSF              0.0087      0.013      0.672      0.502      -0.017       0.034
GrLivArea                 0.2036      0.013     16.010      0.000       0.179       0.229
BsmtFullBath              0.0112      0.007      1.552      0.121      -0.003       0.025
HalfBath                 -0.0133      0.005     -2.590      0.010      -0.023      -0.003
BedroomAbvGr             -0.0631      0.013     -4.853      0.000      -0.089      -0.038
KitchenAbvGr             -0.1159      0.015     -7.580      0.000      -0.146      -0.086
GarageYrBlt               0.1011      0.162      0.623      0.533      -0.217       0.419
GarageCars                0.0163      0.012      1.308      0.191      -0.008       0.041
GarageArea                0.0304      0.015      1.975      0.049       0.000       0.061
WoodDeckSF                0.0108      0.007      1.586      0.113      -0.003       0.024
EnclosedPorch             0.0094      0.009      1.010      0.313      -0.009       0.028
PoolArea                  5.9174      0.729      8.114      0.000       4.486       7.349
MiscVal                   0.1082      0.125      0.867      0.386      -0.137       0.353
MSZoning_FV               0.0246      0.014      1.696      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.264      0.024       0.004       0.059
MSZoning_RL               0.0292      0.012      2.456      0.014       0.006       0.052
MSZoning_RM               0.0256      0.012      2.155      0.031       0.002       0.049
Street_Pave               0.0469      0.017      2.717      0.007       0.013       0.081
LandContour_Low        

In [27]:
lasso = Lasso()

# cross validation
model_cv = GridSearchCV(estimator = lasso, 
                        param_grid = params, 
                        scoring= 'neg_mean_absolute_error', 
                        cv = 10, 
                        return_train_score=True,
                        verbose = 1)            

model_cv.fit(X_tr, y_tr) 
print(model_cv.best_params_)


Fitting 10 folds for each of 28 candidates, totalling 280 fits
{'alpha': 0.0001}


In [28]:
alpha = 0.0001
lasso = Lasso(alpha=alpha)

lasso.fit(X_tr, y_tr)
print(lasso.coef_)

[ 6.88057377e-02  1.11860060e-01  5.29178702e-02  6.20699515e-02
  1.53483027e-02  2.60897091e-02  7.92230452e-02  0.00000000e+00
 -0.00000000e+00  1.84087889e-01  0.00000000e+00  1.42018792e-02
 -2.44427161e-02  4.03741733e-01  2.26725437e-02 -0.00000000e+00
 -2.97762145e-02 -8.51187290e-02 -0.00000000e+00  3.02328944e-02
  1.61153473e-02  1.28121022e-02 -0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  0.00000000e+00  7.41193354e-03
 -5.10625987e-05  4.29777713e-03  1.31932736e-03 -0.00000000e+00
  1.30094620e-02  0.00000000e+00  0.00000000e+00  9.29026667e-03
  3.33357193e-02 -1.15148822e-02  0.00000000e+00  5.56885326e-02
  2.91568528e-02  2.55855770e-02  2.56502714e-02  6.64333107e-03
  1.39818659e-02  0.00000000e+00 -4.42493551e-01 -0.00000000e+00
 -0.00000000e+00  0.00000000e+00 -3.00162484e-02 -1.67350048e-02
  3.21254979e-03 -0.00000000e+00 -0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00 -0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000

In [29]:


y_pred_train = lasso.predict(X_tr)
y_pred_test = lasso.predict(X_te)

metric3 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric3.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric3.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric3.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric3.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric3.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric3.append(mse_test_lr**0.5)

0.9279119121372996
0.6405771601229744
0.887206916789068
1.9586190082485389
0.0008689587823595182
0.004461546715828107


In [30]:
betas = pd.DataFrame(index=X_tr.columns)
betas.rows = X_tr.columns

betas['Linear'] = lm.coef_
betas['Ridge'] = ridge.coef_
betas['Lasso'] = lasso.coef_

pd.set_option('display.max_rows', None)
betas.head(68)

Linear     Ridge     Lasso
LotArea               2.031913e-01  0.122945  0.068806
OverallQual           8.026972e-02  0.090815  0.111860
OverallCond           5.257580e-02  0.057786  0.052918
YearBuilt             6.980190e-02  0.075474  0.062070
YearRemodAdd          1.541679e-02  0.012932  0.015348
MasVnrArea            4.311697e-02  0.035782  0.026090
BsmtFinSF1            7.643134e+11  0.123720  0.079223
BsmtFinSF2            1.996098e+11  0.022700  0.000000
BsmtUnfSF             3.163423e+11  0.018570 -0.000000
TotalBsmtSF          -8.274194e+11  0.126860  0.184088
1stFlrSF              1.918718e+11  0.185540  0.000000
2ndFlrSF              9.091675e+10  0.113664  0.014202
LowQualFinSF          2.518372e+10 -0.008706 -0.024443
GrLivArea            -2.336979e+11  0.195614  0.403742
BsmtFullBath          1.006317e-02  0.021280  0.022673
HalfBath             -1.336288e-02 -0.013134 -0.000000
BedroomAbvGr         -6.148148e-02 -0.049273 -0.029776
KitchenAbvGr         -1.167297e-01 -0.102415 -0.085119
GarageYrBlt           9.722900e-02  0.009017 -0.000000
GarageCars            1.821518e-02  0.037779  0.030233
GarageArea            2.757645e-02  0.012840  0.016115
WoodDeckSF            1.059723e-02  0.011488  0.012812
EnclosedPorch         8.327484e-03 -0.003454 -0.000000
PoolArea              6.390224e+00  0.082614  0.000000
MiscVal               1.282511e-01  0.005852  0.000000
MSZoning_FV           2.358437e-02  0.017705  0.000000
MSZoning_RH           3.474617e-02  0.026281  0.000000
MSZoning_RL           3.112793e-02  0.024110  0.007412
MSZoning_RM           2.795410e-02  0.019185 -0.000051
Street_Pave           4.595947e-02  0.045899  0.004298
LandContour_Low      -1.254272e-02 -0.001490  0.001319
Utilities_NoSeWa     -3.750849e-02 -0.031353 -0.000000
LotConfig_CulDSac     1.130676e-02  0.013076  0.013009
LandSlope_Sev        -4.785156e-02 -0.008599  0.000000
Neighborhood_Blueste  1.397228e-02  0.011258  0.000000
Neighborhood_BrkSide  1.232529e-02  0.010703  0.009290
Neighborhood_Crawfor  3.810120e-02  0.039095  0.033336
Neighborhood_Mitchel -1.502991e-02 -0.016847 -0.011515
Neighborhood_NPkVill  2.857208e-02  0.022872  0.000000
Neighborhood_NoRidge  3.894043e-02  0.055342  0.055689
Neighborhood_NridgHt  2.603149e-02  0.030846  0.029157
Neighborhood_Somerst  2.746964e-02  0.028887  0.025586
Neighborhood_StoneBr  3.582382e-02  0.038418  0.025650
Neighborhood_Veenker  1.705265e-02  0.015675  0.006643
Condition1_Norm       1.585388e-02  0.017129  0.013982
Condition2_PosA       8.850479e-02  0.080418  0.000000
Condition2_PosN      -6.167145e-01 -0.466006 -0.442494
Condition2_RRAe      -4.727983e-02 -0.029074 -0.000000
Condition2_RRAn      -1.238060e-02 -0.011456 -0.000000
Condition2_RRNn       1.318705e-02  0.010857  0.000000
BldgType_Twnhs       -3.105164e-02 -0.035523 -0.030016
BldgType_TwnhsE      -2.166748e-02 -0.024278 -0.016735
HouseStyle_1.5Unf     1.450348e-02  0.011731  0.003213
HouseStyle_2.5Fin    -4.649544e-02 -0.025518 -0.000000
HouseStyle_2.5Unf    -1.239586e-02 -0.009759 -0.000000
RoofStyle_Gambrel     1.033688e-02  0.011841  0.000000
RoofStyle_Mansard     2.439117e-02  0.019567  0.000000
RoofStyle_Shed        1.054001e-01  0.041043  0.000000
RoofMatl_CompShg     -3.436778e+10  0.077030 -0.000000
RoofMatl_Membran     -3.436778e+10  0.124904  0.000000
RoofMatl_Metal       -3.436778e+10  0.077011  0.000000
RoofMatl_Roll        -3.436778e+10  0.061204  0.000000
RoofMatl_Tar&Grv     -3.436778e+10  0.076768 -0.000000
RoofMatl_WdShake     -3.436778e+10  0.068799  0.000000
RoofMatl_WdShngl     -3.436778e+10  0.164138  0.073880
Exterior1st_AsphShn  -1.442619e+10 -0.010724 -0.000000
Exterior1st_BrkComm  -1.710892e-02 -0.010422 -0.000000
Exterior1st_BrkFace   2.481079e-02  0.030069  0.027601

In [31]:
lr_table = {'Metric': ['R2 Score (Train)','R2 Score (Test)','RSS (Train)','RSS (Test)',
                       'MSE (Train)','MSE (Test)'], 
        'Linear Regression': metric
        }

lr_metric = pd.DataFrame(lr_table ,columns = ['Metric', 'Linear Regression'] )

rg_metric = pd.Series(metric2, name = 'Ridge Regression')
ls_metric = pd.Series(metric3, name = 'Lasso Regression')

final_metric = pd.concat([lr_metric, rg_metric, ls_metric], axis = 1)

final_metric

Metric  Linear Regression  Ridge Regression  Lasso Regression
0  R2 Score (Train)       9.456799e-01          0.936472          0.927912
1   R2 Score (Test)      -1.259406e+23          0.694098          0.640577
2       RSS (Train)       6.685318e-01          0.781861          0.887207
3        RSS (Test)       6.862939e+23          1.666965          1.958619
4       MSE (Train)       2.558870e-02          0.027673          0.029478
5        MSE (Test)       3.953874e+10          0.061621          0.066795

In [32]:
#Looking at above R2 values for Linear, Ridge & Lasso Regression , could say model is overfit. 

In [33]:
#Remove the columns to address multicollinearity .
#find the columns whose P value under 0.05 & having low VIF value. After repeating steps for mulitple time
#Finally left with 30 columns in execution step number 147 of this notebook

In [34]:
import statsmodels.api as sm
X_tr_sm = sm.add_constant(X_tr) #adds const=1 column .. useful in intercept calc
X_te_sm = sm.add_constant(X_te)
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     138.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:14   Log-Likelihood:                 2295.0
No. Observations:                1021   AIC:                            -4360.
Df Residuals:                     906   BIC:                            -3793.
Df Model:                         114                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0361      0.484     -8.341      0.000      -4.986      -3.086
LotArea                   0.2032      0.028      7.259      0.000       0.148       0.258
OverallQual               0.0826      0.012      7.158      0.000       0.060       0.105
OverallCond               0.0560      0.009      6.264      0.000       0.038       0.074
YearBuilt                 0.0725      0.011      6.311      0.000       0.050       0.095
YearRemodAdd              0.0151      0.004      3.437      0.001       0.006       0.024
MasVnrArea                0.0435      0.009      4.636      0.000       0.025       0.062
BsmtFinSF1                0.1744      0.018      9.907      0.000       0.140       0.209
BsmtFinSF2                0.0283      0.009      3.152      0.002       0.011       0.046
BsmtUnfSF                 0.0250      0.008      3.176      0.002       0.010       0.040
TotalBsmtSF               0.1775      0.019      9.507      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.269      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.816      0.000       0.112       0.143
LowQualFinSF              0.0087      0.013      0.672      0.502      -0.017       0.034
GrLivArea                 0.2036      0.013     16.010      0.000       0.179       0.229
BsmtFullBath              0.0112      0.007      1.552      0.121      -0.003       0.025
HalfBath                 -0.0133      0.005     -2.590      0.010      -0.023      -0.003
BedroomAbvGr             -0.0631      0.013     -4.853      0.000      -0.089      -0.038
KitchenAbvGr             -0.1159      0.015     -7.580      0.000      -0.146      -0.086
GarageYrBlt               0.1011      0.162      0.623      0.533      -0.217       0.419
GarageCars                0.0163      0.012      1.308      0.191      -0.008       0.041
GarageArea                0.0304      0.015      1.975      0.049       0.000       0.061
WoodDeckSF                0.0108      0.007      1.586      0.113      -0.003       0.024
EnclosedPorch             0.0094      0.009      1.010      0.313      -0.009       0.028
PoolArea                  5.9174      0.729      8.114      0.000       4.486       7.349
MiscVal                   0.1082      0.125      0.867      0.386      -0.137       0.353
MSZoning_FV               0.0246      0.014      1.696      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.264      0.024       0.004       0.059
MSZoning_RL               0.0292      0.012      2.456      0.014       0.006       0.052
MSZoning_RM               0.0256      0.012      2.155      0.031       0.002       0.049
Street_Pave               0.0469      0.017      2.717      0.007       0.013       0.081
LandContour_Low        

In [35]:
X_tr_sm.pop('GarageCond_Po')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     138.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:14   Log-Likelihood:                 2295.0
No. Observations:                1021   AIC:                            -4360.
Df Residuals:                     906   BIC:                            -3793.
Df Model:                         114                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0361      0.484     -8.341      0.000      -4.986      -3.086
LotArea                   0.2032      0.028      7.259      0.000       0.148       0.258
OverallQual               0.0826      0.012      7.158      0.000       0.060       0.105
OverallCond               0.0560      0.009      6.264      0.000       0.038       0.074
YearBuilt                 0.0725      0.011      6.311      0.000       0.050       0.095
YearRemodAdd              0.0151      0.004      3.437      0.001       0.006       0.024
MasVnrArea                0.0435      0.009      4.636      0.000       0.025       0.062
BsmtFinSF1                0.1744      0.018      9.907      0.000       0.140       0.209
BsmtFinSF2                0.0283      0.009      3.152      0.002       0.011       0.046
BsmtUnfSF                 0.0250      0.008      3.176      0.002       0.010       0.040
TotalBsmtSF               0.1775      0.019      9.507      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.269      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.816      0.000       0.112       0.143
LowQualFinSF              0.0087      0.013      0.672      0.502      -0.017       0.034
GrLivArea                 0.2036      0.013     16.010      0.000       0.179       0.229
BsmtFullBath              0.0112      0.007      1.552      0.121      -0.003       0.025
HalfBath                 -0.0133      0.005     -2.590      0.010      -0.023      -0.003
BedroomAbvGr             -0.0631      0.013     -4.853      0.000      -0.089      -0.038
KitchenAbvGr             -0.1159      0.015     -7.580      0.000      -0.146      -0.086
GarageYrBlt               0.1011      0.162      0.623      0.533      -0.217       0.419
GarageCars                0.0163      0.012      1.308      0.191      -0.008       0.041
GarageArea                0.0304      0.015      1.975      0.049       0.000       0.061
WoodDeckSF                0.0108      0.007      1.586      0.113      -0.003       0.024
EnclosedPorch             0.0094      0.009      1.010      0.313      -0.009       0.028
PoolArea                  5.9174      0.729      8.114      0.000       4.486       7.349
MiscVal                   0.1082      0.125      0.867      0.386      -0.137       0.353
MSZoning_FV               0.0246      0.014      1.696      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.264      0.024       0.004       0.059
MSZoning_RL               0.0292      0.012      2.456      0.014       0.006       0.052
MSZoning_RM               0.0256      0.012      2.155      0.031       0.002       0.049
Street_Pave               0.0469      0.017      2.717      0.007       0.013       0.081
LandContour_Low        

In [36]:
X_tr_sm.pop('GarageQual_Gd')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     140.0
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:15   Log-Likelihood:                 2294.9
No. Observations:                1021   AIC:                            -4362.
Df Residuals:                     907   BIC:                            -3800.
Df Model:                         113                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0280      0.483     -8.333      0.000      -4.977      -3.079
LotArea                   0.2031      0.028      7.258      0.000       0.148       0.258
OverallQual               0.0824      0.012      7.149      0.000       0.060       0.105
OverallCond               0.0561      0.009      6.269      0.000       0.039       0.074
YearBuilt                 0.0726      0.011      6.322      0.000       0.050       0.095
YearRemodAdd              0.0152      0.004      3.458      0.001       0.007       0.024
MasVnrArea                0.0435      0.009      4.633      0.000       0.025       0.062
BsmtFinSF1                0.1740      0.018      9.902      0.000       0.140       0.209
BsmtFinSF2                0.0282      0.009      3.151      0.002       0.011       0.046
BsmtUnfSF                 0.0250      0.008      3.178      0.002       0.010       0.040
TotalBsmtSF               0.1771      0.019      9.501      0.000       0.141       0.214
1stFlrSF                  0.1868      0.017     11.303      0.000       0.154       0.219
2ndFlrSF                  0.1276      0.008     15.843      0.000       0.112       0.143
LowQualFinSF              0.0088      0.013      0.685      0.493      -0.016       0.034
GrLivArea                 0.2040      0.013     16.066      0.000       0.179       0.229
BsmtFullBath              0.0113      0.007      1.572      0.116      -0.003       0.025
HalfBath                 -0.0133      0.005     -2.605      0.009      -0.023      -0.003
BedroomAbvGr             -0.0633      0.013     -4.868      0.000      -0.089      -0.038
KitchenAbvGr             -0.1154      0.015     -7.573      0.000      -0.145      -0.085
GarageYrBlt               0.0949      0.162      0.587      0.557      -0.222       0.412
GarageCars                0.0162      0.012      1.308      0.191      -0.008       0.041
GarageArea                0.0306      0.015      1.990      0.047       0.000       0.061
WoodDeckSF                0.0109      0.007      1.604      0.109      -0.002       0.024
EnclosedPorch             0.0093      0.009      1.006      0.314      -0.009       0.027
PoolArea                  5.9227      0.729      8.126      0.000       4.492       7.353
MiscVal                   0.1113      0.125      0.894      0.372      -0.133       0.356
MSZoning_FV               0.0246      0.014      1.698      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.261      0.024       0.004       0.059
MSZoning_RL               0.0292      0.012      2.459      0.014       0.006       0.052
MSZoning_RM               0.0256      0.012      2.153      0.032       0.002       0.049
Street_Pave               0.0465      0.017      2.701      0.007       0.013       0.080
LandContour_Low        

In [37]:

X_tr_sm.pop('Condition2_RRNn')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     141.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:15   Log-Likelihood:                 2294.8
No. Observations:                1021   AIC:                            -4364.
Df Residuals:                     908   BIC:                            -3807.
Df Model:                         112                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0270      0.483     -8.335      0.000      -4.975      -3.079
LotArea                   0.2031      0.028      7.263      0.000       0.148       0.258
OverallQual               0.0824      0.012      7.154      0.000       0.060       0.105
OverallCond               0.0561      0.009      6.276      0.000       0.039       0.074
YearBuilt                 0.0728      0.011      6.345      0.000       0.050       0.095
YearRemodAdd              0.0153      0.004      3.490      0.001       0.007       0.024
MasVnrArea                0.0434      0.009      4.633      0.000       0.025       0.062
BsmtFinSF1                0.1739      0.018      9.899      0.000       0.139       0.208
BsmtFinSF2                0.0288      0.009      3.232      0.001       0.011       0.046
BsmtUnfSF                 0.0251      0.008      3.183      0.002       0.010       0.040
TotalBsmtSF               0.1771      0.019      9.505      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.298      0.000       0.154       0.219
2ndFlrSF                  0.1276      0.008     15.849      0.000       0.112       0.143
LowQualFinSF              0.0088      0.013      0.684      0.494      -0.017       0.034
GrLivArea                 0.2037      0.013     16.067      0.000       0.179       0.229
BsmtFullBath              0.0114      0.007      1.586      0.113      -0.003       0.026
HalfBath                 -0.0134      0.005     -2.612      0.009      -0.023      -0.003
BedroomAbvGr             -0.0634      0.013     -4.878      0.000      -0.089      -0.038
KitchenAbvGr             -0.1153      0.015     -7.576      0.000      -0.145      -0.085
GarageYrBlt               0.0913      0.161      0.566      0.571      -0.225       0.408
GarageCars                0.0161      0.012      1.297      0.195      -0.008       0.040
GarageArea                0.0313      0.015      2.041      0.042       0.001       0.061
WoodDeckSF                0.0110      0.007      1.615      0.107      -0.002       0.024
EnclosedPorch             0.0092      0.009      0.992      0.321      -0.009       0.027
PoolArea                  5.9265      0.728      8.136      0.000       4.497       7.356
MiscVal                   0.1108      0.125      0.890      0.374      -0.134       0.355
MSZoning_FV               0.0246      0.014      1.697      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.261      0.024       0.004       0.059
MSZoning_RL               0.0291      0.012      2.453      0.014       0.006       0.052
MSZoning_RM               0.0257      0.012      2.160      0.031       0.002       0.049
Street_Pave               0.0467      0.017      2.711      0.007       0.013       0.080
LandContour_Low        

In [38]:

X_tr_sm.pop('GarageFinish_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     141.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:15   Log-Likelihood:                 2294.8
No. Observations:                1021   AIC:                            -4364.
Df Residuals:                     908   BIC:                            -3807.
Df Model:                         112                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0270      0.483     -8.335      0.000      -4.975      -3.079
LotArea                   0.2031      0.028      7.263      0.000       0.148       0.258
OverallQual               0.0824      0.012      7.154      0.000       0.060       0.105
OverallCond               0.0561      0.009      6.276      0.000       0.039       0.074
YearBuilt                 0.0728      0.011      6.345      0.000       0.050       0.095
YearRemodAdd              0.0153      0.004      3.490      0.001       0.007       0.024
MasVnrArea                0.0434      0.009      4.633      0.000       0.025       0.062
BsmtFinSF1                0.1739      0.018      9.899      0.000       0.139       0.208
BsmtFinSF2                0.0288      0.009      3.232      0.001       0.011       0.046
BsmtUnfSF                 0.0251      0.008      3.183      0.002       0.010       0.040
TotalBsmtSF               0.1771      0.019      9.505      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.298      0.000       0.154       0.219
2ndFlrSF                  0.1276      0.008     15.849      0.000       0.112       0.143
LowQualFinSF              0.0088      0.013      0.684      0.494      -0.017       0.034
GrLivArea                 0.2037      0.013     16.067      0.000       0.179       0.229
BsmtFullBath              0.0114      0.007      1.586      0.113      -0.003       0.026
HalfBath                 -0.0134      0.005     -2.612      0.009      -0.023      -0.003
BedroomAbvGr             -0.0634      0.013     -4.878      0.000      -0.089      -0.038
KitchenAbvGr             -0.1153      0.015     -7.576      0.000      -0.145      -0.085
GarageYrBlt               0.0913      0.161      0.566      0.571      -0.225       0.408
GarageCars                0.0161      0.012      1.297      0.195      -0.008       0.040
GarageArea                0.0313      0.015      2.041      0.042       0.001       0.061
WoodDeckSF                0.0110      0.007      1.615      0.107      -0.002       0.024
EnclosedPorch             0.0092      0.009      0.992      0.321      -0.009       0.027
PoolArea                  5.9265      0.728      8.136      0.000       4.497       7.356
MiscVal                   0.1108      0.125      0.890      0.374      -0.134       0.355
MSZoning_FV               0.0246      0.014      1.697      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.261      0.024       0.004       0.059
MSZoning_RL               0.0291      0.012      2.453      0.014       0.006       0.052
MSZoning_RM               0.0257      0.012      2.160      0.031       0.002       0.049
Street_Pave               0.0467      0.017      2.711      0.007       0.013       0.080
LandContour_Low        

In [39]:


X_tr_sm.pop('GarageType_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     141.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:16   Log-Likelihood:                 2294.8
No. Observations:                1021   AIC:                            -4364.
Df Residuals:                     908   BIC:                            -3807.
Df Model:                         112                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0270      0.483     -8.335      0.000      -4.975      -3.079
LotArea                   0.2031      0.028      7.263      0.000       0.148       0.258
OverallQual               0.0824      0.012      7.154      0.000       0.060       0.105
OverallCond               0.0561      0.009      6.276      0.000       0.039       0.074
YearBuilt                 0.0728      0.011      6.345      0.000       0.050       0.095
YearRemodAdd              0.0153      0.004      3.490      0.001       0.007       0.024
MasVnrArea                0.0434      0.009      4.633      0.000       0.025       0.062
BsmtFinSF1                0.1739      0.018      9.899      0.000       0.139       0.208
BsmtFinSF2                0.0288      0.009      3.232      0.001       0.011       0.046
BsmtUnfSF                 0.0251      0.008      3.183      0.002       0.010       0.040
TotalBsmtSF               0.1771      0.019      9.505      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.298      0.000       0.154       0.219
2ndFlrSF                  0.1276      0.008     15.849      0.000       0.112       0.143
LowQualFinSF              0.0088      0.013      0.684      0.494      -0.017       0.034
GrLivArea                 0.2037      0.013     16.067      0.000       0.179       0.229
BsmtFullBath              0.0114      0.007      1.586      0.113      -0.003       0.026
HalfBath                 -0.0134      0.005     -2.612      0.009      -0.023      -0.003
BedroomAbvGr             -0.0634      0.013     -4.878      0.000      -0.089      -0.038
KitchenAbvGr             -0.1153      0.015     -7.576      0.000      -0.145      -0.085
GarageYrBlt               0.0913      0.161      0.566      0.571      -0.225       0.408
GarageCars                0.0161      0.012      1.297      0.195      -0.008       0.040
GarageArea                0.0313      0.015      2.041      0.042       0.001       0.061
WoodDeckSF                0.0110      0.007      1.615      0.107      -0.002       0.024
EnclosedPorch             0.0092      0.009      0.992      0.321      -0.009       0.027
PoolArea                  5.9265      0.728      8.136      0.000       4.497       7.356
MiscVal                   0.1108      0.125      0.890      0.374      -0.134       0.355
MSZoning_FV               0.0246      0.014      1.697      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.261      0.024       0.004       0.059
MSZoning_RL               0.0291      0.012      2.453      0.014       0.006       0.052
MSZoning_RM               0.0257      0.012      2.160      0.031       0.002       0.049
Street_Pave               0.0467      0.017      2.711      0.007       0.013       0.080
LandContour_Low        

In [40]:

X_tr_sm.pop('GarageCond_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     141.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:16   Log-Likelihood:                 2294.8
No. Observations:                1021   AIC:                            -4364.
Df Residuals:                     908   BIC:                            -3807.
Df Model:                         112                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0270      0.483     -8.335      0.000      -4.975      -3.079
LotArea                   0.2031      0.028      7.263      0.000       0.148       0.258
OverallQual               0.0824      0.012      7.154      0.000       0.060       0.105
OverallCond               0.0561      0.009      6.276      0.000       0.039       0.074
YearBuilt                 0.0728      0.011      6.345      0.000       0.050       0.095
YearRemodAdd              0.0153      0.004      3.490      0.001       0.007       0.024
MasVnrArea                0.0434      0.009      4.633      0.000       0.025       0.062
BsmtFinSF1                0.1739      0.018      9.899      0.000       0.139       0.208
BsmtFinSF2                0.0288      0.009      3.232      0.001       0.011       0.046
BsmtUnfSF                 0.0251      0.008      3.183      0.002       0.010       0.040
TotalBsmtSF               0.1771      0.019      9.505      0.000       0.141       0.214
1stFlrSF                  0.1865      0.017     11.298      0.000       0.154       0.219
2ndFlrSF                  0.1276      0.008     15.849      0.000       0.112       0.143
LowQualFinSF              0.0088      0.013      0.684      0.494      -0.017       0.034
GrLivArea                 0.2037      0.013     16.067      0.000       0.179       0.229
BsmtFullBath              0.0114      0.007      1.586      0.113      -0.003       0.026
HalfBath                 -0.0134      0.005     -2.612      0.009      -0.023      -0.003
BedroomAbvGr             -0.0634      0.013     -4.878      0.000      -0.089      -0.038
KitchenAbvGr             -0.1153      0.015     -7.576      0.000      -0.145      -0.085
GarageYrBlt               0.0913      0.161      0.566      0.571      -0.225       0.408
GarageCars                0.0161      0.012      1.297      0.195      -0.008       0.040
GarageArea                0.0313      0.015      2.041      0.042       0.001       0.061
WoodDeckSF                0.0110      0.007      1.615      0.107      -0.002       0.024
EnclosedPorch             0.0092      0.009      0.992      0.321      -0.009       0.027
PoolArea                  5.9265      0.728      8.136      0.000       4.497       7.356
MiscVal                   0.1108      0.125      0.890      0.374      -0.134       0.355
MSZoning_FV               0.0246      0.014      1.697      0.090      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.261      0.024       0.004       0.059
MSZoning_RL               0.0291      0.012      2.453      0.014       0.006       0.052
MSZoning_RM               0.0257      0.012      2.160      0.031       0.002       0.049
Street_Pave               0.0467      0.017      2.711      0.007       0.013       0.080
LandContour_Low        

In [41]:

X_tr_sm.pop('GarageQual_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     142.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:16   Log-Likelihood:                 2294.6
No. Observations:                1021   AIC:                            -4365.
Df Residuals:                     909   BIC:                            -3813.
Df Model:                         111                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9870      0.476     -8.370      0.000      -4.922      -3.052
LotArea                   0.2028      0.028      7.256      0.000       0.148       0.258
OverallQual               0.0824      0.012      7.155      0.000       0.060       0.105
OverallCond               0.0557      0.009      6.259      0.000       0.038       0.073
YearBuilt                 0.0746      0.011      6.870      0.000       0.053       0.096
YearRemodAdd              0.0158      0.004      3.717      0.000       0.007       0.024
MasVnrArea                0.0431      0.009      4.612      0.000       0.025       0.061
BsmtFinSF1                0.1734      0.018      9.891      0.000       0.139       0.208
BsmtFinSF2                0.0285      0.009      3.213      0.001       0.011       0.046
BsmtUnfSF                 0.0249      0.008      3.172      0.002       0.010       0.040
TotalBsmtSF               0.1766      0.019      9.496      0.000       0.140       0.213
1stFlrSF                  0.1862      0.016     11.292      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.847      0.000       0.112       0.143
LowQualFinSF              0.0092      0.013      0.710      0.478      -0.016       0.034
GrLivArea                 0.2035      0.013     16.066      0.000       0.179       0.228
BsmtFullBath              0.0112      0.007      1.561      0.119      -0.003       0.025
HalfBath                 -0.0134      0.005     -2.618      0.009      -0.023      -0.003
BedroomAbvGr             -0.0633      0.013     -4.873      0.000      -0.089      -0.038
KitchenAbvGr             -0.1153      0.015     -7.578      0.000      -0.145      -0.085
GarageYrBlt               0.0109      0.018      0.615      0.539      -0.024       0.046
GarageCars                0.0164      0.012      1.323      0.186      -0.008       0.041
GarageArea                0.0331      0.015      2.226      0.026       0.004       0.062
WoodDeckSF                0.0112      0.007      1.645      0.100      -0.002       0.024
EnclosedPorch             0.0094      0.009      1.016      0.310      -0.009       0.028
PoolArea                  5.9675      0.724      8.247      0.000       4.547       7.388
MiscVal                   0.1142      0.124      0.919      0.358      -0.130       0.358
MSZoning_FV               0.0243      0.014      1.682      0.093      -0.004       0.053
MSZoning_RH               0.0312      0.014      2.244      0.025       0.004       0.058
MSZoning_RL               0.0288      0.012      2.431      0.015       0.006       0.052
MSZoning_RM               0.0254      0.012      2.138      0.033       0.002       0.049
Street_Pave               0.0471      0.017      2.743      0.006       0.013       0.081
LandContour_Low        

In [42]:

X_tr_sm.pop('Condition2_RRAn')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     144.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:17   Log-Likelihood:                 2294.5
No. Observations:                1021   AIC:                            -4367.
Df Residuals:                     910   BIC:                            -3820.
Df Model:                         110                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9867      0.476     -8.373      0.000      -4.921      -3.052
LotArea                   0.2027      0.028      7.257      0.000       0.148       0.258
OverallQual               0.0825      0.012      7.173      0.000       0.060       0.105
OverallCond               0.0554      0.009      6.242      0.000       0.038       0.073
YearBuilt                 0.0744      0.011      6.857      0.000       0.053       0.096
YearRemodAdd              0.0158      0.004      3.727      0.000       0.007       0.024
MasVnrArea                0.0431      0.009      4.612      0.000       0.025       0.061
BsmtFinSF1                0.1733      0.018      9.890      0.000       0.139       0.208
BsmtFinSF2                0.0285      0.009      3.209      0.001       0.011       0.046
BsmtUnfSF                 0.0247      0.008      3.148      0.002       0.009       0.040
TotalBsmtSF               0.1764      0.019      9.492      0.000       0.140       0.213
1stFlrSF                  0.1862      0.016     11.298      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.860      0.000       0.112       0.143
LowQualFinSF              0.0091      0.013      0.708      0.479      -0.016       0.034
GrLivArea                 0.2035      0.013     16.076      0.000       0.179       0.228
BsmtFullBath              0.0112      0.007      1.562      0.119      -0.003       0.025
HalfBath                 -0.0134      0.005     -2.622      0.009      -0.023      -0.003
BedroomAbvGr             -0.0633      0.013     -4.874      0.000      -0.089      -0.038
KitchenAbvGr             -0.1165      0.015     -7.730      0.000      -0.146      -0.087
GarageYrBlt               0.0111      0.018      0.625      0.532      -0.024       0.046
GarageCars                0.0164      0.012      1.324      0.186      -0.008       0.041
GarageArea                0.0331      0.015      2.228      0.026       0.004       0.062
WoodDeckSF                0.0112      0.007      1.652      0.099      -0.002       0.025
EnclosedPorch             0.0093      0.009      1.010      0.313      -0.009       0.027
PoolArea                  5.9679      0.723      8.251      0.000       4.548       7.387
MiscVal                   0.1141      0.124      0.918      0.359      -0.130       0.358
MSZoning_FV               0.0243      0.014      1.681      0.093      -0.004       0.053
MSZoning_RH               0.0313      0.014      2.256      0.024       0.004       0.059
MSZoning_RL               0.0288      0.012      2.437      0.015       0.006       0.052
MSZoning_RM               0.0255      0.012      2.148      0.032       0.002       0.049
Street_Pave               0.0473      0.017      2.752      0.006       0.014       0.081
LandContour_Low        

In [43]:

X_tr_sm.pop('Neighborhood_Blueste')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     145.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:17   Log-Likelihood:                 2294.3
No. Observations:                1021   AIC:                            -4369.
Df Residuals:                     911   BIC:                            -3826.
Df Model:                         109                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9848      0.476     -8.373      0.000      -4.919      -3.051
LotArea                   0.2026      0.028      7.254      0.000       0.148       0.257
OverallQual               0.0825      0.011      7.174      0.000       0.060       0.105
OverallCond               0.0556      0.009      6.262      0.000       0.038       0.073
YearBuilt                 0.0744      0.011      6.863      0.000       0.053       0.096
YearRemodAdd              0.0158      0.004      3.719      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.598      0.000       0.025       0.061
BsmtFinSF1                0.1731      0.018      9.886      0.000       0.139       0.207
BsmtFinSF2                0.0290      0.009      3.293      0.001       0.012       0.046
BsmtUnfSF                 0.0247      0.008      3.152      0.002       0.009       0.040
TotalBsmtSF               0.1764      0.019      9.495      0.000       0.140       0.213
1stFlrSF                  0.1863      0.016     11.308      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.872      0.000       0.112       0.143
LowQualFinSF              0.0091      0.013      0.707      0.480      -0.016       0.034
GrLivArea                 0.2036      0.013     16.090      0.000       0.179       0.228
BsmtFullBath              0.0114      0.007      1.588      0.113      -0.003       0.025
HalfBath                 -0.0134      0.005     -2.623      0.009      -0.023      -0.003
BedroomAbvGr             -0.0631      0.013     -4.863      0.000      -0.089      -0.038
KitchenAbvGr             -0.1166      0.015     -7.742      0.000      -0.146      -0.087
GarageYrBlt               0.0110      0.018      0.624      0.533      -0.024       0.046
GarageCars                0.0166      0.012      1.340      0.181      -0.008       0.041
GarageArea                0.0331      0.015      2.230      0.026       0.004       0.062
WoodDeckSF                0.0113      0.007      1.662      0.097      -0.002       0.025
EnclosedPorch             0.0093      0.009      1.004      0.316      -0.009       0.027
PoolArea                  5.9642      0.723      8.249      0.000       4.545       7.383
MiscVal                   0.1143      0.124      0.921      0.357      -0.129       0.358
MSZoning_FV               0.0241      0.014      1.667      0.096      -0.004       0.052
MSZoning_RH               0.0313      0.014      2.250      0.025       0.004       0.059
MSZoning_RL               0.0287      0.012      2.428      0.015       0.006       0.052
MSZoning_RM               0.0255      0.012      2.147      0.032       0.002       0.049
Street_Pave               0.0473      0.017      2.758      0.006       0.014       0.081
LandContour_Low        

In [44]:

X_tr_sm.pop('BsmtExposure_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     147.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:17   Log-Likelihood:                 2294.1
No. Observations:                1021   AIC:                            -4370.
Df Residuals:                     912   BIC:                            -3833.
Df Model:                         108                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9837      0.476     -8.373      0.000      -4.917      -3.050
LotArea                   0.2022      0.028      7.245      0.000       0.147       0.257
OverallQual               0.0825      0.011      7.175      0.000       0.060       0.105
OverallCond               0.0556      0.009      6.272      0.000       0.038       0.073
YearBuilt                 0.0744      0.011      6.861      0.000       0.053       0.096
YearRemodAdd              0.0158      0.004      3.717      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.592      0.000       0.025       0.061
BsmtFinSF1                0.1732      0.018      9.893      0.000       0.139       0.208
BsmtFinSF2                0.0290      0.009      3.294      0.001       0.012       0.046
BsmtUnfSF                 0.0247      0.008      3.145      0.002       0.009       0.040
TotalBsmtSF               0.1764      0.019      9.499      0.000       0.140       0.213
1stFlrSF                  0.1864      0.016     11.319      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.871      0.000       0.112       0.143
LowQualFinSF              0.0091      0.013      0.705      0.481      -0.016       0.034
GrLivArea                 0.2036      0.013     16.101      0.000       0.179       0.228
BsmtFullBath              0.0114      0.007      1.595      0.111      -0.003       0.025
HalfBath                 -0.0135      0.005     -2.634      0.009      -0.024      -0.003
BedroomAbvGr             -0.0630      0.013     -4.856      0.000      -0.088      -0.038
KitchenAbvGr             -0.1166      0.015     -7.749      0.000      -0.146      -0.087
GarageYrBlt               0.0110      0.018      0.621      0.535      -0.024       0.046
GarageCars                0.0166      0.012      1.343      0.180      -0.008       0.041
GarageArea                0.0332      0.015      2.236      0.026       0.004       0.062
WoodDeckSF                0.0112      0.007      1.658      0.098      -0.002       0.025
EnclosedPorch             0.0093      0.009      1.003      0.316      -0.009       0.027
PoolArea                  5.9624      0.723      8.250      0.000       4.544       7.381
MiscVal                   0.1143      0.124      0.921      0.357      -0.129       0.358
MSZoning_FV               0.0241      0.014      1.670      0.095      -0.004       0.052
MSZoning_RH               0.0313      0.014      2.251      0.025       0.004       0.059
MSZoning_RL               0.0287      0.012      2.429      0.015       0.006       0.052
MSZoning_RM               0.0255      0.012      2.149      0.032       0.002       0.049
Street_Pave               0.0473      0.017      2.758      0.006       0.014       0.081
LandContour_Low        

In [45]:

X_tr_sm.pop('Exterior1st_AsphShn')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     147.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:18   Log-Likelihood:                 2294.1
No. Observations:                1021   AIC:                            -4370.
Df Residuals:                     912   BIC:                            -3833.
Df Model:                         108                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9837      0.476     -8.373      0.000      -4.917      -3.050
LotArea                   0.2022      0.028      7.245      0.000       0.147       0.257
OverallQual               0.0825      0.011      7.175      0.000       0.060       0.105
OverallCond               0.0556      0.009      6.272      0.000       0.038       0.073
YearBuilt                 0.0744      0.011      6.861      0.000       0.053       0.096
YearRemodAdd              0.0158      0.004      3.717      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.592      0.000       0.025       0.061
BsmtFinSF1                0.1732      0.018      9.893      0.000       0.139       0.208
BsmtFinSF2                0.0290      0.009      3.294      0.001       0.012       0.046
BsmtUnfSF                 0.0247      0.008      3.145      0.002       0.009       0.040
TotalBsmtSF               0.1764      0.019      9.499      0.000       0.140       0.213
1stFlrSF                  0.1864      0.016     11.319      0.000       0.154       0.219
2ndFlrSF                  0.1275      0.008     15.871      0.000       0.112       0.143
LowQualFinSF              0.0091      0.013      0.705      0.481      -0.016       0.034
GrLivArea                 0.2036      0.013     16.101      0.000       0.179       0.228
BsmtFullBath              0.0114      0.007      1.595      0.111      -0.003       0.025
HalfBath                 -0.0135      0.005     -2.634      0.009      -0.024      -0.003
BedroomAbvGr             -0.0630      0.013     -4.856      0.000      -0.088      -0.038
KitchenAbvGr             -0.1166      0.015     -7.749      0.000      -0.146      -0.087
GarageYrBlt               0.0110      0.018      0.621      0.535      -0.024       0.046
GarageCars                0.0166      0.012      1.343      0.180      -0.008       0.041
GarageArea                0.0332      0.015      2.236      0.026       0.004       0.062
WoodDeckSF                0.0112      0.007      1.658      0.098      -0.002       0.025
EnclosedPorch             0.0093      0.009      1.003      0.316      -0.009       0.027
PoolArea                  5.9624      0.723      8.250      0.000       4.544       7.381
MiscVal                   0.1143      0.124      0.921      0.357      -0.129       0.358
MSZoning_FV               0.0241      0.014      1.670      0.095      -0.004       0.052
MSZoning_RH               0.0313      0.014      2.251      0.025       0.004       0.059
MSZoning_RL               0.0287      0.012      2.429      0.015       0.006       0.052
MSZoning_RM               0.0255      0.012      2.149      0.032       0.002       0.049
Street_Pave               0.0473      0.017      2.758      0.006       0.014       0.081
LandContour_Low        

In [46]:

X_tr_sm.pop('GarageCond_Fa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     148.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:18   Log-Likelihood:                 2293.9
No. Observations:                1021   AIC:                            -4372.
Df Residuals:                     913   BIC:                            -3839.
Df Model:                         107                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9830      0.476     -8.375      0.000      -4.916      -3.050
LotArea                   0.2021      0.028      7.245      0.000       0.147       0.257
OverallQual               0.0826      0.011      7.186      0.000       0.060       0.105
OverallCond               0.0556      0.009      6.272      0.000       0.038       0.073
YearBuilt                 0.0749      0.011      6.939      0.000       0.054       0.096
YearRemodAdd              0.0157      0.004      3.697      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.596      0.000       0.025       0.061
BsmtFinSF1                0.1728      0.017      9.882      0.000       0.139       0.207
BsmtFinSF2                0.0290      0.009      3.287      0.001       0.012       0.046
BsmtUnfSF                 0.0246      0.008      3.144      0.002       0.009       0.040
TotalBsmtSF               0.1761      0.019      9.489      0.000       0.140       0.212
1stFlrSF                  0.1866      0.016     11.333      0.000       0.154       0.219
2ndFlrSF                  0.1277      0.008     15.910      0.000       0.112       0.143
LowQualFinSF              0.0091      0.013      0.710      0.478      -0.016       0.034
GrLivArea                 0.2038      0.013     16.126      0.000       0.179       0.229
BsmtFullBath              0.0115      0.007      1.607      0.108      -0.003       0.026
HalfBath                 -0.0136      0.005     -2.661      0.008      -0.024      -0.004
BedroomAbvGr             -0.0635      0.013     -4.907      0.000      -0.089      -0.038
KitchenAbvGr             -0.1157      0.015     -7.729      0.000      -0.145      -0.086
GarageYrBlt               0.0034      0.013      0.267      0.790      -0.022       0.028
GarageCars                0.0164      0.012      1.329      0.184      -0.008       0.041
GarageArea                0.0335      0.015      2.254      0.024       0.004       0.063
WoodDeckSF                0.0113      0.007      1.664      0.096      -0.002       0.025
EnclosedPorch             0.0090      0.009      0.975      0.330      -0.009       0.027
PoolArea                  5.9598      0.722      8.249      0.000       4.542       7.378
MiscVal                   0.1145      0.124      0.922      0.357      -0.129       0.358
MSZoning_FV               0.0242      0.014      1.678      0.094      -0.004       0.053
MSZoning_RH               0.0312      0.014      2.251      0.025       0.004       0.058
MSZoning_RL               0.0289      0.012      2.443      0.015       0.006       0.052
MSZoning_RM               0.0255      0.012      2.150      0.032       0.002       0.049
Street_Pave               0.0474      0.017      2.762      0.006       0.014       0.081
LandContour_Low        

In [47]:


X_tr_sm.pop('GarageYrBlt')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     150.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:18   Log-Likelihood:                 2293.8
No. Observations:                1021   AIC:                            -4374.
Df Residuals:                     914   BIC:                            -3846.
Df Model:                         106                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9807      0.475     -8.376      0.000      -4.913      -3.048
LotArea                   0.2020      0.028      7.245      0.000       0.147       0.257
OverallQual               0.0827      0.011      7.209      0.000       0.060       0.105
OverallCond               0.0558      0.009      6.310      0.000       0.038       0.073
YearBuilt                 0.0750      0.011      6.951      0.000       0.054       0.096
YearRemodAdd              0.0157      0.004      3.697      0.000       0.007       0.024
MasVnrArea                0.0427      0.009      4.590      0.000       0.024       0.061
BsmtFinSF1                0.1729      0.017      9.890      0.000       0.139       0.207
BsmtFinSF2                0.0290      0.009      3.291      0.001       0.012       0.046
BsmtUnfSF                 0.0246      0.008      3.138      0.002       0.009       0.040
TotalBsmtSF               0.1761      0.019      9.494      0.000       0.140       0.212
1stFlrSF                  0.1866      0.016     11.339      0.000       0.154       0.219
2ndFlrSF                  0.1278      0.008     15.968      0.000       0.112       0.144
LowQualFinSF              0.0089      0.013      0.696      0.486      -0.016       0.034
GrLivArea                 0.2039      0.013     16.138      0.000       0.179       0.229
BsmtFullBath              0.0114      0.007      1.598      0.110      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.693      0.007      -0.024      -0.004
BedroomAbvGr             -0.0637      0.013     -4.945      0.000      -0.089      -0.038
KitchenAbvGr             -0.1155      0.015     -7.730      0.000      -0.145      -0.086
GarageCars                0.0168      0.012      1.368      0.172      -0.007       0.041
GarageArea                0.0338      0.015      2.288      0.022       0.005       0.063
WoodDeckSF                0.0112      0.007      1.660      0.097      -0.002       0.025
EnclosedPorch             0.0089      0.009      0.972      0.331      -0.009       0.027
PoolArea                  5.9578      0.722      8.251      0.000       4.541       7.375
MiscVal                   0.1131      0.124      0.912      0.362      -0.130       0.356
MSZoning_FV               0.0243      0.014      1.686      0.092      -0.004       0.053
MSZoning_RH               0.0312      0.014      2.252      0.025       0.004       0.058
MSZoning_RL               0.0289      0.012      2.452      0.014       0.006       0.052
MSZoning_RM               0.0255      0.012      2.153      0.032       0.002       0.049
Street_Pave               0.0474      0.017      2.768      0.006       0.014       0.081
LandContour_Low          -0.0114      0.007     -1.756      0.079      -0.024       0.001
Utilities_NoSeWa       

In [48]:

X_tr_sm.pop('GarageCond_TA')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     151.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:19   Log-Likelihood:                 2293.7
No. Observations:                1021   AIC:                            -4375.
Df Residuals:                     915   BIC:                            -3853.
Df Model:                         105                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9826      0.475     -8.383      0.000      -4.915      -3.050
LotArea                   0.2018      0.028      7.242      0.000       0.147       0.256
OverallQual               0.0824      0.011      7.191      0.000       0.060       0.105
OverallCond               0.0552      0.009      6.287      0.000       0.038       0.072
YearBuilt                 0.0740      0.011      6.949      0.000       0.053       0.095
YearRemodAdd              0.0158      0.004      3.728      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.608      0.000       0.025       0.061
BsmtFinSF1                0.1732      0.017      9.920      0.000       0.139       0.208
BsmtFinSF2                0.0292      0.009      3.324      0.001       0.012       0.046
BsmtUnfSF                 0.0247      0.008      3.162      0.002       0.009       0.040
TotalBsmtSF               0.1765      0.019      9.530      0.000       0.140       0.213
1stFlrSF                  0.1859      0.016     11.330      0.000       0.154       0.218
2ndFlrSF                  0.1278      0.008     15.981      0.000       0.112       0.144
LowQualFinSF              0.0091      0.013      0.713      0.476      -0.016       0.034
GrLivArea                 0.2034      0.013     16.142      0.000       0.179       0.228
BsmtFullBath              0.0115      0.007      1.610      0.108      -0.003       0.026
HalfBath                 -0.0138      0.005     -2.709      0.007      -0.024      -0.004
BedroomAbvGr             -0.0631      0.013     -4.915      0.000      -0.088      -0.038
KitchenAbvGr             -0.1157      0.015     -7.746      0.000      -0.145      -0.086
GarageCars                0.0168      0.012      1.372      0.171      -0.007       0.041
GarageArea                0.0331      0.015      2.248      0.025       0.004       0.062
WoodDeckSF                0.0111      0.007      1.640      0.101      -0.002       0.024
EnclosedPorch             0.0088      0.009      0.957      0.339      -0.009       0.027
PoolArea                  5.9642      0.722      8.264      0.000       4.548       7.381
MiscVal                   0.1122      0.124      0.906      0.365      -0.131       0.355
MSZoning_FV               0.0245      0.014      1.700      0.089      -0.004       0.053
MSZoning_RH               0.0315      0.014      2.272      0.023       0.004       0.059
MSZoning_RL               0.0292      0.012      2.472      0.014       0.006       0.052
MSZoning_RM               0.0256      0.012      2.160      0.031       0.002       0.049
Street_Pave               0.0471      0.017      2.749      0.006       0.013       0.081
LandContour_Low          -0.0113      0.006     -1.742      0.082      -0.024       0.001
Utilities_NoSeWa       

In [49]:

X_tr_sm.pop('Exterior2nd_AsphShn')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     153.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:19   Log-Likelihood:                 2293.4
No. Observations:                1021   AIC:                            -4377.
Df Residuals:                     916   BIC:                            -3859.
Df Model:                         104                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9858      0.475     -8.393      0.000      -4.918      -3.054
LotArea                   0.2017      0.028      7.241      0.000       0.147       0.256
OverallQual               0.0820      0.011      7.173      0.000       0.060       0.104
OverallCond               0.0552      0.009      6.287      0.000       0.038       0.072
YearBuilt                 0.0737      0.011      6.928      0.000       0.053       0.095
YearRemodAdd              0.0159      0.004      3.755      0.000       0.008       0.024
MasVnrArea                0.0430      0.009      4.622      0.000       0.025       0.061
BsmtFinSF1                0.1743      0.017     10.038      0.000       0.140       0.208
BsmtFinSF2                0.0295      0.009      3.353      0.001       0.012       0.047
BsmtUnfSF                 0.0252      0.008      3.242      0.001       0.010       0.040
TotalBsmtSF               0.1778      0.018      9.660      0.000       0.142       0.214
1stFlrSF                  0.1847      0.016     11.342      0.000       0.153       0.217
2ndFlrSF                  0.1283      0.008     16.114      0.000       0.113       0.144
LowQualFinSF              0.0093      0.013      0.726      0.468      -0.016       0.034
GrLivArea                 0.2026      0.013     16.170      0.000       0.178       0.227
BsmtFullBath              0.0115      0.007      1.605      0.109      -0.003       0.025
HalfBath                 -0.0138      0.005     -2.719      0.007      -0.024      -0.004
BedroomAbvGr             -0.0634      0.013     -4.941      0.000      -0.089      -0.038
KitchenAbvGr             -0.1163      0.015     -7.815      0.000      -0.146      -0.087
GarageCars                0.0169      0.012      1.379      0.168      -0.007       0.041
GarageArea                0.0332      0.015      2.259      0.024       0.004       0.062
WoodDeckSF                0.0111      0.007      1.647      0.100      -0.002       0.024
EnclosedPorch             0.0088      0.009      0.959      0.338      -0.009       0.027
PoolArea                  5.9701      0.721      8.276      0.000       4.554       7.386
MiscVal                   0.1118      0.124      0.903      0.367      -0.131       0.355
MSZoning_FV               0.0247      0.014      1.711      0.087      -0.004       0.053
MSZoning_RH               0.0317      0.014      2.292      0.022       0.005       0.059
MSZoning_RL               0.0293      0.012      2.485      0.013       0.006       0.052
MSZoning_RM               0.0257      0.012      2.167      0.030       0.002       0.049
Street_Pave               0.0470      0.017      2.744      0.006       0.013       0.081
LandContour_Low          -0.0112      0.006     -1.731      0.084      -0.024       0.002
Utilities_NoSeWa       

In [50]:
X_tr_sm.pop('BsmtFinType1_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     153.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:19   Log-Likelihood:                 2293.4
No. Observations:                1021   AIC:                            -4377.
Df Residuals:                     916   BIC:                            -3859.
Df Model:                         104                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9858      0.475     -8.393      0.000      -4.918      -3.054
LotArea                   0.2017      0.028      7.241      0.000       0.147       0.256
OverallQual               0.0820      0.011      7.173      0.000       0.060       0.104
OverallCond               0.0552      0.009      6.287      0.000       0.038       0.072
YearBuilt                 0.0737      0.011      6.928      0.000       0.053       0.095
YearRemodAdd              0.0159      0.004      3.755      0.000       0.008       0.024
MasVnrArea                0.0430      0.009      4.622      0.000       0.025       0.061
BsmtFinSF1                0.1743      0.017     10.038      0.000       0.140       0.208
BsmtFinSF2                0.0295      0.009      3.353      0.001       0.012       0.047
BsmtUnfSF                 0.0252      0.008      3.242      0.001       0.010       0.040
TotalBsmtSF               0.1778      0.018      9.660      0.000       0.142       0.214
1stFlrSF                  0.1847      0.016     11.342      0.000       0.153       0.217
2ndFlrSF                  0.1283      0.008     16.114      0.000       0.113       0.144
LowQualFinSF              0.0093      0.013      0.726      0.468      -0.016       0.034
GrLivArea                 0.2026      0.013     16.170      0.000       0.178       0.227
BsmtFullBath              0.0115      0.007      1.605      0.109      -0.003       0.025
HalfBath                 -0.0138      0.005     -2.719      0.007      -0.024      -0.004
BedroomAbvGr             -0.0634      0.013     -4.941      0.000      -0.089      -0.038
KitchenAbvGr             -0.1163      0.015     -7.815      0.000      -0.146      -0.087
GarageCars                0.0169      0.012      1.379      0.168      -0.007       0.041
GarageArea                0.0332      0.015      2.259      0.024       0.004       0.062
WoodDeckSF                0.0111      0.007      1.647      0.100      -0.002       0.024
EnclosedPorch             0.0088      0.009      0.959      0.338      -0.009       0.027
PoolArea                  5.9701      0.721      8.276      0.000       4.554       7.386
MiscVal                   0.1118      0.124      0.903      0.367      -0.131       0.355
MSZoning_FV               0.0247      0.014      1.711      0.087      -0.004       0.053
MSZoning_RH               0.0317      0.014      2.292      0.022       0.005       0.059
MSZoning_RL               0.0293      0.012      2.485      0.013       0.006       0.052
MSZoning_RM               0.0257      0.012      2.167      0.030       0.002       0.049
Street_Pave               0.0470      0.017      2.744      0.006       0.013       0.081
LandContour_Low          -0.0112      0.006     -1.731      0.084      -0.024       0.002
Utilities_NoSeWa       

In [51]:
X_tr_sm.pop('BsmtCond_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     153.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:19   Log-Likelihood:                 2293.4
No. Observations:                1021   AIC:                            -4377.
Df Residuals:                     916   BIC:                            -3859.
Df Model:                         104                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9858      0.475     -8.393      0.000      -4.918      -3.054
LotArea                   0.2017      0.028      7.241      0.000       0.147       0.256
OverallQual               0.0820      0.011      7.173      0.000       0.060       0.104
OverallCond               0.0552      0.009      6.287      0.000       0.038       0.072
YearBuilt                 0.0737      0.011      6.928      0.000       0.053       0.095
YearRemodAdd              0.0159      0.004      3.755      0.000       0.008       0.024
MasVnrArea                0.0430      0.009      4.622      0.000       0.025       0.061
BsmtFinSF1                0.1743      0.017     10.038      0.000       0.140       0.208
BsmtFinSF2                0.0295      0.009      3.353      0.001       0.012       0.047
BsmtUnfSF                 0.0252      0.008      3.242      0.001       0.010       0.040
TotalBsmtSF               0.1778      0.018      9.660      0.000       0.142       0.214
1stFlrSF                  0.1847      0.016     11.342      0.000       0.153       0.217
2ndFlrSF                  0.1283      0.008     16.114      0.000       0.113       0.144
LowQualFinSF              0.0093      0.013      0.726      0.468      -0.016       0.034
GrLivArea                 0.2026      0.013     16.170      0.000       0.178       0.227
BsmtFullBath              0.0115      0.007      1.605      0.109      -0.003       0.025
HalfBath                 -0.0138      0.005     -2.719      0.007      -0.024      -0.004
BedroomAbvGr             -0.0634      0.013     -4.941      0.000      -0.089      -0.038
KitchenAbvGr             -0.1163      0.015     -7.815      0.000      -0.146      -0.087
GarageCars                0.0169      0.012      1.379      0.168      -0.007       0.041
GarageArea                0.0332      0.015      2.259      0.024       0.004       0.062
WoodDeckSF                0.0111      0.007      1.647      0.100      -0.002       0.024
EnclosedPorch             0.0088      0.009      0.959      0.338      -0.009       0.027
PoolArea                  5.9701      0.721      8.276      0.000       4.554       7.386
MiscVal                   0.1118      0.124      0.903      0.367      -0.131       0.355
MSZoning_FV               0.0247      0.014      1.711      0.087      -0.004       0.053
MSZoning_RH               0.0317      0.014      2.292      0.022       0.005       0.059
MSZoning_RL               0.0293      0.012      2.485      0.013       0.006       0.052
MSZoning_RM               0.0257      0.012      2.167      0.030       0.002       0.049
Street_Pave               0.0470      0.017      2.744      0.006       0.013       0.081
LandContour_Low          -0.0112      0.006     -1.731      0.084      -0.024       0.002
Utilities_NoSeWa       

In [52]:
X_tr_sm.pop('BsmtQual_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     154.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:20   Log-Likelihood:                 2293.3
No. Observations:                1021   AIC:                            -4379.
Df Residuals:                     917   BIC:                            -3866.
Df Model:                         103                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9848      0.475     -8.394      0.000      -4.916      -3.053
LotArea                   0.2019      0.028      7.250      0.000       0.147       0.257
OverallQual               0.0812      0.011      7.165      0.000       0.059       0.103
OverallCond               0.0552      0.009      6.286      0.000       0.038       0.072
YearBuilt                 0.0734      0.011      6.915      0.000       0.053       0.094
YearRemodAdd              0.0158      0.004      3.734      0.000       0.007       0.024
MasVnrArea                0.0431      0.009      4.642      0.000       0.025       0.061
BsmtFinSF1                0.1701      0.016     10.923      0.000       0.140       0.201
BsmtFinSF2                0.0287      0.009      3.308      0.001       0.012       0.046
BsmtUnfSF                 0.0235      0.007      3.297      0.001       0.010       0.037
TotalBsmtSF               0.1730      0.016     10.642      0.000       0.141       0.205
1stFlrSF                  0.1878      0.015     12.247      0.000       0.158       0.218
2ndFlrSF                  0.1271      0.008     16.590      0.000       0.112       0.142
LowQualFinSF              0.0091      0.013      0.710      0.478      -0.016       0.034
GrLivArea                 0.2046      0.012     17.063      0.000       0.181       0.228
BsmtFullBath              0.0112      0.007      1.572      0.116      -0.003       0.025
HalfBath                 -0.0139      0.005     -2.740      0.006      -0.024      -0.004
BedroomAbvGr             -0.0634      0.013     -4.943      0.000      -0.089      -0.038
KitchenAbvGr             -0.1149      0.015     -7.837      0.000      -0.144      -0.086
GarageCars                0.0168      0.012      1.367      0.172      -0.007       0.041
GarageArea                0.0333      0.015      2.263      0.024       0.004       0.062
WoodDeckSF                0.0109      0.007      1.618      0.106      -0.002       0.024
EnclosedPorch             0.0089      0.009      0.973      0.331      -0.009       0.027
PoolArea                  5.9670      0.721      8.275      0.000       4.552       7.382
MiscVal                   0.1157      0.124      0.936      0.349      -0.127       0.358
MSZoning_FV               0.0248      0.014      1.723      0.085      -0.003       0.053
MSZoning_RH               0.0318      0.014      2.299      0.022       0.005       0.059
MSZoning_RL               0.0296      0.012      2.515      0.012       0.007       0.053
MSZoning_RM               0.0257      0.012      2.177      0.030       0.003       0.049
Street_Pave               0.0469      0.017      2.739      0.006       0.013       0.080
LandContour_Low          -0.0110      0.006     -1.695      0.090      -0.024       0.002
Utilities_NoSeWa       

In [53]:
X_tr_sm.pop('Exterior1st_BrkComm')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     156.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:20   Log-Likelihood:                 2293.0
No. Observations:                1021   AIC:                            -4380.
Df Residuals:                     918   BIC:                            -3872.
Df Model:                         102                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9930      0.474     -8.416      0.000      -4.924      -3.062
LotArea                   0.2012      0.028      7.233      0.000       0.147       0.256
OverallQual               0.0813      0.011      7.179      0.000       0.059       0.104
OverallCond               0.0556      0.009      6.352      0.000       0.038       0.073
YearBuilt                 0.0737      0.011      6.951      0.000       0.053       0.095
YearRemodAdd              0.0157      0.004      3.725      0.000       0.007       0.024
MasVnrArea                0.0431      0.009      4.642      0.000       0.025       0.061
BsmtFinSF1                0.1698      0.016     10.914      0.000       0.139       0.200
BsmtFinSF2                0.0287      0.009      3.315      0.001       0.012       0.046
BsmtUnfSF                 0.0232      0.007      3.267      0.001       0.009       0.037
TotalBsmtSF               0.1727      0.016     10.631      0.000       0.141       0.205
1stFlrSF                  0.1882      0.015     12.290      0.000       0.158       0.218
2ndFlrSF                  0.1271      0.008     16.600      0.000       0.112       0.142
LowQualFinSF              0.0093      0.013      0.729      0.466      -0.016       0.034
GrLivArea                 0.2050      0.012     17.122      0.000       0.181       0.228
BsmtFullBath              0.0111      0.007      1.561      0.119      -0.003       0.025
HalfBath                 -0.0140      0.005     -2.758      0.006      -0.024      -0.004
BedroomAbvGr             -0.0634      0.013     -4.947      0.000      -0.089      -0.038
KitchenAbvGr             -0.1146      0.015     -7.822      0.000      -0.143      -0.086
GarageCars                0.0169      0.012      1.379      0.168      -0.007       0.041
GarageArea                0.0330      0.015      2.244      0.025       0.004       0.062
WoodDeckSF                0.0109      0.007      1.620      0.106      -0.002       0.024
EnclosedPorch             0.0092      0.009      0.999      0.318      -0.009       0.027
PoolArea                  5.9692      0.721      8.280      0.000       4.554       7.384
MiscVal                   0.1210      0.123      0.982      0.327      -0.121       0.363
MSZoning_FV               0.0247      0.014      1.717      0.086      -0.004       0.053
MSZoning_RH               0.0318      0.014      2.298      0.022       0.005       0.059
MSZoning_RL               0.0295      0.012      2.507      0.012       0.006       0.053
MSZoning_RM               0.0257      0.012      2.172      0.030       0.002       0.049
Street_Pave               0.0471      0.017      2.754      0.006       0.014       0.081
LandContour_Low          -0.0108      0.006     -1.663      0.097      -0.023       0.002
Utilities_NoSeWa       

In [54]:
X_tr_sm.pop('Condition2_RRAe')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     158.0
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:20   Log-Likelihood:                 2292.8
No. Observations:                1021   AIC:                            -4382.
Df Residuals:                     919   BIC:                            -3879.
Df Model:                         101                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0528      0.466     -8.690      0.000      -4.968      -3.138
LotArea                   0.1983      0.028      7.212      0.000       0.144       0.252
OverallQual               0.0813      0.011      7.176      0.000       0.059       0.103
OverallCond               0.0557      0.009      6.376      0.000       0.039       0.073
YearBuilt                 0.0740      0.011      6.984      0.000       0.053       0.095
YearRemodAdd              0.0156      0.004      3.693      0.000       0.007       0.024
MasVnrArea                0.0430      0.009      4.631      0.000       0.025       0.061
BsmtFinSF1                0.1694      0.016     10.898      0.000       0.139       0.200
BsmtFinSF2                0.0286      0.009      3.298      0.001       0.012       0.046
BsmtUnfSF                 0.0232      0.007      3.262      0.001       0.009       0.037
TotalBsmtSF               0.1722      0.016     10.614      0.000       0.140       0.204
1stFlrSF                  0.1886      0.015     12.331      0.000       0.159       0.219
2ndFlrSF                  0.1270      0.008     16.592      0.000       0.112       0.142
LowQualFinSF              0.0103      0.013      0.807      0.420      -0.015       0.035
GrLivArea                 0.2054      0.012     17.179      0.000       0.182       0.229
BsmtFullBath              0.0111      0.007      1.562      0.119      -0.003       0.025
HalfBath                 -0.0140      0.005     -2.760      0.006      -0.024      -0.004
BedroomAbvGr             -0.0640      0.013     -5.003      0.000      -0.089      -0.039
KitchenAbvGr             -0.1151      0.015     -7.862      0.000      -0.144      -0.086
GarageCars                0.0174      0.012      1.420      0.156      -0.007       0.041
GarageArea                0.0325      0.015      2.214      0.027       0.004       0.061
WoodDeckSF                0.0108      0.007      1.599      0.110      -0.002       0.024
EnclosedPorch             0.0091      0.009      0.990      0.323      -0.009       0.027
PoolArea                  5.9710      0.721      8.285      0.000       4.557       7.385
MiscVal                   0.1820      0.086      2.110      0.035       0.013       0.351
MSZoning_FV               0.0243      0.014      1.689      0.092      -0.004       0.053
MSZoning_RH               0.0316      0.014      2.282      0.023       0.004       0.059
MSZoning_RL               0.0291      0.012      2.475      0.014       0.006       0.052
MSZoning_RM               0.0252      0.012      2.136      0.033       0.002       0.048
Street_Pave               0.0458      0.017      2.696      0.007       0.012       0.079
LandContour_Low          -0.0103      0.006     -1.602      0.109      -0.023       0.002
Utilities_NoSeWa       

In [55]:
X_tr_sm.pop('GarageType_CarPort')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     159.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:21   Log-Likelihood:                 2292.5
No. Observations:                1021   AIC:                            -4383.
Df Residuals:                     920   BIC:                            -3885.
Df Model:                         100                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0517      0.466     -8.691      0.000      -4.967      -3.137
LotArea                   0.1976      0.027      7.192      0.000       0.144       0.251
OverallQual               0.0808      0.011      7.150      0.000       0.059       0.103
OverallCond               0.0558      0.009      6.383      0.000       0.039       0.073
YearBuilt                 0.0738      0.011      6.968      0.000       0.053       0.095
YearRemodAdd              0.0155      0.004      3.692      0.000       0.007       0.024
MasVnrArea                0.0430      0.009      4.631      0.000       0.025       0.061
BsmtFinSF1                0.1694      0.016     10.905      0.000       0.139       0.200
BsmtFinSF2                0.0289      0.009      3.341      0.001       0.012       0.046
BsmtUnfSF                 0.0233      0.007      3.275      0.001       0.009       0.037
TotalBsmtSF               0.1724      0.016     10.628      0.000       0.141       0.204
1stFlrSF                  0.1889      0.015     12.356      0.000       0.159       0.219
2ndFlrSF                  0.1270      0.008     16.599      0.000       0.112       0.142
LowQualFinSF              0.0102      0.013      0.800      0.424      -0.015       0.035
GrLivArea                 0.2056      0.012     17.207      0.000       0.182       0.229
BsmtFullBath              0.0113      0.007      1.588      0.113      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.710      0.007      -0.024      -0.004
BedroomAbvGr             -0.0649      0.013     -5.102      0.000      -0.090      -0.040
KitchenAbvGr             -0.1137      0.014     -7.846      0.000      -0.142      -0.085
GarageCars                0.0172      0.012      1.408      0.160      -0.007       0.041
GarageArea                0.0326      0.015      2.220      0.027       0.004       0.061
WoodDeckSF                0.0107      0.007      1.594      0.111      -0.002       0.024
EnclosedPorch             0.0090      0.009      0.981      0.327      -0.009       0.027
PoolArea                  5.9659      0.720      8.281      0.000       4.552       7.380
MiscVal                   0.1873      0.086      2.180      0.029       0.019       0.356
MSZoning_FV               0.0236      0.014      1.647      0.100      -0.005       0.052
MSZoning_RH               0.0308      0.014      2.237      0.026       0.004       0.058
MSZoning_RL               0.0285      0.012      2.430      0.015       0.005       0.051
MSZoning_RM               0.0245      0.012      2.084      0.037       0.001       0.048
Street_Pave               0.0442      0.017      2.627      0.009       0.011       0.077
LandContour_Low          -0.0099      0.006     -1.552      0.121      -0.023       0.003
Utilities_NoSeWa       

In [56]:
X_tr_sm.pop('RoofStyle_Gambrel')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.946
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     161.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:21   Log-Likelihood:                 2292.2
No. Observations:                1021   AIC:                            -4384.
Df Residuals:                     921   BIC:                            -3892.
Df Model:                          99                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0483      0.466     -8.686      0.000      -4.963      -3.134
LotArea                   0.1971      0.027      7.179      0.000       0.143       0.251
OverallQual               0.0803      0.011      7.123      0.000       0.058       0.102
OverallCond               0.0556      0.009      6.363      0.000       0.038       0.073
YearBuilt                 0.0737      0.011      6.961      0.000       0.053       0.094
YearRemodAdd              0.0157      0.004      3.743      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.623      0.000       0.025       0.061
BsmtFinSF1                0.1700      0.016     10.961      0.000       0.140       0.200
BsmtFinSF2                0.0290      0.009      3.356      0.001       0.012       0.046
BsmtUnfSF                 0.0235      0.007      3.305      0.001       0.010       0.037
TotalBsmtSF               0.1730      0.016     10.688      0.000       0.141       0.205
1stFlrSF                  0.1887      0.015     12.350      0.000       0.159       0.219
2ndFlrSF                  0.1273      0.008     16.680      0.000       0.112       0.142
LowQualFinSF              0.0101      0.013      0.794      0.427      -0.015       0.035
GrLivArea                 0.2056      0.012     17.212      0.000       0.182       0.229
BsmtFullBath              0.0112      0.007      1.582      0.114      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.721      0.007      -0.024      -0.004
BedroomAbvGr             -0.0648      0.013     -5.099      0.000      -0.090      -0.040
KitchenAbvGr             -0.1131      0.014     -7.822      0.000      -0.142      -0.085
GarageCars                0.0168      0.012      1.375      0.169      -0.007       0.041
GarageArea                0.0325      0.015      2.220      0.027       0.004       0.061
WoodDeckSF                0.0108      0.007      1.610      0.108      -0.002       0.024
EnclosedPorch             0.0090      0.009      0.986      0.324      -0.009       0.027
PoolArea                  5.9610      0.720      8.277      0.000       4.548       7.374
MiscVal                   0.1865      0.086      2.172      0.030       0.018       0.355
MSZoning_FV               0.0237      0.014      1.652      0.099      -0.004       0.052
MSZoning_RH               0.0307      0.014      2.230      0.026       0.004       0.058
MSZoning_RL               0.0285      0.012      2.436      0.015       0.006       0.051
MSZoning_RM               0.0246      0.012      2.095      0.036       0.002       0.048
Street_Pave               0.0440      0.017      2.620      0.009       0.011       0.077
LandContour_Low          -0.0099      0.006     -1.550      0.122      -0.022       0.003
Utilities_NoSeWa       

In [57]:
X_tr_sm.pop('Electrical_FuseP')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     163.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:21   Log-Likelihood:                 2291.9
No. Observations:                1021   AIC:                            -4386.
Df Residuals:                     922   BIC:                            -3898.
Df Model:                          98                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0530      0.466     -8.699      0.000      -4.967      -3.139
LotArea                   0.1971      0.027      7.180      0.000       0.143       0.251
OverallQual               0.0802      0.011      7.120      0.000       0.058       0.102
OverallCond               0.0555      0.009      6.359      0.000       0.038       0.073
YearBuilt                 0.0732      0.011      6.927      0.000       0.052       0.094
YearRemodAdd              0.0157      0.004      3.728      0.000       0.007       0.024
MasVnrArea                0.0428      0.009      4.618      0.000       0.025       0.061
BsmtFinSF1                0.1703      0.016     10.987      0.000       0.140       0.201
BsmtFinSF2                0.0290      0.009      3.354      0.001       0.012       0.046
BsmtUnfSF                 0.0236      0.007      3.324      0.001       0.010       0.038
TotalBsmtSF               0.1733      0.016     10.714      0.000       0.142       0.205
1stFlrSF                  0.1886      0.015     12.342      0.000       0.159       0.219
2ndFlrSF                  0.1274      0.008     16.692      0.000       0.112       0.142
LowQualFinSF              0.0101      0.013      0.795      0.427      -0.015       0.035
GrLivArea                 0.2055      0.012     17.207      0.000       0.182       0.229
BsmtFullBath              0.0114      0.007      1.600      0.110      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.708      0.007      -0.024      -0.004
BedroomAbvGr             -0.0642      0.013     -5.064      0.000      -0.089      -0.039
KitchenAbvGr             -0.1143      0.014     -7.955      0.000      -0.143      -0.086
GarageCars                0.0171      0.012      1.406      0.160      -0.007       0.041
GarageArea                0.0323      0.015      2.203      0.028       0.004       0.061
WoodDeckSF                0.0109      0.007      1.624      0.105      -0.002       0.024
EnclosedPorch             0.0093      0.009      1.018      0.309      -0.009       0.027
PoolArea                  5.9676      0.720      8.289      0.000       4.555       7.381
MiscVal                   0.1871      0.086      2.179      0.030       0.019       0.356
MSZoning_FV               0.0238      0.014      1.657      0.098      -0.004       0.052
MSZoning_RH               0.0309      0.014      2.240      0.025       0.004       0.058
MSZoning_RL               0.0286      0.012      2.445      0.015       0.006       0.052
MSZoning_RM               0.0245      0.012      2.084      0.037       0.001       0.048
Street_Pave               0.0442      0.017      2.628      0.009       0.011       0.077
LandContour_Low          -0.0100      0.006     -1.559      0.119      -0.023       0.003
Utilities_NoSeWa       

In [58]:
X_tr_sm.pop('Exterior2nd_CBlock')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     163.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:21   Log-Likelihood:                 2291.9
No. Observations:                1021   AIC:                            -4386.
Df Residuals:                     922   BIC:                            -3898.
Df Model:                          98                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0530      0.466     -8.699      0.000      -4.967      -3.139
LotArea                   0.1971      0.027      7.180      0.000       0.143       0.251
OverallQual               0.0802      0.011      7.120      0.000       0.058       0.102
OverallCond               0.0555      0.009      6.359      0.000       0.038       0.073
YearBuilt                 0.0732      0.011      6.927      0.000       0.052       0.094
YearRemodAdd              0.0157      0.004      3.728      0.000       0.007       0.024
MasVnrArea                0.0428      0.009      4.618      0.000       0.025       0.061
BsmtFinSF1                0.1703      0.016     10.987      0.000       0.140       0.201
BsmtFinSF2                0.0290      0.009      3.354      0.001       0.012       0.046
BsmtUnfSF                 0.0236      0.007      3.324      0.001       0.010       0.038
TotalBsmtSF               0.1733      0.016     10.714      0.000       0.142       0.205
1stFlrSF                  0.1886      0.015     12.342      0.000       0.159       0.219
2ndFlrSF                  0.1274      0.008     16.692      0.000       0.112       0.142
LowQualFinSF              0.0101      0.013      0.795      0.427      -0.015       0.035
GrLivArea                 0.2055      0.012     17.207      0.000       0.182       0.229
BsmtFullBath              0.0114      0.007      1.600      0.110      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.708      0.007      -0.024      -0.004
BedroomAbvGr             -0.0642      0.013     -5.064      0.000      -0.089      -0.039
KitchenAbvGr             -0.1143      0.014     -7.955      0.000      -0.143      -0.086
GarageCars                0.0171      0.012      1.406      0.160      -0.007       0.041
GarageArea                0.0323      0.015      2.203      0.028       0.004       0.061
WoodDeckSF                0.0109      0.007      1.624      0.105      -0.002       0.024
EnclosedPorch             0.0093      0.009      1.018      0.309      -0.009       0.027
PoolArea                  5.9676      0.720      8.289      0.000       4.555       7.381
MiscVal                   0.1871      0.086      2.179      0.030       0.019       0.356
MSZoning_FV               0.0238      0.014      1.657      0.098      -0.004       0.052
MSZoning_RH               0.0309      0.014      2.240      0.025       0.004       0.058
MSZoning_RL               0.0286      0.012      2.445      0.015       0.006       0.052
MSZoning_RM               0.0245      0.012      2.084      0.037       0.001       0.048
Street_Pave               0.0442      0.017      2.628      0.009       0.011       0.077
LandContour_Low          -0.0100      0.006     -1.559      0.119      -0.023       0.003
Utilities_NoSeWa       

In [59]:
X_tr_sm.pop('Exterior1st_CBlock')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     164.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:22   Log-Likelihood:                 2291.6
No. Observations:                1021   AIC:                            -4387.
Df Residuals:                     923   BIC:                            -3904.
Df Model:                          97                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0529      0.466     -8.701      0.000      -4.967      -3.139
LotArea                   0.1969      0.027      7.175      0.000       0.143       0.251
OverallQual               0.0805      0.011      7.149      0.000       0.058       0.103
OverallCond               0.0555      0.009      6.361      0.000       0.038       0.073
YearBuilt                 0.0734      0.011      6.958      0.000       0.053       0.094
YearRemodAdd              0.0157      0.004      3.743      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.630      0.000       0.025       0.061
BsmtFinSF1                0.1701      0.015     10.976      0.000       0.140       0.200
BsmtFinSF2                0.0291      0.009      3.366      0.001       0.012       0.046
BsmtUnfSF                 0.0235      0.007      3.310      0.001       0.010       0.037
TotalBsmtSF               0.1731      0.016     10.703      0.000       0.141       0.205
1stFlrSF                  0.1884      0.015     12.339      0.000       0.158       0.218
2ndFlrSF                  0.1270      0.008     16.689      0.000       0.112       0.142
LowQualFinSF              0.0109      0.013      0.857      0.392      -0.014       0.036
GrLivArea                 0.2053      0.012     17.201      0.000       0.182       0.229
BsmtFullBath              0.0114      0.007      1.607      0.109      -0.003       0.025
HalfBath                 -0.0135      0.005     -2.686      0.007      -0.023      -0.004
BedroomAbvGr             -0.0636      0.013     -5.027      0.000      -0.088      -0.039
KitchenAbvGr             -0.1141      0.014     -7.943      0.000      -0.142      -0.086
GarageCars                0.0174      0.012      1.424      0.155      -0.007       0.041
GarageArea                0.0321      0.015      2.193      0.029       0.003       0.061
WoodDeckSF                0.0110      0.007      1.634      0.103      -0.002       0.024
EnclosedPorch             0.0089      0.009      0.977      0.329      -0.009       0.027
PoolArea                  5.9664      0.720      8.289      0.000       4.554       7.379
MiscVal                   0.1919      0.086      2.243      0.025       0.024       0.360
MSZoning_FV               0.0226      0.014      1.588      0.113      -0.005       0.051
MSZoning_RH               0.0299      0.014      2.184      0.029       0.003       0.057
MSZoning_RL               0.0274      0.012      2.369      0.018       0.005       0.050
MSZoning_RM               0.0234      0.012      2.011      0.045       0.001       0.046
Street_Pave               0.0418      0.016      2.540      0.011       0.009       0.074
LandContour_Low          -0.0099      0.006     -1.553      0.121      -0.023       0.003
Utilities_NoSeWa       

In [60]:
X_tr_sm.pop('ExterQual_Fa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     166.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:22   Log-Likelihood:                 2291.4
No. Observations:                1021   AIC:                            -4389.
Df Residuals:                     924   BIC:                            -3911.
Df Model:                          96                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0663      0.465     -8.743      0.000      -4.979      -3.154
LotArea                   0.1960      0.027      7.155      0.000       0.142       0.250
OverallQual               0.0803      0.011      7.135      0.000       0.058       0.102
OverallCond               0.0555      0.009      6.363      0.000       0.038       0.073
YearBuilt                 0.0734      0.011      6.962      0.000       0.053       0.094
YearRemodAdd              0.0157      0.004      3.741      0.000       0.007       0.024
MasVnrArea                0.0430      0.009      4.637      0.000       0.025       0.061
BsmtFinSF1                0.1705      0.015     11.022      0.000       0.140       0.201
BsmtFinSF2                0.0295      0.009      3.423      0.001       0.013       0.046
BsmtUnfSF                 0.0235      0.007      3.316      0.001       0.010       0.037
TotalBsmtSF               0.1736      0.016     10.755      0.000       0.142       0.205
1stFlrSF                  0.1882      0.015     12.331      0.000       0.158       0.218
2ndFlrSF                  0.1272      0.008     16.724      0.000       0.112       0.142
LowQualFinSF              0.0120      0.013      0.958      0.338      -0.013       0.037
GrLivArea                 0.2053      0.012     17.204      0.000       0.182       0.229
BsmtFullBath              0.0111      0.007      1.570      0.117      -0.003       0.025
HalfBath                 -0.0136      0.005     -2.697      0.007      -0.023      -0.004
BedroomAbvGr             -0.0638      0.013     -5.048      0.000      -0.089      -0.039
KitchenAbvGr             -0.1139      0.014     -7.935      0.000      -0.142      -0.086
GarageCars                0.0174      0.012      1.428      0.154      -0.007       0.041
GarageArea                0.0320      0.015      2.187      0.029       0.003       0.061
WoodDeckSF                0.0110      0.007      1.633      0.103      -0.002       0.024
EnclosedPorch             0.0092      0.009      1.011      0.312      -0.009       0.027
PoolArea                  5.9847      0.719      8.325      0.000       4.574       7.396
MiscVal                   0.1997      0.085      2.363      0.018       0.034       0.366
MSZoning_FV               0.0214      0.014      1.517      0.130      -0.006       0.049
MSZoning_RH               0.0289      0.014      2.126      0.034       0.002       0.056
MSZoning_RL               0.0261      0.011      2.298      0.022       0.004       0.048
MSZoning_RM               0.0221      0.011      1.933      0.054      -0.000       0.044
Street_Pave               0.0379      0.015      2.506      0.012       0.008       0.068
LandContour_Low          -0.0099      0.006     -1.541      0.124      -0.022       0.003
Utilities_NoSeWa       

In [61]:
X_tr_sm.pop('Electrical_Mix')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     166.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:22   Log-Likelihood:                 2291.4
No. Observations:                1021   AIC:                            -4389.
Df Residuals:                     924   BIC:                            -3911.
Df Model:                          96                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0663      0.465     -8.743      0.000      -4.979      -3.154
LotArea                   0.1960      0.027      7.155      0.000       0.142       0.250
OverallQual               0.0803      0.011      7.135      0.000       0.058       0.102
OverallCond               0.0555      0.009      6.363      0.000       0.038       0.073
YearBuilt                 0.0734      0.011      6.962      0.000       0.053       0.094
YearRemodAdd              0.0157      0.004      3.741      0.000       0.007       0.024
MasVnrArea                0.0430      0.009      4.637      0.000       0.025       0.061
BsmtFinSF1                0.1705      0.015     11.022      0.000       0.140       0.201
BsmtFinSF2                0.0295      0.009      3.423      0.001       0.013       0.046
BsmtUnfSF                 0.0235      0.007      3.316      0.001       0.010       0.037
TotalBsmtSF               0.1736      0.016     10.755      0.000       0.142       0.205
1stFlrSF                  0.1882      0.015     12.331      0.000       0.158       0.218
2ndFlrSF                  0.1272      0.008     16.724      0.000       0.112       0.142
LowQualFinSF              0.0120      0.013      0.958      0.338      -0.013       0.037
GrLivArea                 0.2053      0.012     17.204      0.000       0.182       0.229
BsmtFullBath              0.0111      0.007      1.570      0.117      -0.003       0.025
HalfBath                 -0.0136      0.005     -2.697      0.007      -0.023      -0.004
BedroomAbvGr             -0.0638      0.013     -5.048      0.000      -0.089      -0.039
KitchenAbvGr             -0.1139      0.014     -7.935      0.000      -0.142      -0.086
GarageCars                0.0174      0.012      1.428      0.154      -0.007       0.041
GarageArea                0.0320      0.015      2.187      0.029       0.003       0.061
WoodDeckSF                0.0110      0.007      1.633      0.103      -0.002       0.024
EnclosedPorch             0.0092      0.009      1.011      0.312      -0.009       0.027
PoolArea                  5.9847      0.719      8.325      0.000       4.574       7.396
MiscVal                   0.1997      0.085      2.363      0.018       0.034       0.366
MSZoning_FV               0.0214      0.014      1.517      0.130      -0.006       0.049
MSZoning_RH               0.0289      0.014      2.126      0.034       0.002       0.056
MSZoning_RL               0.0261      0.011      2.298      0.022       0.004       0.048
MSZoning_RM               0.0221      0.011      1.933      0.054      -0.000       0.044
Street_Pave               0.0379      0.015      2.506      0.012       0.008       0.068
LandContour_Low          -0.0099      0.006     -1.541      0.124      -0.022       0.003
Utilities_NoSeWa       

In [62]:
X_tr_sm.pop('LowQualFinSF')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     166.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:22   Log-Likelihood:                 2291.4
No. Observations:                1021   AIC:                            -4389.
Df Residuals:                     924   BIC:                            -3911.
Df Model:                          96                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0663      0.465     -8.743      0.000      -4.979      -3.154
LotArea                   0.1960      0.027      7.155      0.000       0.142       0.250
OverallQual               0.0803      0.011      7.135      0.000       0.058       0.102
OverallCond               0.0555      0.009      6.363      0.000       0.038       0.073
YearBuilt                 0.0734      0.011      6.962      0.000       0.053       0.094
YearRemodAdd              0.0157      0.004      3.741      0.000       0.007       0.024
MasVnrArea                0.0430      0.009      4.637      0.000       0.025       0.061
BsmtFinSF1                0.1705      0.015     11.022      0.000       0.140       0.201
BsmtFinSF2                0.0295      0.009      3.423      0.001       0.013       0.046
BsmtUnfSF                 0.0235      0.007      3.316      0.001       0.010       0.037
TotalBsmtSF               0.1736      0.016     10.755      0.000       0.142       0.205
1stFlrSF                  0.0968      0.098      0.990      0.323      -0.095       0.289
2ndFlrSF                  0.0839      0.046      1.835      0.067      -0.006       0.174
GrLivArea                 0.3166      0.117      2.700      0.007       0.086       0.547
BsmtFullBath              0.0111      0.007      1.570      0.117      -0.003       0.025
HalfBath                 -0.0136      0.005     -2.697      0.007      -0.023      -0.004
BedroomAbvGr             -0.0638      0.013     -5.048      0.000      -0.089      -0.039
KitchenAbvGr             -0.1139      0.014     -7.935      0.000      -0.142      -0.086
GarageCars                0.0174      0.012      1.428      0.154      -0.007       0.041
GarageArea                0.0320      0.015      2.187      0.029       0.003       0.061
WoodDeckSF                0.0110      0.007      1.633      0.103      -0.002       0.024
EnclosedPorch             0.0092      0.009      1.011      0.312      -0.009       0.027
PoolArea                  5.9847      0.719      8.325      0.000       4.574       7.396
MiscVal                   0.1997      0.085      2.363      0.018       0.034       0.366
MSZoning_FV               0.0214      0.014      1.517      0.130      -0.006       0.049
MSZoning_RH               0.0289      0.014      2.126      0.034       0.002       0.056
MSZoning_RL               0.0261      0.011      2.298      0.022       0.004       0.048
MSZoning_RM               0.0221      0.011      1.933      0.054      -0.000       0.044
Street_Pave               0.0379      0.015      2.506      0.012       0.008       0.068
LandContour_Low          -0.0099      0.006     -1.541      0.124      -0.022       0.003
Utilities_NoSeWa         -0.0345      0.028     -1.242      0.214      -0.089       0.020
LotConfig_CulDSac      

In [63]:
X_tr_sm.pop('Foundation_Stone')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     168.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:23   Log-Likelihood:                 2290.9
No. Observations:                1021   AIC:                            -4390.
Df Residuals:                     925   BIC:                            -3917.
Df Model:                          95                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0919      0.464     -8.812      0.000      -5.003      -3.181
LotArea                   0.1965      0.027      7.176      0.000       0.143       0.250
OverallQual               0.0804      0.011      7.150      0.000       0.058       0.103
OverallCond               0.0558      0.009      6.403      0.000       0.039       0.073
YearBuilt                 0.0730      0.011      6.927      0.000       0.052       0.094
YearRemodAdd              0.0158      0.004      3.759      0.000       0.008       0.024
MasVnrArea                0.0427      0.009      4.611      0.000       0.025       0.061
BsmtFinSF1                0.1701      0.015     10.999      0.000       0.140       0.200
BsmtFinSF2                0.0293      0.009      3.400      0.001       0.012       0.046
BsmtUnfSF                 0.0232      0.007      3.279      0.001       0.009       0.037
TotalBsmtSF               0.1731      0.016     10.728      0.000       0.141       0.205
1stFlrSF                  0.0963      0.098      0.985      0.325      -0.096       0.288
2ndFlrSF                  0.0833      0.046      1.822      0.069      -0.006       0.173
GrLivArea                 0.3182      0.117      2.714      0.007       0.088       0.548
BsmtFullBath              0.0111      0.007      1.564      0.118      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.721      0.007      -0.024      -0.004
BedroomAbvGr             -0.0636      0.013     -5.037      0.000      -0.088      -0.039
KitchenAbvGr             -0.1138      0.014     -7.926      0.000      -0.142      -0.086
GarageCars                0.0185      0.012      1.528      0.127      -0.005       0.042
GarageArea                0.0315      0.015      2.155      0.031       0.003       0.060
WoodDeckSF                0.0112      0.007      1.660      0.097      -0.002       0.024
EnclosedPorch             0.0104      0.009      1.152      0.249      -0.007       0.028
PoolArea                  6.0155      0.718      8.376      0.000       4.606       7.425
MiscVal                   0.2047      0.084      2.426      0.015       0.039       0.370
MSZoning_FV               0.0215      0.014      1.529      0.127      -0.006       0.049
MSZoning_RH               0.0290      0.014      2.133      0.033       0.002       0.056
MSZoning_RL               0.0263      0.011      2.314      0.021       0.004       0.049
MSZoning_RM               0.0223      0.011      1.954      0.051    -9.6e-05       0.045
Street_Pave               0.0378      0.015      2.496      0.013       0.008       0.068
LandContour_Low          -0.0101      0.006     -1.584      0.113      -0.023       0.002
Utilities_NoSeWa         -0.0348      0.028     -1.256      0.210      -0.089       0.020
LotConfig_CulDSac      

In [64]:
X_tr_sm.pop('Electrical_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     168.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:23   Log-Likelihood:                 2290.9
No. Observations:                1021   AIC:                            -4390.
Df Residuals:                     925   BIC:                            -3917.
Df Model:                          95                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0919      0.464     -8.812      0.000      -5.003      -3.181
LotArea                   0.1965      0.027      7.176      0.000       0.143       0.250
OverallQual               0.0804      0.011      7.150      0.000       0.058       0.103
OverallCond               0.0558      0.009      6.403      0.000       0.039       0.073
YearBuilt                 0.0730      0.011      6.927      0.000       0.052       0.094
YearRemodAdd              0.0158      0.004      3.759      0.000       0.008       0.024
MasVnrArea                0.0427      0.009      4.611      0.000       0.025       0.061
BsmtFinSF1                0.1701      0.015     10.999      0.000       0.140       0.200
BsmtFinSF2                0.0293      0.009      3.400      0.001       0.012       0.046
BsmtUnfSF                 0.0232      0.007      3.279      0.001       0.009       0.037
TotalBsmtSF               0.1731      0.016     10.728      0.000       0.141       0.205
1stFlrSF                  0.0963      0.098      0.985      0.325      -0.096       0.288
2ndFlrSF                  0.0833      0.046      1.822      0.069      -0.006       0.173
GrLivArea                 0.3182      0.117      2.714      0.007       0.088       0.548
BsmtFullBath              0.0111      0.007      1.564      0.118      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.721      0.007      -0.024      -0.004
BedroomAbvGr             -0.0636      0.013     -5.037      0.000      -0.088      -0.039
KitchenAbvGr             -0.1138      0.014     -7.926      0.000      -0.142      -0.086
GarageCars                0.0185      0.012      1.528      0.127      -0.005       0.042
GarageArea                0.0315      0.015      2.155      0.031       0.003       0.060
WoodDeckSF                0.0112      0.007      1.660      0.097      -0.002       0.024
EnclosedPorch             0.0104      0.009      1.152      0.249      -0.007       0.028
PoolArea                  6.0155      0.718      8.376      0.000       4.606       7.425
MiscVal                   0.2047      0.084      2.426      0.015       0.039       0.370
MSZoning_FV               0.0215      0.014      1.529      0.127      -0.006       0.049
MSZoning_RH               0.0290      0.014      2.133      0.033       0.002       0.056
MSZoning_RL               0.0263      0.011      2.314      0.021       0.004       0.049
MSZoning_RM               0.0223      0.011      1.954      0.051    -9.6e-05       0.045
Street_Pave               0.0378      0.015      2.496      0.013       0.008       0.068
LandContour_Low          -0.0101      0.006     -1.584      0.113      -0.023       0.002
Utilities_NoSeWa         -0.0348      0.028     -1.256      0.210      -0.089       0.020
LotConfig_CulDSac      

In [65]:
X_tr_sm.pop('1stFlrSF')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     170.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:23   Log-Likelihood:                 2290.4
No. Observations:                1021   AIC:                            -4391.
Df Residuals:                     926   BIC:                            -3923.
Df Model:                          94                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.1974      0.452     -9.290      0.000      -5.084      -3.311
LotArea                   0.1970      0.027      7.196      0.000       0.143       0.251
OverallQual               0.0806      0.011      7.162      0.000       0.058       0.103
OverallCond               0.0562      0.009      6.457      0.000       0.039       0.073
YearBuilt                 0.0730      0.011      6.930      0.000       0.052       0.094
YearRemodAdd              0.0158      0.004      3.765      0.000       0.008       0.024
MasVnrArea                0.0430      0.009      4.647      0.000       0.025       0.061
BsmtFinSF1                0.1722      0.015     11.249      0.000       0.142       0.202
BsmtFinSF2                0.0294      0.009      3.421      0.001       0.013       0.046
BsmtUnfSF                 0.0239      0.007      3.383      0.001       0.010       0.038
TotalBsmtSF               0.1753      0.016     10.980      0.000       0.144       0.207
2ndFlrSF                  0.0398      0.012      3.376      0.001       0.017       0.063
GrLivArea                 0.4299      0.030     14.468      0.000       0.372       0.488
BsmtFullBath              0.0110      0.007      1.553      0.121      -0.003       0.025
HalfBath                 -0.0137      0.005     -2.725      0.007      -0.024      -0.004
BedroomAbvGr             -0.0638      0.013     -5.048      0.000      -0.089      -0.039
KitchenAbvGr             -0.1126      0.014     -7.870      0.000      -0.141      -0.084
GarageCars                0.0183      0.012      1.511      0.131      -0.005       0.042
GarageArea                0.0323      0.015      2.212      0.027       0.004       0.061
WoodDeckSF                0.0114      0.007      1.695      0.090      -0.002       0.025
EnclosedPorch             0.0106      0.009      1.174      0.241      -0.007       0.028
PoolArea                  6.1663      0.702      8.788      0.000       4.789       7.543
MiscVal                   0.2101      0.084      2.496      0.013       0.045       0.375
MSZoning_FV               0.0227      0.014      1.621      0.105      -0.005       0.050
MSZoning_RH               0.0303      0.014      2.237      0.026       0.004       0.057
MSZoning_RL               0.0277      0.011      2.461      0.014       0.006       0.050
MSZoning_RM               0.0236      0.011      2.079      0.038       0.001       0.046
Street_Pave               0.0369      0.015      2.443      0.015       0.007       0.067
LandContour_Low          -0.0102      0.006     -1.589      0.112      -0.023       0.002
Utilities_NoSeWa         -0.0345      0.028     -1.243      0.214      -0.089       0.020
LotConfig_CulDSac         0.0112      0.004      2.928      0.003       0.004       0.019
LandSlope_Sev          

In [66]:
X_tr_sm.pop('HouseStyle_2.5Unf')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     172.0
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:23   Log-Likelihood:                 2289.7
No. Observations:                1021   AIC:                            -4391.
Df Residuals:                     927   BIC:                            -3928.
Df Model:                          93                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.1983      0.452     -9.291      0.000      -5.085      -3.311
LotArea                   0.1970      0.027      7.196      0.000       0.143       0.251
OverallQual               0.0791      0.011      7.080      0.000       0.057       0.101
OverallCond               0.0566      0.009      6.508      0.000       0.040       0.074
YearBuilt                 0.0742      0.010      7.077      0.000       0.054       0.095
YearRemodAdd              0.0154      0.004      3.688      0.000       0.007       0.024
MasVnrArea                0.0435      0.009      4.707      0.000       0.025       0.062
BsmtFinSF1                0.1708      0.015     11.194      0.000       0.141       0.201
BsmtFinSF2                0.0293      0.009      3.403      0.001       0.012       0.046
BsmtUnfSF                 0.0237      0.007      3.361      0.001       0.010       0.038
TotalBsmtSF               0.1739      0.016     10.925      0.000       0.143       0.205
2ndFlrSF                  0.0384      0.012      3.276      0.001       0.015       0.061
GrLivArea                 0.4310      0.030     14.511      0.000       0.373       0.489
BsmtFullBath              0.0114      0.007      1.604      0.109      -0.003       0.025
HalfBath                 -0.0133      0.005     -2.647      0.008      -0.023      -0.003
BedroomAbvGr             -0.0628      0.013     -4.982      0.000      -0.088      -0.038
KitchenAbvGr             -0.1148      0.014     -8.109      0.000      -0.143      -0.087
GarageCars                0.0180      0.012      1.485      0.138      -0.006       0.042
GarageArea                0.0333      0.015      2.282      0.023       0.005       0.062
WoodDeckSF                0.0116      0.007      1.722      0.085      -0.002       0.025
EnclosedPorch             0.0106      0.009      1.169      0.243      -0.007       0.028
PoolArea                  6.1677      0.702      8.789      0.000       4.790       7.545
MiscVal                   0.2120      0.084      2.519      0.012       0.047       0.377
MSZoning_FV               0.0243      0.014      1.742      0.082      -0.003       0.052
MSZoning_RH               0.0321      0.013      2.385      0.017       0.006       0.058
MSZoning_RL               0.0291      0.011      2.603      0.009       0.007       0.051
MSZoning_RM               0.0247      0.011      2.190      0.029       0.003       0.047
Street_Pave               0.0367      0.015      2.428      0.015       0.007       0.066
LandContour_Low          -0.0101      0.006     -1.575      0.116      -0.023       0.002
Utilities_NoSeWa         -0.0348      0.028     -1.254      0.210      -0.089       0.020
LotConfig_CulDSac         0.0112      0.004      2.922      0.004       0.004       0.019
LandSlope_Sev          

In [67]:
X_tr_sm.pop('Exterior1st_Stone')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     173.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:24   Log-Likelihood:                 2289.0
No. Observations:                1021   AIC:                            -4392.
Df Residuals:                     928   BIC:                            -3934.
Df Model:                          92                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.1915      0.452     -9.275      0.000      -5.078      -3.305
LotArea                   0.1959      0.027      7.159      0.000       0.142       0.250
OverallQual               0.0796      0.011      7.125      0.000       0.058       0.101
OverallCond               0.0567      0.009      6.510      0.000       0.040       0.074
YearBuilt                 0.0736      0.010      7.028      0.000       0.053       0.094
YearRemodAdd              0.0154      0.004      3.677      0.000       0.007       0.024
MasVnrArea                0.0439      0.009      4.752      0.000       0.026       0.062
BsmtFinSF1                0.1718      0.015     11.276      0.000       0.142       0.202
BsmtFinSF2                0.0285      0.009      3.324      0.001       0.012       0.045
BsmtUnfSF                 0.0247      0.007      3.526      0.000       0.011       0.038
TotalBsmtSF               0.1750      0.016     11.013      0.000       0.144       0.206
2ndFlrSF                  0.0401      0.012      3.445      0.001       0.017       0.063
GrLivArea                 0.4261      0.029     14.512      0.000       0.368       0.484
BsmtFullBath              0.0119      0.007      1.689      0.092      -0.002       0.026
HalfBath                 -0.0133      0.005     -2.638      0.008      -0.023      -0.003
BedroomAbvGr             -0.0618      0.013     -4.914      0.000      -0.086      -0.037
KitchenAbvGr             -0.1151      0.014     -8.133      0.000      -0.143      -0.087
GarageCars                0.0174      0.012      1.439      0.151      -0.006       0.041
GarageArea                0.0339      0.015      2.328      0.020       0.005       0.063
WoodDeckSF                0.0118      0.007      1.757      0.079      -0.001       0.025
EnclosedPorch             0.0089      0.009      0.996      0.319      -0.009       0.026
PoolArea                  6.1425      0.701      8.757      0.000       4.766       7.519
MiscVal                   0.2213      0.084      2.642      0.008       0.057       0.386
MSZoning_FV               0.0239      0.014      1.715      0.087      -0.003       0.051
MSZoning_RH               0.0320      0.013      2.378      0.018       0.006       0.058
MSZoning_RL               0.0289      0.011      2.579      0.010       0.007       0.051
MSZoning_RM               0.0244      0.011      2.160      0.031       0.002       0.047
Street_Pave               0.0368      0.015      2.432      0.015       0.007       0.066
LandContour_Low          -0.0101      0.006     -1.577      0.115      -0.023       0.002
Utilities_NoSeWa         -0.0343      0.028     -1.236      0.217      -0.089       0.020
LotConfig_CulDSac         0.0113      0.004      2.935      0.003       0.004       0.019
LandSlope_Sev          

In [68]:
X_tr_sm.pop('EnclosedPorch')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     175.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:24   Log-Likelihood:                 2288.5
No. Observations:                1021   AIC:                            -4393.
Df Residuals:                     929   BIC:                            -3940.
Df Model:                          91                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0970      0.442     -9.273      0.000      -4.964      -3.230
LotArea                   0.1944      0.027      7.116      0.000       0.141       0.248
OverallQual               0.0803      0.011      7.203      0.000       0.058       0.102
OverallCond               0.0558      0.009      6.444      0.000       0.039       0.073
YearBuilt                 0.0709      0.010      7.014      0.000       0.051       0.091
YearRemodAdd              0.0155      0.004      3.703      0.000       0.007       0.024
MasVnrArea                0.0438      0.009      4.738      0.000       0.026       0.062
BsmtFinSF1                0.1714      0.015     11.253      0.000       0.141       0.201
BsmtFinSF2                0.0289      0.009      3.366      0.001       0.012       0.046
BsmtUnfSF                 0.0249      0.007      3.564      0.000       0.011       0.039
TotalBsmtSF               0.1748      0.016     11.001      0.000       0.144       0.206
2ndFlrSF                  0.0402      0.012      3.461      0.001       0.017       0.063
GrLivArea                 0.4260      0.029     14.511      0.000       0.368       0.484
BsmtFullBath              0.0124      0.007      1.767      0.078      -0.001       0.026
HalfBath                 -0.0134      0.005     -2.665      0.008      -0.023      -0.004
BedroomAbvGr             -0.0616      0.013     -4.899      0.000      -0.086      -0.037
KitchenAbvGr             -0.1164      0.014     -8.249      0.000      -0.144      -0.089
GarageCars                0.0171      0.012      1.412      0.158      -0.007       0.041
GarageArea                0.0346      0.015      2.378      0.018       0.006       0.063
WoodDeckSF                0.0113      0.007      1.690      0.091      -0.002       0.024
PoolArea                  6.0101      0.689      8.726      0.000       4.658       7.362
MiscVal                   0.2149      0.084      2.573      0.010       0.051       0.379
MSZoning_FV               0.0237      0.014      1.699      0.090      -0.004       0.051
MSZoning_RH               0.0323      0.013      2.406      0.016       0.006       0.059
MSZoning_RL               0.0286      0.011      2.556      0.011       0.007       0.051
MSZoning_RM               0.0244      0.011      2.159      0.031       0.002       0.047
Street_Pave               0.0371      0.015      2.455      0.014       0.007       0.067
LandContour_Low          -0.0099      0.006     -1.554      0.121      -0.022       0.003
Utilities_NoSeWa         -0.0349      0.028     -1.260      0.208      -0.089       0.019
LotConfig_CulDSac         0.0112      0.004      2.933      0.003       0.004       0.019
LandSlope_Sev            -0.0471      0.015     -3.189      0.001      -0.076      -0.018
Neighborhood_BrkSide   

In [69]:
X_tr_sm.pop('SaleCondition_AdjLand')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     177.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:24   Log-Likelihood:                 2287.6
No. Observations:                1021   AIC:                            -4393.
Df Residuals:                     930   BIC:                            -3945.
Df Model:                          90                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0947      0.442     -9.265      0.000      -4.962      -3.227
LotArea                   0.1942      0.027      7.105      0.000       0.141       0.248
OverallQual               0.0806      0.011      7.234      0.000       0.059       0.102
OverallCond               0.0550      0.009      6.369      0.000       0.038       0.072
YearBuilt                 0.0701      0.010      6.947      0.000       0.050       0.090
YearRemodAdd              0.0156      0.004      3.731      0.000       0.007       0.024
MasVnrArea                0.0438      0.009      4.742      0.000       0.026       0.062
BsmtFinSF1                0.1702      0.015     11.194      0.000       0.140       0.200
BsmtFinSF2                0.0285      0.009      3.331      0.001       0.012       0.045
BsmtUnfSF                 0.0246      0.007      3.519      0.000       0.011       0.038
TotalBsmtSF               0.1735      0.016     10.941      0.000       0.142       0.205
2ndFlrSF                  0.0397      0.012      3.418      0.001       0.017       0.063
GrLivArea                 0.4261      0.029     14.509      0.000       0.368       0.484
BsmtFullBath              0.0126      0.007      1.790      0.074      -0.001       0.026
HalfBath                 -0.0132      0.005     -2.638      0.008      -0.023      -0.003
BedroomAbvGr             -0.0610      0.013     -4.856      0.000      -0.086      -0.036
KitchenAbvGr             -0.1157      0.014     -8.204      0.000      -0.143      -0.088
GarageCars                0.0169      0.012      1.395      0.163      -0.007       0.041
GarageArea                0.0345      0.015      2.370      0.018       0.006       0.063
WoodDeckSF                0.0112      0.007      1.676      0.094      -0.002       0.024
PoolArea                  6.0083      0.689      8.721      0.000       4.656       7.360
MiscVal                   0.2142      0.084      2.565      0.010       0.050       0.378
MSZoning_FV               0.0242      0.014      1.735      0.083      -0.003       0.052
MSZoning_RH               0.0325      0.013      2.418      0.016       0.006       0.059
MSZoning_RL               0.0292      0.011      2.612      0.009       0.007       0.051
MSZoning_RM               0.0248      0.011      2.193      0.029       0.003       0.047
Street_Pave               0.0372      0.015      2.460      0.014       0.008       0.067
LandContour_Low          -0.0099      0.006     -1.552      0.121      -0.022       0.003
Utilities_NoSeWa         -0.0351      0.028     -1.267      0.206      -0.090       0.019
LotConfig_CulDSac         0.0113      0.004      2.943      0.003       0.004       0.019
LandSlope_Sev            -0.0470      0.015     -3.183      0.002      -0.076      -0.018
Neighborhood_BrkSide   

In [70]:
X_tr_sm.pop('Foundation_Wood')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     179.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:25   Log-Likelihood:                 2286.8
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     931   BIC:                            -3950.
Df Model:                          89                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0952      0.442     -9.263      0.000      -4.963      -3.228
LotArea                   0.1942      0.027      7.103      0.000       0.141       0.248
OverallQual               0.0811      0.011      7.279      0.000       0.059       0.103
OverallCond               0.0553      0.009      6.404      0.000       0.038       0.072
YearBuilt                 0.0700      0.010      6.940      0.000       0.050       0.090
YearRemodAdd              0.0154      0.004      3.686      0.000       0.007       0.024
MasVnrArea                0.0443      0.009      4.798      0.000       0.026       0.062
BsmtFinSF1                0.1693      0.015     11.143      0.000       0.139       0.199
BsmtFinSF2                0.0286      0.009      3.332      0.001       0.012       0.045
BsmtUnfSF                 0.0249      0.007      3.565      0.000       0.011       0.039
TotalBsmtSF               0.1728      0.016     10.898      0.000       0.142       0.204
2ndFlrSF                  0.0393      0.012      3.383      0.001       0.017       0.062
GrLivArea                 0.4241      0.029     14.458      0.000       0.367       0.482
BsmtFullBath              0.0130      0.007      1.845      0.065      -0.001       0.027
HalfBath                 -0.0133      0.005     -2.645      0.008      -0.023      -0.003
BedroomAbvGr             -0.0599      0.013     -4.777      0.000      -0.084      -0.035
KitchenAbvGr             -0.1153      0.014     -8.177      0.000      -0.143      -0.088
GarageCars                0.0174      0.012      1.437      0.151      -0.006       0.041
GarageArea                0.0339      0.015      2.327      0.020       0.005       0.062
WoodDeckSF                0.0117      0.007      1.743      0.082      -0.001       0.025
PoolArea                  6.0145      0.689      8.728      0.000       4.662       7.367
MiscVal                   0.2119      0.084      2.536      0.011       0.048       0.376
MSZoning_FV               0.0242      0.014      1.735      0.083      -0.003       0.052
MSZoning_RH               0.0323      0.013      2.402      0.017       0.006       0.059
MSZoning_RL               0.0290      0.011      2.592      0.010       0.007       0.051
MSZoning_RM               0.0245      0.011      2.173      0.030       0.002       0.047
Street_Pave               0.0371      0.015      2.451      0.014       0.007       0.067
LandContour_Low          -0.0097      0.006     -1.521      0.129      -0.022       0.003
Utilities_NoSeWa         -0.0357      0.028     -1.288      0.198      -0.090       0.019
LotConfig_CulDSac         0.0114      0.004      2.981      0.003       0.004       0.019
LandSlope_Sev            -0.0470      0.015     -3.177      0.002      -0.076      -0.018
Neighborhood_BrkSide   

In [71]:
X_tr_sm.pop('Utilities_NoSeWa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     181.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:25   Log-Likelihood:                 2285.9
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     932   BIC:                            -3955.
Df Model:                          88                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0833      0.442     -9.235      0.000      -4.951      -3.216
LotArea                   0.1936      0.027      7.081      0.000       0.140       0.247
OverallQual               0.0809      0.011      7.257      0.000       0.059       0.103
OverallCond               0.0553      0.009      6.402      0.000       0.038       0.072
YearBuilt                 0.0701      0.010      6.952      0.000       0.050       0.090
YearRemodAdd              0.0157      0.004      3.766      0.000       0.008       0.024
MasVnrArea                0.0431      0.009      4.691      0.000       0.025       0.061
BsmtFinSF1                0.1707      0.015     11.262      0.000       0.141       0.200
BsmtFinSF2                0.0281      0.009      3.276      0.001       0.011       0.045
BsmtUnfSF                 0.0255      0.007      3.663      0.000       0.012       0.039
TotalBsmtSF               0.1742      0.016     11.012      0.000       0.143       0.205
2ndFlrSF                  0.0403      0.012      3.472      0.001       0.018       0.063
GrLivArea                 0.4229      0.029     14.420      0.000       0.365       0.480
BsmtFullBath              0.0132      0.007      1.874      0.061      -0.001       0.027
HalfBath                 -0.0132      0.005     -2.631      0.009      -0.023      -0.003
BedroomAbvGr             -0.0602      0.013     -4.798      0.000      -0.085      -0.036
KitchenAbvGr             -0.1152      0.014     -8.172      0.000      -0.143      -0.088
GarageCars                0.0170      0.012      1.404      0.161      -0.007       0.041
GarageArea                0.0340      0.015      2.334      0.020       0.005       0.063
WoodDeckSF                0.0119      0.007      1.783      0.075      -0.001       0.025
PoolArea                  5.9961      0.689      8.700      0.000       4.644       7.349
MiscVal                   0.2114      0.084      2.529      0.012       0.047       0.375
MSZoning_FV               0.0239      0.014      1.716      0.087      -0.003       0.051
MSZoning_RH               0.0322      0.013      2.396      0.017       0.006       0.059
MSZoning_RL               0.0289      0.011      2.582      0.010       0.007       0.051
MSZoning_RM               0.0245      0.011      2.168      0.030       0.002       0.047
Street_Pave               0.0370      0.015      2.447      0.015       0.007       0.067
LandContour_Low          -0.0097      0.006     -1.512      0.131      -0.022       0.003
LotConfig_CulDSac         0.0108      0.004      2.834      0.005       0.003       0.018
LandSlope_Sev            -0.0468      0.015     -3.163      0.002      -0.076      -0.018
Neighborhood_BrkSide      0.0127      0.005      2.603      0.009       0.003       0.022
Neighborhood_Crawfor   

In [72]:
X_tr_sm.pop('Exterior1st_CemntBd')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     183.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:25   Log-Likelihood:                 2285.0
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     933   BIC:                            -3960.
Df Model:                          87                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0639      0.442     -9.193      0.000      -4.931      -3.196
LotArea                   0.1924      0.027      7.039      0.000       0.139       0.246
OverallQual               0.0809      0.011      7.259      0.000       0.059       0.103
OverallCond               0.0553      0.009      6.396      0.000       0.038       0.072
YearBuilt                 0.0705      0.010      6.989      0.000       0.051       0.090
YearRemodAdd              0.0157      0.004      3.753      0.000       0.007       0.024
MasVnrArea                0.0429      0.009      4.661      0.000       0.025       0.061
BsmtFinSF1                0.1700      0.015     11.220      0.000       0.140       0.200
BsmtFinSF2                0.0282      0.009      3.291      0.001       0.011       0.045
BsmtUnfSF                 0.0260      0.007      3.741      0.000       0.012       0.040
TotalBsmtSF               0.1738      0.016     10.985      0.000       0.143       0.205
2ndFlrSF                  0.0405      0.012      3.494      0.000       0.018       0.063
GrLivArea                 0.4231      0.029     14.422      0.000       0.366       0.481
BsmtFullBath              0.0131      0.007      1.858      0.063      -0.001       0.027
HalfBath                 -0.0136      0.005     -2.709      0.007      -0.023      -0.004
BedroomAbvGr             -0.0603      0.013     -4.804      0.000      -0.085      -0.036
KitchenAbvGr             -0.1154      0.014     -8.181      0.000      -0.143      -0.088
GarageCars                0.0171      0.012      1.413      0.158      -0.007       0.041
GarageArea                0.0337      0.015      2.313      0.021       0.005       0.062
WoodDeckSF                0.0115      0.007      1.722      0.085      -0.002       0.025
PoolArea                  5.9663      0.689      8.659      0.000       4.614       7.319
MiscVal                   0.2106      0.084      2.519      0.012       0.047       0.375
MSZoning_FV               0.0242      0.014      1.732      0.084      -0.003       0.052
MSZoning_RH               0.0322      0.013      2.396      0.017       0.006       0.059
MSZoning_RL               0.0289      0.011      2.581      0.010       0.007       0.051
MSZoning_RM               0.0244      0.011      2.158      0.031       0.002       0.047
Street_Pave               0.0371      0.015      2.450      0.014       0.007       0.067
LandContour_Low          -0.0095      0.006     -1.488      0.137      -0.022       0.003
LotConfig_CulDSac         0.0109      0.004      2.855      0.004       0.003       0.018
LandSlope_Sev            -0.0463      0.015     -3.130      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0126      0.005      2.585      0.010       0.003       0.022
Neighborhood_Crawfor   

In [73]:
X_tr_sm.pop('Exterior1st_VinylSd')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.945
Model:                            OLS   Adj. R-squared:                  0.940
Method:                 Least Squares   F-statistic:                     185.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:25   Log-Likelihood:                 2283.9
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     934   BIC:                            -3965.
Df Model:                          86                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0669      0.442     -9.195      0.000      -4.935      -3.199
LotArea                   0.1929      0.027      7.052      0.000       0.139       0.247
OverallQual               0.0802      0.011      7.200      0.000       0.058       0.102
OverallCond               0.0543      0.009      6.300      0.000       0.037       0.071
YearBuilt                 0.0739      0.010      7.522      0.000       0.055       0.093
YearRemodAdd              0.0167      0.004      4.055      0.000       0.009       0.025
MasVnrArea                0.0426      0.009      4.634      0.000       0.025       0.061
BsmtFinSF1                0.1698      0.015     11.203      0.000       0.140       0.200
BsmtFinSF2                0.0281      0.009      3.272      0.001       0.011       0.045
BsmtUnfSF                 0.0271      0.007      3.909      0.000       0.013       0.041
TotalBsmtSF               0.1740      0.016     10.992      0.000       0.143       0.205
2ndFlrSF                  0.0423      0.012      3.668      0.000       0.020       0.065
GrLivArea                 0.4223      0.029     14.389      0.000       0.365       0.480
BsmtFullBath              0.0136      0.007      1.928      0.054      -0.000       0.027
HalfBath                 -0.0143      0.005     -2.862      0.004      -0.024      -0.004
BedroomAbvGr             -0.0617      0.013     -4.929      0.000      -0.086      -0.037
KitchenAbvGr             -0.1151      0.014     -8.158      0.000      -0.143      -0.087
GarageCars                0.0172      0.012      1.423      0.155      -0.007       0.041
GarageArea                0.0338      0.015      2.322      0.020       0.005       0.062
WoodDeckSF                0.0114      0.007      1.705      0.089      -0.002       0.025
PoolArea                  5.9602      0.689      8.645      0.000       4.607       7.313
MiscVal                   0.2151      0.084      2.574      0.010       0.051       0.379
MSZoning_FV               0.0230      0.014      1.651      0.099      -0.004       0.050
MSZoning_RH               0.0325      0.013      2.416      0.016       0.006       0.059
MSZoning_RL               0.0287      0.011      2.562      0.011       0.007       0.051
MSZoning_RM               0.0249      0.011      2.198      0.028       0.003       0.047
Street_Pave               0.0379      0.015      2.504      0.012       0.008       0.068
LandContour_Low          -0.0104      0.006     -1.629      0.104      -0.023       0.002
LotConfig_CulDSac         0.0106      0.004      2.791      0.005       0.003       0.018
LandSlope_Sev            -0.0459      0.015     -3.105      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0126      0.005      2.592      0.010       0.003       0.022
Neighborhood_Crawfor   

In [74]:
X_tr_sm.pop('GarageCars')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     187.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:26   Log-Likelihood:                 2282.8
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     935   BIC:                            -3970.
Df Model:                          85                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.1021      0.442     -9.284      0.000      -4.969      -3.235
LotArea                   0.1935      0.027      7.072      0.000       0.140       0.247
OverallQual               0.0810      0.011      7.273      0.000       0.059       0.103
OverallCond               0.0531      0.009      6.184      0.000       0.036       0.070
YearBuilt                 0.0743      0.010      7.572      0.000       0.055       0.094
YearRemodAdd              0.0172      0.004      4.196      0.000       0.009       0.025
MasVnrArea                0.0430      0.009      4.674      0.000       0.025       0.061
BsmtFinSF1                0.1701      0.015     11.216      0.000       0.140       0.200
BsmtFinSF2                0.0279      0.009      3.255      0.001       0.011       0.045
BsmtUnfSF                 0.0276      0.007      3.979      0.000       0.014       0.041
TotalBsmtSF               0.1744      0.016     11.013      0.000       0.143       0.205
2ndFlrSF                  0.0431      0.012      3.738      0.000       0.020       0.066
GrLivArea                 0.4218      0.029     14.365      0.000       0.364       0.479
BsmtFullBath              0.0132      0.007      1.877      0.061      -0.001       0.027
HalfBath                 -0.0140      0.005     -2.797      0.005      -0.024      -0.004
BedroomAbvGr             -0.0613      0.013     -4.898      0.000      -0.086      -0.037
KitchenAbvGr             -0.1133      0.014     -8.058      0.000      -0.141      -0.086
GarageArea                0.0497      0.009      5.279      0.000       0.031       0.068
WoodDeckSF                0.0116      0.007      1.738      0.082      -0.001       0.025
PoolArea                  6.0086      0.689      8.721      0.000       4.656       7.361
MiscVal                   0.2157      0.084      2.580      0.010       0.052       0.380
MSZoning_FV               0.0229      0.014      1.642      0.101      -0.004       0.050
MSZoning_RH               0.0322      0.013      2.394      0.017       0.006       0.059
MSZoning_RL               0.0290      0.011      2.585      0.010       0.007       0.051
MSZoning_RM               0.0254      0.011      2.246      0.025       0.003       0.048
Street_Pave               0.0376      0.015      2.487      0.013       0.008       0.067
LandContour_Low          -0.0107      0.006     -1.672      0.095      -0.023       0.002
LotConfig_CulDSac         0.0107      0.004      2.824      0.005       0.003       0.018
LandSlope_Sev            -0.0464      0.015     -3.139      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0129      0.005      2.652      0.008       0.003       0.023
Neighborhood_Crawfor      0.0364      0.005      6.757      0.000       0.026       0.047
Neighborhood_Mitchel   

In [75]:
X_tr_sm.pop('Exterior2nd_Wd Sdng')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     189.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:26   Log-Likelihood:                 2282.0
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     936   BIC:                            -3975.
Df Model:                          84                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -4.0296      0.438     -9.205      0.000      -4.889      -3.170
LotArea                   0.1915      0.027      7.011      0.000       0.138       0.245
OverallQual               0.0804      0.011      7.228      0.000       0.059       0.102
OverallCond               0.0537      0.009      6.272      0.000       0.037       0.071
YearBuilt                 0.0749      0.010      7.639      0.000       0.056       0.094
YearRemodAdd              0.0170      0.004      4.140      0.000       0.009       0.025
MasVnrArea                0.0429      0.009      4.661      0.000       0.025       0.061
BsmtFinSF1                0.1698      0.015     11.193      0.000       0.140       0.200
BsmtFinSF2                0.0277      0.009      3.230      0.001       0.011       0.045
BsmtUnfSF                 0.0276      0.007      3.979      0.000       0.014       0.041
TotalBsmtSF               0.1740      0.016     10.989      0.000       0.143       0.205
2ndFlrSF                  0.0425      0.012      3.686      0.000       0.020       0.065
GrLivArea                 0.4234      0.029     14.435      0.000       0.366       0.481
BsmtFullBath              0.0133      0.007      1.893      0.059      -0.000       0.027
HalfBath                 -0.0136      0.005     -2.734      0.006      -0.023      -0.004
BedroomAbvGr             -0.0613      0.013     -4.896      0.000      -0.086      -0.037
KitchenAbvGr             -0.1139      0.014     -8.104      0.000      -0.142      -0.086
GarageArea                0.0495      0.009      5.258      0.000       0.031       0.068
WoodDeckSF                0.0116      0.007      1.729      0.084      -0.002       0.025
PoolArea                  5.8919      0.682      8.637      0.000       4.553       7.231
MiscVal                   0.2151      0.084      2.572      0.010       0.051       0.379
MSZoning_FV               0.0228      0.014      1.631      0.103      -0.005       0.050
MSZoning_RH               0.0321      0.013      2.385      0.017       0.006       0.059
MSZoning_RL               0.0288      0.011      2.568      0.010       0.007       0.051
MSZoning_RM               0.0253      0.011      2.233      0.026       0.003       0.047
Street_Pave               0.0374      0.015      2.468      0.014       0.008       0.067
LandContour_Low          -0.0106      0.006     -1.667      0.096      -0.023       0.002
LotConfig_CulDSac         0.0108      0.004      2.851      0.004       0.003       0.018
LandSlope_Sev            -0.0462      0.015     -3.120      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0126      0.005      2.596      0.010       0.003       0.022
Neighborhood_Crawfor      0.0359      0.005      6.674      0.000       0.025       0.046
Neighborhood_Mitchel   

In [76]:
X_tr_sm.pop('Exterior1st_Wd Sdng')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     191.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:26   Log-Likelihood:                 2280.9
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     937   BIC:                            -3980.
Df Model:                          83                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9685      0.436     -9.108      0.000      -4.824      -3.113
LotArea                   0.1912      0.027      6.995      0.000       0.138       0.245
OverallQual               0.0794      0.011      7.147      0.000       0.058       0.101
OverallCond               0.0549      0.009      6.442      0.000       0.038       0.072
YearBuilt                 0.0787      0.009      8.344      0.000       0.060       0.097
YearRemodAdd              0.0166      0.004      4.064      0.000       0.009       0.025
MasVnrArea                0.0432      0.009      4.693      0.000       0.025       0.061
BsmtFinSF1                0.1700      0.015     11.202      0.000       0.140       0.200
BsmtFinSF2                0.0268      0.009      3.133      0.002       0.010       0.044
BsmtUnfSF                 0.0277      0.007      3.991      0.000       0.014       0.041
TotalBsmtSF               0.1741      0.016     10.985      0.000       0.143       0.205
2ndFlrSF                  0.0432      0.012      3.750      0.000       0.021       0.066
GrLivArea                 0.4225      0.029     14.399      0.000       0.365       0.480
BsmtFullBath              0.0135      0.007      1.914      0.056      -0.000       0.027
HalfBath                 -0.0138      0.005     -2.762      0.006      -0.024      -0.004
BedroomAbvGr             -0.0614      0.013     -4.903      0.000      -0.086      -0.037
KitchenAbvGr             -0.1127      0.014     -8.028      0.000      -0.140      -0.085
GarageArea                0.0496      0.009      5.268      0.000       0.031       0.068
WoodDeckSF                0.0113      0.007      1.693      0.091      -0.002       0.024
PoolArea                  5.7858      0.678      8.532      0.000       4.455       7.117
MiscVal                   0.2179      0.084      2.605      0.009       0.054       0.382
MSZoning_FV               0.0220      0.014      1.579      0.115      -0.005       0.049
MSZoning_RH               0.0316      0.013      2.349      0.019       0.005       0.058
MSZoning_RL               0.0281      0.011      2.509      0.012       0.006       0.050
MSZoning_RM               0.0245      0.011      2.164      0.031       0.002       0.047
Street_Pave               0.0388      0.015      2.572      0.010       0.009       0.068
LandContour_Low          -0.0109      0.006     -1.709      0.088      -0.023       0.002
LotConfig_CulDSac         0.0110      0.004      2.885      0.004       0.004       0.018
LandSlope_Sev            -0.0451      0.015     -3.048      0.002      -0.074      -0.016
Neighborhood_BrkSide      0.0124      0.005      2.550      0.011       0.003       0.022
Neighborhood_Crawfor      0.0356      0.005      6.623      0.000       0.025       0.046
Neighborhood_Mitchel   

In [77]:
X_tr_sm.pop('GarageQual_Po')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     193.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:26   Log-Likelihood:                 2279.8
No. Observations:                1021   AIC:                            -4394.
Df Residuals:                     938   BIC:                            -3984.
Df Model:                          82                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9739      0.436     -9.115      0.000      -4.830      -3.118
LotArea                   0.1904      0.027      6.965      0.000       0.137       0.244
OverallQual               0.0793      0.011      7.130      0.000       0.057       0.101
OverallCond               0.0544      0.009      6.377      0.000       0.038       0.071
YearBuilt                 0.0782      0.009      8.296      0.000       0.060       0.097
YearRemodAdd              0.0170      0.004      4.148      0.000       0.009       0.025
MasVnrArea                0.0434      0.009      4.712      0.000       0.025       0.061
BsmtFinSF1                0.1692      0.015     11.150      0.000       0.139       0.199
BsmtFinSF2                0.0265      0.009      3.094      0.002       0.010       0.043
BsmtUnfSF                 0.0271      0.007      3.908      0.000       0.013       0.041
TotalBsmtSF               0.1730      0.016     10.924      0.000       0.142       0.204
2ndFlrSF                  0.0420      0.011      3.650      0.000       0.019       0.065
GrLivArea                 0.4252      0.029     14.515      0.000       0.368       0.483
BsmtFullBath              0.0134      0.007      1.907      0.057      -0.000       0.027
HalfBath                 -0.0136      0.005     -2.721      0.007      -0.023      -0.004
BedroomAbvGr             -0.0614      0.013     -4.903      0.000      -0.086      -0.037
KitchenAbvGr             -0.1140      0.014     -8.132      0.000      -0.141      -0.086
GarageArea                0.0484      0.009      5.160      0.000       0.030       0.067
WoodDeckSF                0.0113      0.007      1.685      0.092      -0.002       0.024
PoolArea                  5.7932      0.679      8.537      0.000       4.461       7.125
MiscVal                   0.2202      0.084      2.631      0.009       0.056       0.384
MSZoning_FV               0.0217      0.014      1.557      0.120      -0.006       0.049
MSZoning_RH               0.0320      0.013      2.373      0.018       0.006       0.058
MSZoning_RL               0.0278      0.011      2.482      0.013       0.006       0.050
MSZoning_RM               0.0241      0.011      2.130      0.033       0.002       0.046
Street_Pave               0.0385      0.015      2.545      0.011       0.009       0.068
LandContour_Low          -0.0108      0.006     -1.697      0.090      -0.023       0.002
LotConfig_CulDSac         0.0109      0.004      2.863      0.004       0.003       0.018
LandSlope_Sev            -0.0448      0.015     -3.027      0.003      -0.074      -0.016
Neighborhood_BrkSide      0.0129      0.005      2.650      0.008       0.003       0.022
Neighborhood_Crawfor      0.0346      0.005      6.485      0.000       0.024       0.045
Neighborhood_Mitchel   

In [78]:
X_tr_sm.pop('GarageQual_TA')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     195.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:27   Log-Likelihood:                 2278.6
No. Observations:                1021   AIC:                            -4393.
Df Residuals:                     939   BIC:                            -3989.
Df Model:                          81                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9710      0.436     -9.103      0.000      -4.827      -3.115
LotArea                   0.1899      0.027      6.941      0.000       0.136       0.244
OverallQual               0.0785      0.011      7.066      0.000       0.057       0.100
OverallCond               0.0534      0.009      6.279      0.000       0.037       0.070
YearBuilt                 0.0769      0.009      8.191      0.000       0.059       0.095
YearRemodAdd              0.0178      0.004      4.396      0.000       0.010       0.026
MasVnrArea                0.0434      0.009      4.711      0.000       0.025       0.062
BsmtFinSF1                0.1695      0.015     11.167      0.000       0.140       0.199
BsmtFinSF2                0.0261      0.009      3.053      0.002       0.009       0.043
BsmtUnfSF                 0.0275      0.007      3.977      0.000       0.014       0.041
TotalBsmtSF               0.1734      0.016     10.945      0.000       0.142       0.205
2ndFlrSF                  0.0419      0.012      3.643      0.000       0.019       0.064
GrLivArea                 0.4269      0.029     14.574      0.000       0.369       0.484
BsmtFullBath              0.0139      0.007      1.970      0.049    5.38e-05       0.028
HalfBath                 -0.0137      0.005     -2.741      0.006      -0.023      -0.004
BedroomAbvGr             -0.0617      0.013     -4.923      0.000      -0.086      -0.037
KitchenAbvGr             -0.1107      0.014     -7.997      0.000      -0.138      -0.084
GarageArea                0.0416      0.008      5.114      0.000       0.026       0.058
WoodDeckSF                0.0115      0.007      1.717      0.086      -0.002       0.025
PoolArea                  5.7801      0.679      8.514      0.000       4.448       7.112
MiscVal                   0.2230      0.084      2.663      0.008       0.059       0.387
MSZoning_FV               0.0212      0.014      1.515      0.130      -0.006       0.049
MSZoning_RH               0.0321      0.013      2.378      0.018       0.006       0.059
MSZoning_RL               0.0275      0.011      2.454      0.014       0.006       0.050
MSZoning_RM               0.0237      0.011      2.099      0.036       0.002       0.046
Street_Pave               0.0374      0.015      2.474      0.014       0.008       0.067
LandContour_Low          -0.0104      0.006     -1.626      0.104      -0.023       0.002
LotConfig_CulDSac         0.0109      0.004      2.863      0.004       0.003       0.018
LandSlope_Sev            -0.0455      0.015     -3.079      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0128      0.005      2.631      0.009       0.003       0.022
Neighborhood_Crawfor      0.0342      0.005      6.423      0.000       0.024       0.045
Neighborhood_Mitchel   

In [79]:
X_tr_sm.pop('MSZoning_FV')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     197.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:27   Log-Likelihood:                 2277.4
No. Observations:                1021   AIC:                            -4393.
Df Residuals:                     940   BIC:                            -3993.
Df Model:                          80                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9577      0.436     -9.068      0.000      -4.814      -3.101
LotArea                   0.1917      0.027      7.010      0.000       0.138       0.245
OverallQual               0.0793      0.011      7.143      0.000       0.058       0.101
OverallCond               0.0551      0.008      6.531      0.000       0.039       0.072
YearBuilt                 0.0787      0.009      8.429      0.000       0.060       0.097
YearRemodAdd              0.0175      0.004      4.324      0.000       0.010       0.025
MasVnrArea                0.0434      0.009      4.703      0.000       0.025       0.061
BsmtFinSF1                0.1687      0.015     11.111      0.000       0.139       0.198
BsmtFinSF2                0.0263      0.009      3.071      0.002       0.009       0.043
BsmtUnfSF                 0.0273      0.007      3.940      0.000       0.014       0.041
TotalBsmtSF               0.1726      0.016     10.891      0.000       0.141       0.204
2ndFlrSF                  0.0418      0.012      3.629      0.000       0.019       0.064
GrLivArea                 0.4265      0.029     14.550      0.000       0.369       0.484
BsmtFullBath              0.0144      0.007      2.043      0.041       0.001       0.028
HalfBath                 -0.0133      0.005     -2.665      0.008      -0.023      -0.004
BedroomAbvGr             -0.0605      0.013     -4.831      0.000      -0.085      -0.036
KitchenAbvGr             -0.1103      0.014     -7.962      0.000      -0.137      -0.083
GarageArea                0.0410      0.008      5.045      0.000       0.025       0.057
WoodDeckSF                0.0114      0.007      1.702      0.089      -0.002       0.025
PoolArea                  5.7671      0.679      8.489      0.000       4.434       7.100
MiscVal                   0.2266      0.084      2.705      0.007       0.062       0.391
MSZoning_RH               0.0188      0.010      1.831      0.067      -0.001       0.039
MSZoning_RL               0.0141      0.007      2.052      0.040       0.001       0.028
MSZoning_RM               0.0105      0.007      1.460      0.145      -0.004       0.025
Street_Pave               0.0405      0.015      2.704      0.007       0.011       0.070
LandContour_Low          -0.0111      0.006     -1.740      0.082      -0.024       0.001
LotConfig_CulDSac         0.0104      0.004      2.750      0.006       0.003       0.018
LandSlope_Sev            -0.0450      0.015     -3.043      0.002      -0.074      -0.016
Neighborhood_BrkSide      0.0131      0.005      2.696      0.007       0.004       0.023
Neighborhood_Crawfor      0.0345      0.005      6.469      0.000       0.024       0.045
Neighborhood_Mitchel     -0.0158      0.005     -3.244      0.001      -0.025      -0.006
Neighborhood_NPkVill   

In [80]:
X_tr_sm.pop('MSZoning_RM')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     199.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:27   Log-Likelihood:                 2276.2
No. Observations:                1021   AIC:                            -4392.
Df Residuals:                     941   BIC:                            -3998.
Df Model:                          79                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9593      0.437     -9.066      0.000      -4.816      -3.102
LotArea                   0.1921      0.027      7.021      0.000       0.138       0.246
OverallQual               0.0809      0.011      7.310      0.000       0.059       0.103
OverallCond               0.0562      0.008      6.689      0.000       0.040       0.073
YearBuilt                 0.0781      0.009      8.374      0.000       0.060       0.096
YearRemodAdd              0.0174      0.004      4.306      0.000       0.009       0.025
MasVnrArea                0.0437      0.009      4.734      0.000       0.026       0.062
BsmtFinSF1                0.1685      0.015     11.093      0.000       0.139       0.198
BsmtFinSF2                0.0265      0.009      3.094      0.002       0.010       0.043
BsmtUnfSF                 0.0279      0.007      4.032      0.000       0.014       0.041
TotalBsmtSF               0.1727      0.016     10.892      0.000       0.142       0.204
2ndFlrSF                  0.0417      0.012      3.619      0.000       0.019       0.064
GrLivArea                 0.4246      0.029     14.491      0.000       0.367       0.482
BsmtFullBath              0.0149      0.007      2.124      0.034       0.001       0.029
HalfBath                 -0.0136      0.005     -2.726      0.007      -0.023      -0.004
BedroomAbvGr             -0.0597      0.013     -4.772      0.000      -0.084      -0.035
KitchenAbvGr             -0.1095      0.014     -7.908      0.000      -0.137      -0.082
GarageArea                0.0412      0.008      5.063      0.000       0.025       0.057
WoodDeckSF                0.0118      0.007      1.767      0.078      -0.001       0.025
PoolArea                  5.7765      0.680      8.498      0.000       4.443       7.110
MiscVal                   0.2280      0.084      2.721      0.007       0.064       0.392
MSZoning_RH               0.0097      0.008      1.186      0.236      -0.006       0.026
MSZoning_RL               0.0051      0.003      1.676      0.094      -0.001       0.011
Street_Pave               0.0422      0.015      2.827      0.005       0.013       0.072
LandContour_Low          -0.0117      0.006     -1.841      0.066      -0.024       0.001
LotConfig_CulDSac         0.0107      0.004      2.833      0.005       0.003       0.018
LandSlope_Sev            -0.0445      0.015     -3.009      0.003      -0.074      -0.015
Neighborhood_BrkSide      0.0136      0.005      2.803      0.005       0.004       0.023
Neighborhood_Crawfor      0.0343      0.005      6.437      0.000       0.024       0.045
Neighborhood_Mitchel     -0.0156      0.005     -3.214      0.001      -0.025      -0.006
Neighborhood_NPkVill      0.0300      0.012      2.425      0.016       0.006       0.054
Neighborhood_NoRidge   

In [81]:
X_tr_sm.pop('MSZoning_RH')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     202.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:27   Log-Likelihood:                 2275.4
No. Observations:                1021   AIC:                            -4393.
Df Residuals:                     942   BIC:                            -4004.
Df Model:                          78                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9564      0.437     -9.058      0.000      -4.814      -3.099
LotArea                   0.1924      0.027      7.028      0.000       0.139       0.246
OverallQual               0.0808      0.011      7.300      0.000       0.059       0.102
OverallCond               0.0559      0.008      6.655      0.000       0.039       0.072
YearBuilt                 0.0787      0.009      8.448      0.000       0.060       0.097
YearRemodAdd              0.0176      0.004      4.334      0.000       0.010       0.026
MasVnrArea                0.0436      0.009      4.730      0.000       0.026       0.062
BsmtFinSF1                0.1685      0.015     11.092      0.000       0.139       0.198
BsmtFinSF2                0.0263      0.009      3.073      0.002       0.010       0.043
BsmtUnfSF                 0.0275      0.007      3.982      0.000       0.014       0.041
TotalBsmtSF               0.1725      0.016     10.880      0.000       0.141       0.204
2ndFlrSF                  0.0412      0.012      3.576      0.000       0.019       0.064
GrLivArea                 0.4257      0.029     14.531      0.000       0.368       0.483
BsmtFullBath              0.0150      0.007      2.127      0.034       0.001       0.029
HalfBath                 -0.0138      0.005     -2.768      0.006      -0.024      -0.004
BedroomAbvGr             -0.0585      0.012     -4.688      0.000      -0.083      -0.034
KitchenAbvGr             -0.1087      0.014     -7.857      0.000      -0.136      -0.082
GarageArea                0.0405      0.008      4.995      0.000       0.025       0.056
WoodDeckSF                0.0120      0.007      1.792      0.073      -0.001       0.025
PoolArea                  5.7716      0.680      8.489      0.000       4.437       7.106
MiscVal                   0.2271      0.084      2.710      0.007       0.063       0.392
MSZoning_RL               0.0042      0.003      1.426      0.154      -0.002       0.010
Street_Pave               0.0427      0.015      2.858      0.004       0.013       0.072
LandContour_Low          -0.0117      0.006     -1.842      0.066      -0.024       0.001
LotConfig_CulDSac         0.0108      0.004      2.855      0.004       0.003       0.018
LandSlope_Sev            -0.0446      0.015     -3.012      0.003      -0.074      -0.016
Neighborhood_BrkSide      0.0132      0.005      2.720      0.007       0.004       0.023
Neighborhood_Crawfor      0.0346      0.005      6.494      0.000       0.024       0.045
Neighborhood_Mitchel     -0.0158      0.005     -3.246      0.001      -0.025      -0.006
Neighborhood_NPkVill      0.0301      0.012      2.435      0.015       0.006       0.054
Neighborhood_NoRidge      0.0405      0.006      7.181      0.000       0.029       0.052
Neighborhood_NridgHt   

In [82]:
X_tr_sm.pop('MSZoning_RL')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.944
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     204.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:27   Log-Likelihood:                 2274.3
No. Observations:                1021   AIC:                            -4393.
Df Residuals:                     943   BIC:                            -4008.
Df Model:                          77                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9326      0.437     -9.005      0.000      -4.790      -3.076
LotArea                   0.1958      0.027      7.179      0.000       0.142       0.249
OverallQual               0.0797      0.011      7.216      0.000       0.058       0.101
OverallCond               0.0564      0.008      6.710      0.000       0.040       0.073
YearBuilt                 0.0829      0.009      9.372      0.000       0.066       0.100
YearRemodAdd              0.0170      0.004      4.218      0.000       0.009       0.025
MasVnrArea                0.0431      0.009      4.672      0.000       0.025       0.061
BsmtFinSF1                0.1677      0.015     11.042      0.000       0.138       0.198
BsmtFinSF2                0.0262      0.009      3.060      0.002       0.009       0.043
BsmtUnfSF                 0.0270      0.007      3.915      0.000       0.013       0.041
TotalBsmtSF               0.1716      0.016     10.825      0.000       0.141       0.203
2ndFlrSF                  0.0385      0.011      3.385      0.001       0.016       0.061
GrLivArea                 0.4294      0.029     14.710      0.000       0.372       0.487
BsmtFullBath              0.0150      0.007      2.135      0.033       0.001       0.029
HalfBath                 -0.0131      0.005     -2.645      0.008      -0.023      -0.003
BedroomAbvGr             -0.0572      0.012     -4.595      0.000      -0.082      -0.033
KitchenAbvGr             -0.1104      0.014     -8.009      0.000      -0.138      -0.083
GarageArea                0.0402      0.008      4.950      0.000       0.024       0.056
WoodDeckSF                0.0126      0.007      1.883      0.060      -0.001       0.026
PoolArea                  5.7326      0.680      8.434      0.000       4.399       7.066
MiscVal                   0.2292      0.084      2.733      0.006       0.065       0.394
Street_Pave               0.0450      0.015      3.034      0.002       0.016       0.074
LandContour_Low          -0.0120      0.006     -1.884      0.060      -0.024       0.000
LotConfig_CulDSac         0.0110      0.004      2.914      0.004       0.004       0.018
LandSlope_Sev            -0.0453      0.015     -3.058      0.002      -0.074      -0.016
Neighborhood_BrkSide      0.0125      0.005      2.589      0.010       0.003       0.022
Neighborhood_Crawfor      0.0357      0.005      6.758      0.000       0.025       0.046
Neighborhood_Mitchel     -0.0158      0.005     -3.254      0.001      -0.025      -0.006
Neighborhood_NPkVill      0.0323      0.012      2.634      0.009       0.008       0.056
Neighborhood_NoRidge      0.0407      0.006      7.214      0.000       0.030       0.052
Neighborhood_NridgHt      0.0265      0.005      5.414      0.000       0.017       0.036
Neighborhood_Somerst   

In [83]:
X_tr_sm.pop('Neighborhood_Veenker')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.943
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     207.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:28   Log-Likelihood:                 2273.1
No. Observations:                1021   AIC:                            -4392.
Df Residuals:                     944   BIC:                            -4013.
Df Model:                          76                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9312      0.437     -8.995      0.000      -4.789      -3.074
LotArea                   0.1963      0.027      7.193      0.000       0.143       0.250
OverallQual               0.0800      0.011      7.244      0.000       0.058       0.102
OverallCond               0.0575      0.008      6.859      0.000       0.041       0.074
YearBuilt                 0.0827      0.009      9.347      0.000       0.065       0.100
YearRemodAdd              0.0169      0.004      4.187      0.000       0.009       0.025
MasVnrArea                0.0423      0.009      4.594      0.000       0.024       0.060
BsmtFinSF1                0.1679      0.015     11.045      0.000       0.138       0.198
BsmtFinSF2                0.0272      0.009      3.172      0.002       0.010       0.044
BsmtUnfSF                 0.0270      0.007      3.903      0.000       0.013       0.041
TotalBsmtSF               0.1720      0.016     10.840      0.000       0.141       0.203
2ndFlrSF                  0.0381      0.011      3.349      0.001       0.016       0.060
GrLivArea                 0.4288      0.029     14.679      0.000       0.371       0.486
BsmtFullBath              0.0151      0.007      2.139      0.033       0.001       0.029
HalfBath                 -0.0124      0.005     -2.513      0.012      -0.022      -0.003
BedroomAbvGr             -0.0577      0.012     -4.631      0.000      -0.082      -0.033
KitchenAbvGr             -0.1100      0.014     -7.974      0.000      -0.137      -0.083
GarageArea                0.0405      0.008      4.984      0.000       0.025       0.056
WoodDeckSF                0.0129      0.007      1.927      0.054      -0.000       0.026
PoolArea                  5.7280      0.680      8.422      0.000       4.393       7.063
MiscVal                   0.2300      0.084      2.741      0.006       0.065       0.395
Street_Pave               0.0452      0.015      3.042      0.002       0.016       0.074
LandContour_Low          -0.0121      0.006     -1.903      0.057      -0.025       0.000
LotConfig_CulDSac         0.0114      0.004      3.016      0.003       0.004       0.019
LandSlope_Sev            -0.0466      0.015     -3.151      0.002      -0.076      -0.018
Neighborhood_BrkSide      0.0124      0.005      2.578      0.010       0.003       0.022
Neighborhood_Crawfor      0.0354      0.005      6.702      0.000       0.025       0.046
Neighborhood_Mitchel     -0.0161      0.005     -3.312      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0308      0.012      2.521      0.012       0.007       0.055
Neighborhood_NoRidge      0.0405      0.006      7.178      0.000       0.029       0.052
Neighborhood_NridgHt      0.0263      0.005      5.363      0.000       0.017       0.036
Neighborhood_Somerst   

In [84]:
X_tr_sm.pop('GarageCond_Gd')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.943
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     209.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:28   Log-Likelihood:                 2271.7
No. Observations:                1021   AIC:                            -4391.
Df Residuals:                     945   BIC:                            -4017.
Df Model:                          75                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9389      0.437     -9.007      0.000      -4.797      -3.081
LotArea                   0.1976      0.027      7.238      0.000       0.144       0.251
OverallQual               0.0803      0.011      7.258      0.000       0.059       0.102
OverallCond               0.0573      0.008      6.837      0.000       0.041       0.074
YearBuilt                 0.0830      0.009      9.370      0.000       0.066       0.100
YearRemodAdd              0.0171      0.004      4.236      0.000       0.009       0.025
MasVnrArea                0.0422      0.009      4.573      0.000       0.024       0.060
BsmtFinSF1                0.1681      0.015     11.051      0.000       0.138       0.198
BsmtFinSF2                0.0273      0.009      3.185      0.001       0.010       0.044
BsmtUnfSF                 0.0271      0.007      3.921      0.000       0.014       0.041
TotalBsmtSF               0.1722      0.016     10.850      0.000       0.141       0.203
2ndFlrSF                  0.0380      0.011      3.340      0.001       0.016       0.060
GrLivArea                 0.4291      0.029     14.677      0.000       0.372       0.486
BsmtFullBath              0.0146      0.007      2.079      0.038       0.001       0.028
HalfBath                 -0.0122      0.005     -2.457      0.014      -0.022      -0.002
BedroomAbvGr             -0.0577      0.012     -4.631      0.000      -0.082      -0.033
KitchenAbvGr             -0.1095      0.014     -7.930      0.000      -0.137      -0.082
GarageArea                0.0402      0.008      4.954      0.000       0.024       0.056
WoodDeckSF                0.0125      0.007      1.863      0.063      -0.001       0.026
PoolArea                  5.7384      0.681      8.431      0.000       4.403       7.074
MiscVal                   0.2310      0.084      2.752      0.006       0.066       0.396
Street_Pave               0.0452      0.015      3.038      0.002       0.016       0.074
LandContour_Low          -0.0120      0.006     -1.888      0.059      -0.024       0.000
LotConfig_CulDSac         0.0109      0.004      2.880      0.004       0.003       0.018
LandSlope_Sev            -0.0468      0.015     -3.164      0.002      -0.076      -0.018
Neighborhood_BrkSide      0.0126      0.005      2.608      0.009       0.003       0.022
Neighborhood_Crawfor      0.0356      0.005      6.749      0.000       0.025       0.046
Neighborhood_Mitchel     -0.0159      0.005     -3.265      0.001      -0.025      -0.006
Neighborhood_NPkVill      0.0309      0.012      2.522      0.012       0.007       0.055
Neighborhood_NoRidge      0.0401      0.006      7.117      0.000       0.029       0.051
Neighborhood_NridgHt      0.0263      0.005      5.370      0.000       0.017       0.036
Neighborhood_Somerst   

In [85]:

X_tr_sm.pop('Foundation_Slab')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.943
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     211.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:28   Log-Likelihood:                 2270.2
No. Observations:                1021   AIC:                            -4390.
Df Residuals:                     946   BIC:                            -4021.
Df Model:                          74                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9280      0.438     -8.974      0.000      -4.787      -3.069
LotArea                   0.1966      0.027      7.196      0.000       0.143       0.250
OverallQual               0.0816      0.011      7.396      0.000       0.060       0.103
OverallCond               0.0573      0.008      6.831      0.000       0.041       0.074
YearBuilt                 0.0815      0.009      9.241      0.000       0.064       0.099
YearRemodAdd              0.0176      0.004      4.373      0.000       0.010       0.026
MasVnrArea                0.0419      0.009      4.538      0.000       0.024       0.060
BsmtFinSF1                0.1763      0.014     12.220      0.000       0.148       0.205
BsmtFinSF2                0.0289      0.009      3.385      0.001       0.012       0.046
BsmtUnfSF                 0.0304      0.007      4.580      0.000       0.017       0.043
TotalBsmtSF               0.1814      0.015     12.164      0.000       0.152       0.211
2ndFlrSF                  0.0421      0.011      3.788      0.000       0.020       0.064
GrLivArea                 0.4185      0.029     14.650      0.000       0.362       0.475
BsmtFullBath              0.0150      0.007      2.128      0.034       0.001       0.029
HalfBath                 -0.0114      0.005     -2.305      0.021      -0.021      -0.002
BedroomAbvGr             -0.0587      0.012     -4.711      0.000      -0.083      -0.034
KitchenAbvGr             -0.1111      0.014     -8.066      0.000      -0.138      -0.084
GarageArea                0.0396      0.008      4.871      0.000       0.024       0.056
WoodDeckSF                0.0129      0.007      1.921      0.055      -0.000       0.026
PoolArea                  5.7475      0.681      8.437      0.000       4.411       7.084
MiscVal                   0.2081      0.083      2.510      0.012       0.045       0.371
Street_Pave               0.0438      0.015      2.945      0.003       0.015       0.073
LandContour_Low          -0.0118      0.006     -1.857      0.064      -0.024       0.001
LotConfig_CulDSac         0.0109      0.004      2.892      0.004       0.004       0.018
LandSlope_Sev            -0.0463      0.015     -3.126      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0123      0.005      2.537      0.011       0.003       0.022
Neighborhood_Crawfor      0.0359      0.005      6.790      0.000       0.026       0.046
Neighborhood_Mitchel     -0.0152      0.005     -3.134      0.002      -0.025      -0.006
Neighborhood_NPkVill      0.0310      0.012      2.533      0.011       0.007       0.055
Neighborhood_NoRidge      0.0399      0.006      7.066      0.000       0.029       0.051
Neighborhood_NridgHt      0.0264      0.005      5.385      0.000       0.017       0.036
Neighborhood_Somerst   

In [86]:

X_tr_sm.pop('SaleCondition_Alloca')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.943
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     214.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:29   Log-Likelihood:                 2269.1
No. Observations:                1021   AIC:                            -4390.
Df Residuals:                     947   BIC:                            -4025.
Df Model:                          73                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9209      0.438     -8.953      0.000      -4.780      -3.061
LotArea                   0.1937      0.027      7.104      0.000       0.140       0.247
OverallQual               0.0821      0.011      7.440      0.000       0.060       0.104
OverallCond               0.0571      0.008      6.800      0.000       0.041       0.074
YearBuilt                 0.0820      0.009      9.299      0.000       0.065       0.099
YearRemodAdd              0.0178      0.004      4.427      0.000       0.010       0.026
MasVnrArea                0.0415      0.009      4.493      0.000       0.023       0.060
BsmtFinSF1                0.1732      0.014     12.129      0.000       0.145       0.201
BsmtFinSF2                0.0278      0.008      3.268      0.001       0.011       0.044
BsmtUnfSF                 0.0293      0.007      4.442      0.000       0.016       0.042
TotalBsmtSF               0.1779      0.015     12.079      0.000       0.149       0.207
2ndFlrSF                  0.0402      0.011      3.639      0.000       0.019       0.062
GrLivArea                 0.4235      0.028     14.921      0.000       0.368       0.479
BsmtFullBath              0.0159      0.007      2.271      0.023       0.002       0.030
HalfBath                 -0.0112      0.005     -2.272      0.023      -0.021      -0.002
BedroomAbvGr             -0.0592      0.012     -4.748      0.000      -0.084      -0.035
KitchenAbvGr             -0.1076      0.014     -7.928      0.000      -0.134      -0.081
GarageArea                0.0394      0.008      4.844      0.000       0.023       0.055
WoodDeckSF                0.0127      0.007      1.896      0.058      -0.000       0.026
PoolArea                  5.7439      0.682      8.426      0.000       4.406       7.082
MiscVal                   0.2044      0.083      2.465      0.014       0.042       0.367
Street_Pave               0.0400      0.015      2.733      0.006       0.011       0.069
LandContour_Low          -0.0118      0.006     -1.853      0.064      -0.024       0.001
LotConfig_CulDSac         0.0109      0.004      2.875      0.004       0.003       0.018
LandSlope_Sev            -0.0462      0.015     -3.114      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0122      0.005      2.535      0.011       0.003       0.022
Neighborhood_Crawfor      0.0363      0.005      6.882      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0152      0.005     -3.127      0.002      -0.025      -0.006
Neighborhood_NPkVill      0.0306      0.012      2.494      0.013       0.007       0.055
Neighborhood_NoRidge      0.0399      0.006      7.074      0.000       0.029       0.051
Neighborhood_NridgHt      0.0266      0.005      5.417      0.000       0.017       0.036
Neighborhood_Somerst   

In [87]:

X_tr_sm.pop('Heating_Wall')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.943
Model:                            OLS   Adj. R-squared:                  0.939
Method:                 Least Squares   F-statistic:                     217.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:29   Log-Likelihood:                 2267.9
No. Observations:                1021   AIC:                            -4390.
Df Residuals:                     948   BIC:                            -4030.
Df Model:                          72                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9146      0.438     -8.933      0.000      -4.775      -3.055
LotArea                   0.1930      0.027      7.076      0.000       0.140       0.247
OverallQual               0.0810      0.011      7.352      0.000       0.059       0.103
OverallCond               0.0566      0.008      6.746      0.000       0.040       0.073
YearBuilt                 0.0818      0.009      9.265      0.000       0.064       0.099
YearRemodAdd              0.0176      0.004      4.357      0.000       0.010       0.025
MasVnrArea                0.0423      0.009      4.586      0.000       0.024       0.060
BsmtFinSF1                0.1710      0.014     12.032      0.000       0.143       0.199
BsmtFinSF2                0.0271      0.008      3.192      0.001       0.010       0.044
BsmtUnfSF                 0.0285      0.007      4.329      0.000       0.016       0.041
TotalBsmtSF               0.1754      0.015     11.979      0.000       0.147       0.204
2ndFlrSF                  0.0394      0.011      3.571      0.000       0.018       0.061
GrLivArea                 0.4241      0.028     14.935      0.000       0.368       0.480
BsmtFullBath              0.0159      0.007      2.258      0.024       0.002       0.030
HalfBath                 -0.0111      0.005     -2.255      0.024      -0.021      -0.001
BedroomAbvGr             -0.0598      0.012     -4.800      0.000      -0.084      -0.035
KitchenAbvGr             -0.1049      0.013     -7.793      0.000      -0.131      -0.078
GarageArea                0.0396      0.008      4.875      0.000       0.024       0.056
WoodDeckSF                0.0129      0.007      1.932      0.054      -0.000       0.026
PoolArea                  5.7426      0.682      8.419      0.000       4.404       7.081
MiscVal                   0.2020      0.083      2.435      0.015       0.039       0.365
Street_Pave               0.0402      0.015      2.740      0.006       0.011       0.069
LandContour_Low          -0.0119      0.006     -1.868      0.062      -0.024       0.001
LotConfig_CulDSac         0.0109      0.004      2.874      0.004       0.003       0.018
LandSlope_Sev            -0.0457      0.015     -3.082      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0121      0.005      2.512      0.012       0.003       0.022
Neighborhood_Crawfor      0.0363      0.005      6.872      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0155      0.005     -3.179      0.002      -0.025      -0.006
Neighborhood_NPkVill      0.0309      0.012      2.521      0.012       0.007       0.055
Neighborhood_NoRidge      0.0401      0.006      7.105      0.000       0.029       0.051
Neighborhood_NridgHt      0.0267      0.005      5.440      0.000       0.017       0.036
Neighborhood_Somerst   

In [88]:

X_tr_sm.pop('GarageQual_Fa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.943
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     219.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:29   Log-Likelihood:                 2266.4
No. Observations:                1021   AIC:                            -4389.
Df Residuals:                     949   BIC:                            -4034.
Df Model:                          71                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.9092      0.439     -8.913      0.000      -4.770      -3.049
LotArea                   0.1933      0.027      7.079      0.000       0.140       0.247
OverallQual               0.0813      0.011      7.373      0.000       0.060       0.103
OverallCond               0.0580      0.008      6.928      0.000       0.042       0.074
YearBuilt                 0.0847      0.009      9.800      0.000       0.068       0.102
YearRemodAdd              0.0170      0.004      4.226      0.000       0.009       0.025
MasVnrArea                0.0423      0.009      4.585      0.000       0.024       0.060
BsmtFinSF1                0.1703      0.014     11.977      0.000       0.142       0.198
BsmtFinSF2                0.0272      0.008      3.200      0.001       0.011       0.044
BsmtUnfSF                 0.0270      0.007      4.139      0.000       0.014       0.040
TotalBsmtSF               0.1742      0.015     11.901      0.000       0.145       0.203
2ndFlrSF                  0.0378      0.011      3.432      0.001       0.016       0.059
GrLivArea                 0.4280      0.028     15.111      0.000       0.372       0.484
BsmtFullBath              0.0152      0.007      2.164      0.031       0.001       0.029
HalfBath                 -0.0113      0.005     -2.297      0.022      -0.021      -0.002
BedroomAbvGr             -0.0586      0.012     -4.705      0.000      -0.083      -0.034
KitchenAbvGr             -0.1064      0.013     -7.918      0.000      -0.133      -0.080
GarageArea                0.0398      0.008      4.890      0.000       0.024       0.056
WoodDeckSF                0.0127      0.007      1.889      0.059      -0.000       0.026
PoolArea                  5.7263      0.683      8.388      0.000       4.387       7.066
MiscVal                   0.2062      0.083      2.484      0.013       0.043       0.369
Street_Pave               0.0399      0.015      2.721      0.007       0.011       0.069
LandContour_Low          -0.0117      0.006     -1.834      0.067      -0.024       0.001
LotConfig_CulDSac         0.0108      0.004      2.857      0.004       0.003       0.018
LandSlope_Sev            -0.0454      0.015     -3.061      0.002      -0.075      -0.016
Neighborhood_BrkSide      0.0122      0.005      2.516      0.012       0.003       0.022
Neighborhood_Crawfor      0.0362      0.005      6.856      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0153      0.005     -3.145      0.002      -0.025      -0.006
Neighborhood_NPkVill      0.0313      0.012      2.550      0.011       0.007       0.055
Neighborhood_NoRidge      0.0400      0.006      7.080      0.000       0.029       0.051
Neighborhood_NridgHt      0.0267      0.005      5.433      0.000       0.017       0.036
Neighborhood_Somerst   

In [89]:

X_tr_sm.pop('LandContour_Low')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.942
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     222.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:29   Log-Likelihood:                 2264.6
No. Observations:                1021   AIC:                            -4387.
Df Residuals:                     950   BIC:                            -4037.
Df Model:                          70                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.8830      0.439     -8.847      0.000      -4.744      -3.022
LotArea                   0.1808      0.026      6.829      0.000       0.129       0.233
OverallQual               0.0822      0.011      7.446      0.000       0.061       0.104
OverallCond               0.0583      0.008      6.968      0.000       0.042       0.075
YearBuilt                 0.0851      0.009      9.833      0.000       0.068       0.102
YearRemodAdd              0.0170      0.004      4.229      0.000       0.009       0.025
MasVnrArea                0.0433      0.009      4.691      0.000       0.025       0.061
BsmtFinSF1                0.1696      0.014     11.913      0.000       0.142       0.197
BsmtFinSF2                0.0275      0.009      3.238      0.001       0.011       0.044
BsmtUnfSF                 0.0275      0.007      4.217      0.000       0.015       0.040
TotalBsmtSF               0.1738      0.015     11.858      0.000       0.145       0.203
2ndFlrSF                  0.0380      0.011      3.447      0.001       0.016       0.060
GrLivArea                 0.4286      0.028     15.115      0.000       0.373       0.484
BsmtFullBath              0.0155      0.007      2.214      0.027       0.002       0.029
HalfBath                 -0.0116      0.005     -2.351      0.019      -0.021      -0.002
BedroomAbvGr             -0.0580      0.012     -4.652      0.000      -0.082      -0.034
KitchenAbvGr             -0.1073      0.013     -7.980      0.000      -0.134      -0.081
GarageArea                0.0391      0.008      4.802      0.000       0.023       0.055
WoodDeckSF                0.0118      0.007      1.769      0.077      -0.001       0.025
PoolArea                  5.7060      0.683      8.349      0.000       4.365       7.047
MiscVal                   0.1936      0.083      2.338      0.020       0.031       0.356
Street_Pave               0.0374      0.015      2.557      0.011       0.009       0.066
LotConfig_CulDSac         0.0107      0.004      2.822      0.005       0.003       0.018
LandSlope_Sev            -0.0460      0.015     -3.100      0.002      -0.075      -0.017
Neighborhood_BrkSide      0.0121      0.005      2.503      0.012       0.003       0.022
Neighborhood_Crawfor      0.0361      0.005      6.818      0.000       0.026       0.046
Neighborhood_Mitchel     -0.0163      0.005     -3.375      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0310      0.012      2.523      0.012       0.007       0.055
Neighborhood_NoRidge      0.0401      0.006      7.087      0.000       0.029       0.051
Neighborhood_NridgHt      0.0266      0.005      5.404      0.000       0.017       0.036
Neighborhood_Somerst      0.0209      0.004      4.859      0.000       0.012       0.029
Neighborhood_StoneBr   

In [90]:

#X_tr_sm.pop('LandContour_Low')
#model1 = sm.OLS(y_tr,X_tr_sm)
#res1 = model1.fit()
#res1.summary()

from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data

Feature          VIF
0                   const     0.000000
1                 LotArea     2.226558
2             OverallQual     4.030415
3             OverallCond     1.788087
4               YearBuilt     4.948867
5            YearRemodAdd     2.609961
6              MasVnrArea     1.597500
7              BsmtFinSF1          inf
8              BsmtFinSF2          inf
9               BsmtUnfSF          inf
10            TotalBsmtSF          inf
11               2ndFlrSF     7.386729
12              GrLivArea    11.050247
13           BsmtFullBath     2.069505
14               HalfBath     2.095698
15           BedroomAbvGr     2.234339
16           KitchenAbvGr     1.457724
17             GarageArea     2.029648
18             WoodDeckSF     1.295857
19               PoolArea  1399.042890
20                MiscVal    13.071718
21            Street_Pave     1.143405
22      LotConfig_CulDSac     1.188818
23          LandSlope_Sev     2.931418
24   Neighborhood_BrkSide     1.181773
25   Neighborhood_Crawfor     1.164964
26   Neighborhood_Mitchel     1.149638
27   Neighborhood_NPkVill     1.208463
28   Neighborhood_NoRidge     1.453779
29   Neighborhood_NridgHt     1.804269
30   Neighborhood_Somerst     1.396299
31   Neighborhood_StoneBr     1.192957
32        Condition1_Norm     1.184495
33        Condition2_PosA     1.075347
34        Condition2_PosN     1.176350
35         BldgType_Twnhs     1.358603
36        BldgType_TwnhsE     1.588584
37      HouseStyle_1.5Unf     1.120720
38      HouseStyle_2.5Fin     1.169000
39      RoofStyle_Mansard     1.386109
40         RoofStyle_Shed     2.786640
41       RoofMatl_CompShg          inf
42       RoofMatl_Membran          inf
43         RoofMatl_Metal          inf
44          RoofMatl_Roll          inf
45       RoofMatl_Tar&Grv          inf
46       RoofMatl_WdShake          inf
47       RoofMatl_WdShngl          inf
48    Exterior1st_BrkFace     1.221708
49    Exterior1st_Plywood     1.482456
50    Exterior2nd_CmentBd     1.174711
51      Exterior2nd_Other          NaN
52           ExterCond_Po          NaN
53            BsmtQual_Fa     1.725713
54            BsmtQual_Gd     4.647214
55            BsmtQual_TA     6.233887
56            BsmtCond_Po     1.497348
57        BsmtExposure_Gd     1.494343
58       BsmtFinType2_BLQ     1.166714
59           Heating_OthW     1.077363
60         KitchenQual_Fa     2.142542
61         KitchenQual_Gd     6.762488
62         KitchenQual_TA     9.053770
63        Functional_Min1     2.269507
64        Functional_Min2     2.642423
65         Functional_Sev     1.321661
66         Functional_Typ     4.164745
67              PoolQC_Fa    16.896615
68              PoolQC_Gd          inf
69           PoolQC_Nonen  1304.541142
70      MiscFeature_Nonen   294.387571
71       MiscFeature_Othr    13.499025
72       MiscFeature_Shed   243.665164
73           SaleType_Con     1.053933
74           SaleType_New          inf
75  SaleCondition_Partial          inf

In [91]:

X_tr_sm.pop('MiscFeature_Shed')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.942
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     224.0
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:30   Log-Likelihood:                 2260.7
No. Observations:                1021   AIC:                            -4381.
Df Residuals:                     951   BIC:                            -4036.
Df Model:                          69                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.7018      0.435     -8.506      0.000      -4.556      -2.848
LotArea                   0.1721      0.026      6.528      0.000       0.120       0.224
OverallQual               0.0839      0.011      7.587      0.000       0.062       0.106
OverallCond               0.0582      0.008      6.934      0.000       0.042       0.075
YearBuilt                 0.0842      0.009      9.701      0.000       0.067       0.101
YearRemodAdd              0.0174      0.004      4.326      0.000       0.010       0.025
MasVnrArea                0.0445      0.009      4.812      0.000       0.026       0.063
BsmtFinSF1                0.1699      0.014     11.896      0.000       0.142       0.198
BsmtFinSF2                0.0268      0.009      3.146      0.002       0.010       0.044
BsmtUnfSF                 0.0282      0.007      4.313      0.000       0.015       0.041
TotalBsmtSF               0.1742      0.015     11.846      0.000       0.145       0.203
2ndFlrSF                  0.0402      0.011      3.652      0.000       0.019       0.062
GrLivArea                 0.4201      0.028     14.857      0.000       0.365       0.476
BsmtFullBath              0.0171      0.007      2.436      0.015       0.003       0.031
HalfBath                 -0.0120      0.005     -2.431      0.015      -0.022      -0.002
BedroomAbvGr             -0.0584      0.013     -4.670      0.000      -0.083      -0.034
KitchenAbvGr             -0.1065      0.013     -7.894      0.000      -0.133      -0.080
GarageArea                0.0390      0.008      4.778      0.000       0.023       0.055
WoodDeckSF                0.0121      0.007      1.798      0.072      -0.001       0.025
PoolArea                  5.7114      0.686      8.330      0.000       4.366       7.057
MiscVal                  -0.0177      0.027     -0.646      0.519      -0.072       0.036
Street_Pave               0.0401      0.015      2.736      0.006       0.011       0.069
LotConfig_CulDSac         0.0108      0.004      2.849      0.004       0.003       0.018
LandSlope_Sev            -0.0362      0.014     -2.505      0.012      -0.065      -0.008
Neighborhood_BrkSide      0.0116      0.005      2.386      0.017       0.002       0.021
Neighborhood_Crawfor      0.0362      0.005      6.828      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0163      0.005     -3.351      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0315      0.012      2.558      0.011       0.007       0.056
Neighborhood_NoRidge      0.0404      0.006      7.119      0.000       0.029       0.052
Neighborhood_NridgHt      0.0265      0.005      5.363      0.000       0.017       0.036
Neighborhood_Somerst      0.0208      0.004      4.832      0.000       0.012       0.029
Neighborhood_StoneBr   

In [92]:

X_tr_sm.pop('MiscFeature_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.942
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     227.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:31   Log-Likelihood:                 2260.3
No. Observations:                1021   AIC:                            -4383.
Df Residuals:                     952   BIC:                            -4043.
Df Model:                          68                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.7032      0.435     -8.511      0.000      -4.557      -2.849
LotArea                   0.1730      0.026      6.570      0.000       0.121       0.225
OverallQual               0.0838      0.011      7.588      0.000       0.062       0.106
OverallCond               0.0587      0.008      7.008      0.000       0.042       0.075
YearBuilt                 0.0844      0.009      9.740      0.000       0.067       0.101
YearRemodAdd              0.0172      0.004      4.278      0.000       0.009       0.025
MasVnrArea                0.0444      0.009      4.806      0.000       0.026       0.063
BsmtFinSF1                0.1693      0.014     11.873      0.000       0.141       0.197
BsmtFinSF2                0.0264      0.009      3.101      0.002       0.010       0.043
BsmtUnfSF                 0.0279      0.007      4.277      0.000       0.015       0.041
TotalBsmtSF               0.1735      0.015     11.821      0.000       0.145       0.202
2ndFlrSF                  0.0396      0.011      3.604      0.000       0.018       0.061
GrLivArea                 0.4209      0.028     14.898      0.000       0.365       0.476
BsmtFullBath              0.0170      0.007      2.423      0.016       0.003       0.031
HalfBath                 -0.0119      0.005     -2.400      0.017      -0.022      -0.002
BedroomAbvGr             -0.0585      0.013     -4.676      0.000      -0.083      -0.034
KitchenAbvGr             -0.1068      0.013     -7.923      0.000      -0.133      -0.080
GarageArea                0.0391      0.008      4.791      0.000       0.023       0.055
WoodDeckSF                0.0124      0.007      1.853      0.064      -0.001       0.026
PoolArea                  5.7101      0.686      8.329      0.000       4.365       7.055
MiscVal                  -0.0090      0.025     -0.354      0.723      -0.059       0.041
Street_Pave               0.0384      0.014      2.650      0.008       0.010       0.067
LotConfig_CulDSac         0.0106      0.004      2.792      0.005       0.003       0.018
LandSlope_Sev            -0.0361      0.014     -2.498      0.013      -0.064      -0.008
Neighborhood_BrkSide      0.0117      0.005      2.415      0.016       0.002       0.021
Neighborhood_Crawfor      0.0361      0.005      6.809      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0160      0.005     -3.310      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0315      0.012      2.558      0.011       0.007       0.056
Neighborhood_NoRidge      0.0404      0.006      7.116      0.000       0.029       0.052
Neighborhood_NridgHt      0.0265      0.005      5.364      0.000       0.017       0.036
Neighborhood_Somerst      0.0208      0.004      4.828      0.000       0.012       0.029
Neighborhood_StoneBr   

In [93]:

X_tr_sm.pop('MiscFeature_Othr')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.942
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     230.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:31   Log-Likelihood:                 2259.9
No. Observations:                1021   AIC:                            -4384.
Df Residuals:                     953   BIC:                            -4049.
Df Model:                          67                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.6980      0.435     -8.500      0.000      -4.552      -2.844
LotArea                   0.1734      0.026      6.584      0.000       0.122       0.225
OverallQual               0.0839      0.011      7.594      0.000       0.062       0.106
OverallCond               0.0593      0.008      7.094      0.000       0.043       0.076
YearBuilt                 0.0846      0.009      9.764      0.000       0.068       0.102
YearRemodAdd              0.0169      0.004      4.217      0.000       0.009       0.025
MasVnrArea                0.0444      0.009      4.807      0.000       0.026       0.063
BsmtFinSF1                0.1694      0.014     11.882      0.000       0.141       0.197
BsmtFinSF2                0.0264      0.009      3.098      0.002       0.010       0.043
BsmtUnfSF                 0.0279      0.007      4.271      0.000       0.015       0.041
TotalBsmtSF               0.1735      0.015     11.827      0.000       0.145       0.202
2ndFlrSF                  0.0399      0.011      3.631      0.000       0.018       0.061
GrLivArea                 0.4199      0.028     14.874      0.000       0.364       0.475
BsmtFullBath              0.0170      0.007      2.417      0.016       0.003       0.031
HalfBath                 -0.0119      0.005     -2.405      0.016      -0.022      -0.002
BedroomAbvGr             -0.0585      0.013     -4.679      0.000      -0.083      -0.034
KitchenAbvGr             -0.1059      0.013     -7.876      0.000      -0.132      -0.080
GarageArea                0.0389      0.008      4.766      0.000       0.023       0.055
WoodDeckSF                0.0124      0.007      1.852      0.064      -0.001       0.026
PoolArea                  5.7030      0.685      8.320      0.000       4.358       7.048
MiscVal                  -0.0060      0.025     -0.239      0.811      -0.055       0.043
Street_Pave               0.0387      0.014      2.670      0.008       0.010       0.067
LotConfig_CulDSac         0.0105      0.004      2.781      0.006       0.003       0.018
LandSlope_Sev            -0.0361      0.014     -2.497      0.013      -0.064      -0.008
Neighborhood_BrkSide      0.0116      0.005      2.385      0.017       0.002       0.021
Neighborhood_Crawfor      0.0361      0.005      6.805      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0161      0.005     -3.321      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0316      0.012      2.561      0.011       0.007       0.056
Neighborhood_NoRidge      0.0405      0.006      7.136      0.000       0.029       0.052
Neighborhood_NridgHt      0.0265      0.005      5.379      0.000       0.017       0.036
Neighborhood_Somerst      0.0209      0.004      4.846      0.000       0.012       0.029
Neighborhood_StoneBr   

In [94]:
X_tr_sm.pop('MiscVal')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.942
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     234.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:31   Log-Likelihood:                 2259.8
No. Observations:                1021   AIC:                            -4386.
Df Residuals:                     954   BIC:                            -4055.
Df Model:                          66                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.6982      0.435     -8.505      0.000      -4.552      -2.845
LotArea                   0.1728      0.026      6.593      0.000       0.121       0.224
OverallQual               0.0838      0.011      7.594      0.000       0.062       0.106
OverallCond               0.0591      0.008      7.099      0.000       0.043       0.075
YearBuilt                 0.0846      0.009      9.766      0.000       0.068       0.102
YearRemodAdd              0.0169      0.004      4.215      0.000       0.009       0.025
MasVnrArea                0.0445      0.009      4.811      0.000       0.026       0.063
BsmtFinSF1                0.1694      0.014     11.885      0.000       0.141       0.197
BsmtFinSF2                0.0264      0.009      3.098      0.002       0.010       0.043
BsmtUnfSF                 0.0279      0.007      4.280      0.000       0.015       0.041
TotalBsmtSF               0.1735      0.015     11.830      0.000       0.145       0.202
2ndFlrSF                  0.0399      0.011      3.631      0.000       0.018       0.061
GrLivArea                 0.4200      0.028     14.889      0.000       0.365       0.475
BsmtFullBath              0.0171      0.007      2.434      0.015       0.003       0.031
HalfBath                 -0.0119      0.005     -2.404      0.016      -0.022      -0.002
BedroomAbvGr             -0.0585      0.012     -4.679      0.000      -0.083      -0.034
KitchenAbvGr             -0.1061      0.013     -7.902      0.000      -0.132      -0.080
GarageArea                0.0389      0.008      4.771      0.000       0.023       0.055
WoodDeckSF                0.0124      0.007      1.855      0.064      -0.001       0.026
PoolArea                  5.7034      0.685      8.324      0.000       4.359       7.048
Street_Pave               0.0388      0.014      2.676      0.008       0.010       0.067
LotConfig_CulDSac         0.0104      0.004      2.772      0.006       0.003       0.018
LandSlope_Sev            -0.0357      0.014     -2.487      0.013      -0.064      -0.008
Neighborhood_BrkSide      0.0116      0.005      2.389      0.017       0.002       0.021
Neighborhood_Crawfor      0.0361      0.005      6.813      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0161      0.005     -3.317      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0316      0.012      2.564      0.010       0.007       0.056
Neighborhood_NoRidge      0.0405      0.006      7.140      0.000       0.029       0.052
Neighborhood_NridgHt      0.0265      0.005      5.381      0.000       0.017       0.036
Neighborhood_Somerst      0.0209      0.004      4.850      0.000       0.012       0.029
Neighborhood_StoneBr      0.0361      0.008      4.327      0.000       0.020       0.052
Condition1_Norm        

In [95]:
X_tr_sm.pop('RoofStyle_Shed')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.942
Model:                            OLS   Adj. R-squared:                  0.938
Method:                 Least Squares   F-statistic:                     237.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:31   Log-Likelihood:                 2258.7
No. Observations:                1021   AIC:                            -4385.
Df Residuals:                     955   BIC:                            -4060.
Df Model:                          65                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -3.6899      0.435     -8.482      0.000      -4.544      -2.836
LotArea                   0.1688      0.026      6.474      0.000       0.118       0.220
OverallQual               0.0834      0.011      7.552      0.000       0.062       0.105
OverallCond               0.0593      0.008      7.113      0.000       0.043       0.076
YearBuilt                 0.0845      0.009      9.749      0.000       0.067       0.101
YearRemodAdd              0.0168      0.004      4.201      0.000       0.009       0.025
MasVnrArea                0.0440      0.009      4.761      0.000       0.026       0.062
BsmtFinSF1                0.1712      0.014     12.051      0.000       0.143       0.199
BsmtFinSF2                0.0267      0.009      3.134      0.002       0.010       0.043
BsmtUnfSF                 0.0288      0.007      4.422      0.000       0.016       0.042
TotalBsmtSF               0.1755      0.015     12.021      0.000       0.147       0.204
2ndFlrSF                  0.0412      0.011      3.769      0.000       0.020       0.063
GrLivArea                 0.4169      0.028     14.815      0.000       0.362       0.472
BsmtFullBath              0.0170      0.007      2.422      0.016       0.003       0.031
HalfBath                 -0.0112      0.005     -2.281      0.023      -0.021      -0.002
BedroomAbvGr             -0.0596      0.012     -4.782      0.000      -0.084      -0.035
KitchenAbvGr             -0.1037      0.013     -7.780      0.000      -0.130      -0.078
GarageArea                0.0390      0.008      4.784      0.000       0.023       0.055
WoodDeckSF                0.0126      0.007      1.882      0.060      -0.001       0.026
PoolArea                  5.6897      0.685      8.301      0.000       4.345       7.035
Street_Pave               0.0391      0.014      2.701      0.007       0.011       0.068
LotConfig_CulDSac         0.0104      0.004      2.748      0.006       0.003       0.018
LandSlope_Sev            -0.0315      0.014     -2.240      0.025      -0.059      -0.004
Neighborhood_BrkSide      0.0116      0.005      2.384      0.017       0.002       0.021
Neighborhood_Crawfor      0.0362      0.005      6.828      0.000       0.026       0.047
Neighborhood_Mitchel     -0.0161      0.005     -3.326      0.001      -0.026      -0.007
Neighborhood_NPkVill      0.0309      0.012      2.506      0.012       0.007       0.055
Neighborhood_NoRidge      0.0406      0.006      7.149      0.000       0.029       0.052
Neighborhood_NridgHt      0.0266      0.005      5.401      0.000       0.017       0.036
Neighborhood_Somerst      0.0209      0.004      4.848      0.000       0.012       0.029
Neighborhood_StoneBr      0.0361      0.008      4.324      0.000       0.020       0.052
Condition1_Norm        

In [96]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data

Feature          VIF
0                   const     0.000000
1                 LotArea     2.146390
2             OverallQual     4.011049
3             OverallCond     1.760808
4               YearBuilt     4.929843
5            YearRemodAdd     2.574547
6              MasVnrArea     1.591497
7              BsmtFinSF1          inf
8              BsmtFinSF2          inf
9               BsmtUnfSF          inf
10            TotalBsmtSF          inf
11               2ndFlrSF     7.245510
12              GrLivArea    10.813394
13           BsmtFullBath     2.048895
14               HalfBath     2.072153
15           BedroomAbvGr     2.223618
16           KitchenAbvGr     1.421795
17             GarageArea     2.026936
18             WoodDeckSF     1.290042
19               PoolArea  1398.576376
20            Street_Pave     1.115899
21      LotConfig_CulDSac     1.168855
22          LandSlope_Sev     2.606213
23   Neighborhood_BrkSide     1.177210
24   Neighborhood_Crawfor     1.163429
25   Neighborhood_Mitchel     1.144762
26   Neighborhood_NPkVill     1.206046
27   Neighborhood_NoRidge     1.452466
28   Neighborhood_NridgHt     1.803285
29   Neighborhood_Somerst     1.395755
30   Neighborhood_StoneBr     1.192838
31        Condition1_Norm     1.181453
32        Condition2_PosA     1.075196
33        Condition2_PosN     1.174810
34         BldgType_Twnhs     1.350425
35        BldgType_TwnhsE     1.579553
36      HouseStyle_1.5Unf     1.118413
37      HouseStyle_2.5Fin     1.168496
38      RoofStyle_Mansard     1.310329
39       RoofMatl_CompShg          inf
40       RoofMatl_Membran          inf
41         RoofMatl_Metal          inf
42          RoofMatl_Roll          inf
43       RoofMatl_Tar&Grv          inf
44       RoofMatl_WdShake          inf
45       RoofMatl_WdShngl          inf
46    Exterior1st_BrkFace     1.217498
47    Exterior1st_Plywood     1.457910
48    Exterior2nd_CmentBd     1.174161
49      Exterior2nd_Other          NaN
50           ExterCond_Po          NaN
51            BsmtQual_Fa     1.715552
52            BsmtQual_Gd     4.617356
53            BsmtQual_TA     6.189586
54            BsmtCond_Po     1.447508
55        BsmtExposure_Gd     1.486943
56       BsmtFinType2_BLQ     1.163253
57           Heating_OthW     1.076948
58         KitchenQual_Fa     2.122833
59         KitchenQual_Gd     6.758900
60         KitchenQual_TA     9.043504
61        Functional_Min1     2.223713
62        Functional_Min2     2.572764
63         Functional_Sev     1.318838
64         Functional_Typ     3.984991
65              PoolQC_Fa    16.891958
66              PoolQC_Gd          inf
67           PoolQC_Nonen  1304.076244
68           SaleType_Con     1.053725
69           SaleType_New          inf
70  SaleCondition_Partial          inf

In [97]:
X_tr_sm.pop('PoolQC_Nonen')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.938
Model:                            OLS   Adj. R-squared:                  0.934
Method:                 Least Squares   F-statistic:                     225.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:32   Log-Likelihood:                 2224.9
No. Observations:                1021   AIC:                            -4320.
Df Residuals:                     956   BIC:                            -3999.
Df Model:                          64                                         
Covariance Type:            nonrobust                                         
=========================================================================================
                            coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------
const                    -0.1742      0.021     -8.493      0.000      -0.214      -0.134
LotArea                   0.1613      0.027      5.991      0.000       0.108       0.214
OverallQual               0.0786      0.011      6.898      0.000       0.056       0.101
OverallCond               0.0655      0.009      7.637      0.000       0.049       0.082
YearBuilt                 0.0914      0.009     10.266      0.000       0.074       0.109
YearRemodAdd              0.0150      0.004      3.630      0.000       0.007       0.023
MasVnrArea                0.0388      0.010      4.074      0.000       0.020       0.057
BsmtFinSF1                0.1787      0.015     12.204      0.000       0.150       0.207
BsmtFinSF2                0.0267      0.009      3.039      0.002       0.009       0.044
BsmtUnfSF                 0.0310      0.007      4.620      0.000       0.018       0.044
TotalBsmtSF               0.1834      0.015     12.181      0.000       0.154       0.213
2ndFlrSF                  0.0444      0.011      3.929      0.000       0.022       0.067
GrLivArea                 0.4183      0.029     14.387      0.000       0.361       0.475
BsmtFullBath              0.0154      0.007      2.134      0.033       0.001       0.030
HalfBath                 -0.0113      0.005     -2.219      0.027      -0.021      -0.001
BedroomAbvGr             -0.0632      0.013     -4.909      0.000      -0.088      -0.038
KitchenAbvGr             -0.1026      0.014     -7.455      0.000      -0.130      -0.076
GarageArea                0.0361      0.008      4.290      0.000       0.020       0.053
WoodDeckSF                0.0132      0.007      1.905      0.057      -0.000       0.027
PoolArea                  0.1493      0.030      5.040      0.000       0.091       0.207
Street_Pave               0.0380      0.015      2.535      0.011       0.009       0.067
LotConfig_CulDSac         0.0098      0.004      2.508      0.012       0.002       0.017
LandSlope_Sev            -0.0293      0.015     -2.021      0.044      -0.058      -0.001
Neighborhood_BrkSide      0.0121      0.005      2.411      0.016       0.002       0.022
Neighborhood_Crawfor      0.0369      0.005      6.740      0.000       0.026       0.048
Neighborhood_Mitchel     -0.0167      0.005     -3.334      0.001      -0.027      -0.007
Neighborhood_NPkVill      0.0298      0.013      2.343      0.019       0.005       0.055
Neighborhood_NoRidge      0.0454      0.006      7.779      0.000       0.034       0.057
Neighborhood_NridgHt      0.0257      0.005      5.038      0.000       0.016       0.036
Neighborhood_Somerst      0.0215      0.004      4.842      0.000       0.013       0.030
Neighborhood_StoneBr      0.0363      0.009      4.206      0.000       0.019       0.053
Condition1_Norm        

In [98]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data

Feature        VIF
0                   const   0.000000
1                 LotArea   2.143661
2             OverallQual   3.999417
3             OverallCond   1.745911
4               YearBuilt   4.881097
5            YearRemodAdd   2.566359
6              MasVnrArea   1.583817
7              BsmtFinSF1        inf
8              BsmtFinSF2        inf
9               BsmtUnfSF        inf
10            TotalBsmtSF        inf
11               2ndFlrSF   7.236382
12              GrLivArea  10.812991
13           BsmtFullBath   2.047405
14               HalfBath   2.072148
15           BedroomAbvGr   2.220830
16           KitchenAbvGr   1.421661
17             GarageArea   2.022997
18             WoodDeckSF   1.289898
19               PoolArea   2.445916
20            Street_Pave   1.115786
21      LotConfig_CulDSac   1.168410
22          LandSlope_Sev   2.605294
23   Neighborhood_BrkSide   1.177007
24   Neighborhood_Crawfor   1.163111
25   Neighborhood_Mitchel   1.144519
26   Neighborhood_NPkVill   1.205910
27   Neighborhood_NoRidge   1.436646
28   Neighborhood_NridgHt   1.802209
29   Neighborhood_Somerst   1.395255
30   Neighborhood_StoneBr   1.192830
31        Condition1_Norm   1.178039
32        Condition2_PosA   1.074807
33        Condition2_PosN   1.174614
34         BldgType_Twnhs   1.350421
35        BldgType_TwnhsE   1.579500
36      HouseStyle_1.5Unf   1.118303
37      HouseStyle_2.5Fin   1.168464
38      RoofStyle_Mansard   1.310015
39       RoofMatl_CompShg        inf
40       RoofMatl_Membran        inf
41         RoofMatl_Metal        inf
42          RoofMatl_Roll        inf
43       RoofMatl_Tar&Grv        inf
44       RoofMatl_WdShake        inf
45       RoofMatl_WdShngl        inf
46    Exterior1st_BrkFace   1.217491
47    Exterior1st_Plywood   1.457783
48    Exterior2nd_CmentBd   1.173545
49      Exterior2nd_Other        NaN
50           ExterCond_Po        NaN
51            BsmtQual_Fa   1.715113
52            BsmtQual_Gd   4.596559
53            BsmtQual_TA   6.167823
54            BsmtCond_Po   1.447475
55        BsmtExposure_Gd   1.486441
56       BsmtFinType2_BLQ   1.163206
57           Heating_OthW   1.076505
58         KitchenQual_Fa   2.121300
59         KitchenQual_Gd   6.720071
60         KitchenQual_TA   9.026342
61        Functional_Min1   2.223711
62        Functional_Min2   2.572729
63         Functional_Sev   1.318838
64         Functional_Typ   3.984832
65              PoolQC_Fa   1.880491
66              PoolQC_Gd        inf
67           SaleType_Con   1.053717
68           SaleType_New        inf
69  SaleCondition_Partial        inf

In [99]:
X_tr_sm.pop('SaleCondition_Partial')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.938
Model:                            OLS   Adj. R-squared:                  0.934
Method:                 Least Squares   F-statistic:                     225.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:33   Log-Likelihood:                 2224.9
No. Observations:                1021   AIC:                            -4320.
Df Residuals:                     956   BIC:                            -3999.
Df Model:                          64                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1742      0.021     -8.493      0.000      -0.214      -0.134
LotArea                  0.1613      0.027      5.991      0.000       0.108       0.214
OverallQual              0.0786      0.011      6.898      0.000       0.056       0.101
OverallCond              0.0655      0.009      7.637      0.000       0.049       0.082
YearBuilt                0.0914      0.009     10.266      0.000       0.074       0.109
YearRemodAdd             0.0150      0.004      3.630      0.000       0.007       0.023
MasVnrArea               0.0388      0.010      4.074      0.000       0.020       0.057
BsmtFinSF1               0.1787      0.015     12.204      0.000       0.150       0.207
BsmtFinSF2               0.0267      0.009      3.039      0.002       0.009       0.044
BsmtUnfSF                0.0310      0.007      4.620      0.000       0.018       0.044
TotalBsmtSF              0.1834      0.015     12.181      0.000       0.154       0.213
2ndFlrSF                 0.0444      0.011      3.929      0.000       0.022       0.067
GrLivArea                0.4183      0.029     14.387      0.000       0.361       0.475
BsmtFullBath             0.0154      0.007      2.134      0.033       0.001       0.030
HalfBath                -0.0113      0.005     -2.219      0.027      -0.021      -0.001
BedroomAbvGr            -0.0632      0.013     -4.909      0.000      -0.088      -0.038
KitchenAbvGr            -0.1026      0.014     -7.455      0.000      -0.130      -0.076
GarageArea               0.0361      0.008      4.290      0.000       0.020       0.053
WoodDeckSF               0.0132      0.007      1.905      0.057      -0.000       0.027
PoolArea                 0.1493      0.030      5.040      0.000       0.091       0.207
Street_Pave              0.0380      0.015      2.535      0.011       0.009       0.067
LotConfig_CulDSac        0.0098      0.004      2.508      0.012       0.002       0.017
LandSlope_Sev           -0.0293      0.015     -2.021      0.044      -0.058      -0.001
Neighborhood_BrkSide     0.0121      0.005      2.411      0.016       0.002       0.022
Neighborhood_Crawfor     0.0369      0.005      6.740      0.000       0.026       0.048
Neighborhood_Mitchel    -0.0167      0.005     -3.334      0.001      -0.027      -0.007
Neighborhood_NPkVill     0.0298      0.013      2.343      0.019       0.005       0.055
Neighborhood_NoRidge     0.0454      0.006      7.779      0.000       0.034       0.057
Neighborhood_NridgHt     0.0257      0.005      5.038      0.000       0.016       0.036
Neighborhood_Somerst     0.0215      0.004      4.842      0.000       0.013       0.030
Neighborhood_StoneBr     0.0363      0.009      4.206      0.000       0.019       0.053
Condition1_Norm          0.0148      0.003      5.428    

In [100]:
X_tr_sm.pop('ExterCond_Po')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.938
Model:                            OLS   Adj. R-squared:                  0.934
Method:                 Least Squares   F-statistic:                     225.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:33   Log-Likelihood:                 2224.9
No. Observations:                1021   AIC:                            -4320.
Df Residuals:                     956   BIC:                            -3999.
Df Model:                          64                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1742      0.021     -8.493      0.000      -0.214      -0.134
LotArea                  0.1613      0.027      5.991      0.000       0.108       0.214
OverallQual              0.0786      0.011      6.898      0.000       0.056       0.101
OverallCond              0.0655      0.009      7.637      0.000       0.049       0.082
YearBuilt                0.0914      0.009     10.266      0.000       0.074       0.109
YearRemodAdd             0.0150      0.004      3.630      0.000       0.007       0.023
MasVnrArea               0.0388      0.010      4.074      0.000       0.020       0.057
BsmtFinSF1               0.1787      0.015     12.204      0.000       0.150       0.207
BsmtFinSF2               0.0267      0.009      3.039      0.002       0.009       0.044
BsmtUnfSF                0.0310      0.007      4.620      0.000       0.018       0.044
TotalBsmtSF              0.1834      0.015     12.181      0.000       0.154       0.213
2ndFlrSF                 0.0444      0.011      3.929      0.000       0.022       0.067
GrLivArea                0.4183      0.029     14.387      0.000       0.361       0.475
BsmtFullBath             0.0154      0.007      2.134      0.033       0.001       0.030
HalfBath                -0.0113      0.005     -2.219      0.027      -0.021      -0.001
BedroomAbvGr            -0.0632      0.013     -4.909      0.000      -0.088      -0.038
KitchenAbvGr            -0.1026      0.014     -7.455      0.000      -0.130      -0.076
GarageArea               0.0361      0.008      4.290      0.000       0.020       0.053
WoodDeckSF               0.0132      0.007      1.905      0.057      -0.000       0.027
PoolArea                 0.1493      0.030      5.040      0.000       0.091       0.207
Street_Pave              0.0380      0.015      2.535      0.011       0.009       0.067
LotConfig_CulDSac        0.0098      0.004      2.508      0.012       0.002       0.017
LandSlope_Sev           -0.0293      0.015     -2.021      0.044      -0.058      -0.001
Neighborhood_BrkSide     0.0121      0.005      2.411      0.016       0.002       0.022
Neighborhood_Crawfor     0.0369      0.005      6.740      0.000       0.026       0.048
Neighborhood_Mitchel    -0.0167      0.005     -3.334      0.001      -0.027      -0.007
Neighborhood_NPkVill     0.0298      0.013      2.343      0.019       0.005       0.055
Neighborhood_NoRidge     0.0454      0.006      7.779      0.000       0.034       0.057
Neighborhood_NridgHt     0.0257      0.005      5.038      0.000       0.016       0.036
Neighborhood_Somerst     0.0215      0.004      4.842      0.000       0.013       0.030
Neighborhood_StoneBr     0.0363      0.009      4.206      0.000       0.019       0.053
Condition1_Norm          0.0148      0.003      5.428    

In [101]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data

Feature        VIF
0                  const   0.000000
1                LotArea   2.143661
2            OverallQual   3.999417
3            OverallCond   1.745911
4              YearBuilt   4.881097
5           YearRemodAdd   2.566359
6             MasVnrArea   1.583817
7             BsmtFinSF1        inf
8             BsmtFinSF2        inf
9              BsmtUnfSF        inf
10           TotalBsmtSF        inf
11              2ndFlrSF   7.236382
12             GrLivArea  10.812991
13          BsmtFullBath   2.047405
14              HalfBath   2.072148
15          BedroomAbvGr   2.220830
16          KitchenAbvGr   1.421661
17            GarageArea   2.022997
18            WoodDeckSF   1.289898
19              PoolArea   2.445916
20           Street_Pave   1.115786
21     LotConfig_CulDSac   1.168410
22         LandSlope_Sev   2.605294
23  Neighborhood_BrkSide   1.177007
24  Neighborhood_Crawfor   1.163111
25  Neighborhood_Mitchel   1.144519
26  Neighborhood_NPkVill   1.205910
27  Neighborhood_NoRidge   1.436646
28  Neighborhood_NridgHt   1.802209
29  Neighborhood_Somerst   1.395255
30  Neighborhood_StoneBr   1.192830
31       Condition1_Norm   1.178039
32       Condition2_PosA   1.074807
33       Condition2_PosN   1.174614
34        BldgType_Twnhs   1.350421
35       BldgType_TwnhsE   1.579500
36     HouseStyle_1.5Unf   1.118303
37     HouseStyle_2.5Fin   1.168464
38     RoofStyle_Mansard   1.310015
39      RoofMatl_CompShg        inf
40      RoofMatl_Membran        inf
41        RoofMatl_Metal        inf
42         RoofMatl_Roll        inf
43      RoofMatl_Tar&Grv        inf
44      RoofMatl_WdShake        inf
45      RoofMatl_WdShngl        inf
46   Exterior1st_BrkFace   1.217491
47   Exterior1st_Plywood   1.457783
48   Exterior2nd_CmentBd   1.173545
49     Exterior2nd_Other        NaN
50           BsmtQual_Fa   1.715113
51           BsmtQual_Gd   4.596559
52           BsmtQual_TA   6.167823
53           BsmtCond_Po   1.447475
54       BsmtExposure_Gd   1.486441
55      BsmtFinType2_BLQ   1.163206
56          Heating_OthW   1.076505
57        KitchenQual_Fa   2.121300
58        KitchenQual_Gd   6.720071
59        KitchenQual_TA   9.026342
60       Functional_Min1   2.223711
61       Functional_Min2   2.572729
62        Functional_Sev   1.318838
63        Functional_Typ   3.984832
64             PoolQC_Fa   1.880491
65             PoolQC_Gd        inf
66          SaleType_Con   1.053717
67          SaleType_New   1.480453

In [102]:
X_tr_sm.pop('PoolQC_Gd')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.938
Model:                            OLS   Adj. R-squared:                  0.934
Method:                 Least Squares   F-statistic:                     225.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:34   Log-Likelihood:                 2224.9
No. Observations:                1021   AIC:                            -4320.
Df Residuals:                     956   BIC:                            -3999.
Df Model:                          64                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -1.1238      0.043    -26.083      0.000      -1.208      -1.039
LotArea                  0.1613      0.027      5.991      0.000       0.108       0.214
OverallQual              0.0786      0.011      6.898      0.000       0.056       0.101
OverallCond              0.0655      0.009      7.637      0.000       0.049       0.082
YearBuilt                0.0914      0.009     10.266      0.000       0.074       0.109
YearRemodAdd             0.0150      0.004      3.630      0.000       0.007       0.023
MasVnrArea               0.0388      0.010      4.074      0.000       0.020       0.057
BsmtFinSF1               0.1787      0.015     12.204      0.000       0.150       0.207
BsmtFinSF2               0.0267      0.009      3.039      0.002       0.009       0.044
BsmtUnfSF                0.0310      0.007      4.620      0.000       0.018       0.044
TotalBsmtSF              0.1834      0.015     12.181      0.000       0.154       0.213
2ndFlrSF                 0.0444      0.011      3.929      0.000       0.022       0.067
GrLivArea                0.4183      0.029     14.387      0.000       0.361       0.475
BsmtFullBath             0.0154      0.007      2.134      0.033       0.001       0.030
HalfBath                -0.0113      0.005     -2.219      0.027      -0.021      -0.001
BedroomAbvGr            -0.0632      0.013     -4.909      0.000      -0.088      -0.038
KitchenAbvGr            -0.1026      0.014     -7.455      0.000      -0.130      -0.076
GarageArea               0.0361      0.008      4.290      0.000       0.020       0.053
WoodDeckSF               0.0132      0.007      1.905      0.057      -0.000       0.027
PoolArea                 0.1493      0.030      5.040      0.000       0.091       0.207
Street_Pave              0.0380      0.015      2.535      0.011       0.009       0.067
LotConfig_CulDSac        0.0098      0.004      2.508      0.012       0.002       0.017
LandSlope_Sev           -0.0293      0.015     -2.021      0.044      -0.058      -0.001
Neighborhood_BrkSide     0.0121      0.005      2.411      0.016       0.002       0.022
Neighborhood_Crawfor     0.0369      0.005      6.740      0.000       0.026       0.048
Neighborhood_Mitchel    -0.0167      0.005     -3.334      0.001      -0.027      -0.007
Neighborhood_NPkVill     0.0298      0.013      2.343      0.019       0.005       0.055
Neighborhood_NoRidge     0.0454      0.006      7.779      0.000       0.034       0.057
Neighborhood_NridgHt     0.0257      0.005      5.038      0.000       0.016       0.036
Neighborhood_Somerst     0.0215      0.004      4.842      0.000       0.013       0.030
Neighborhood_StoneBr     0.0363      0.009      4.206      0.000       0.019       0.053
Condition1_Norm          0.0148      0.003      5.428    

In [103]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data

Feature          VIF
0                  const  2367.823244
1                LotArea     2.143661
2            OverallQual     3.999417
3            OverallCond     1.745911
4              YearBuilt     4.881097
5           YearRemodAdd     2.566359
6             MasVnrArea     1.583817
7             BsmtFinSF1          inf
8             BsmtFinSF2          inf
9              BsmtUnfSF          inf
10           TotalBsmtSF          inf
11              2ndFlrSF     7.236382
12             GrLivArea    10.812991
13          BsmtFullBath     2.047405
14              HalfBath     2.072148
15          BedroomAbvGr     2.220830
16          KitchenAbvGr     1.421661
17            GarageArea     2.022997
18            WoodDeckSF     1.289898
19              PoolArea     2.445916
20           Street_Pave     1.115786
21     LotConfig_CulDSac     1.168410
22         LandSlope_Sev     2.605294
23  Neighborhood_BrkSide     1.177007
24  Neighborhood_Crawfor     1.163111
25  Neighborhood_Mitchel     1.144519
26  Neighborhood_NPkVill     1.205910
27  Neighborhood_NoRidge     1.436646
28  Neighborhood_NridgHt     1.802209
29  Neighborhood_Somerst     1.395255
30  Neighborhood_StoneBr     1.192830
31       Condition1_Norm     1.178039
32       Condition2_PosA     1.074807
33       Condition2_PosN     1.174614
34        BldgType_Twnhs     1.350421
35       BldgType_TwnhsE     1.579500
36     HouseStyle_1.5Unf     1.118303
37     HouseStyle_2.5Fin     1.168464
38     RoofStyle_Mansard     1.310015
39      RoofMatl_CompShg    30.955623
40      RoofMatl_Membran     3.202052
41        RoofMatl_Metal     3.145871
42         RoofMatl_Roll     2.752227
43      RoofMatl_Tar&Grv    11.965582
44      RoofMatl_WdShake     8.399552
45      RoofMatl_WdShngl     7.792312
46   Exterior1st_BrkFace     1.217491
47   Exterior1st_Plywood     1.457783
48   Exterior2nd_CmentBd     1.173545
49     Exterior2nd_Other          NaN
50           BsmtQual_Fa     1.715113
51           BsmtQual_Gd     4.596559
52           BsmtQual_TA     6.167823
53           BsmtCond_Po     1.447475
54       BsmtExposure_Gd     1.486441
55      BsmtFinType2_BLQ     1.163206
56          Heating_OthW     1.076505
57        KitchenQual_Fa     2.121300
58        KitchenQual_Gd     6.720071
59        KitchenQual_TA     9.026342
60       Functional_Min1     2.223711
61       Functional_Min2     2.572729
62        Functional_Sev     1.318838
63        Functional_Typ     3.984832
64             PoolQC_Fa     1.880491
65          SaleType_Con     1.053717
66          SaleType_New     1.480453

In [104]:
X_tr_sm.pop('RoofStyle_Mansard')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.938
Model:                            OLS   Adj. R-squared:                  0.934
Method:                 Least Squares   F-statistic:                     228.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:35   Log-Likelihood:                 2223.2
No. Observations:                1021   AIC:                            -4318.
Df Residuals:                     957   BIC:                            -4003.
Df Model:                          63                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -1.1230      0.043    -26.038      0.000      -1.208      -1.038
LotArea                  0.1641      0.027      6.099      0.000       0.111       0.217
OverallQual              0.0788      0.011      6.906      0.000       0.056       0.101
OverallCond              0.0649      0.009      7.563      0.000       0.048       0.082
YearBuilt                0.0896      0.009     10.118      0.000       0.072       0.107
YearRemodAdd             0.0156      0.004      3.777      0.000       0.007       0.024
MasVnrArea               0.0390      0.010      4.095      0.000       0.020       0.058
BsmtFinSF1               0.1791      0.015     12.218      0.000       0.150       0.208
BsmtFinSF2               0.0266      0.009      3.026      0.003       0.009       0.044
BsmtUnfSF                0.0314      0.007      4.680      0.000       0.018       0.045
TotalBsmtSF              0.1839      0.015     12.203      0.000       0.154       0.213
2ndFlrSF                 0.0445      0.011      3.936      0.000       0.022       0.067
GrLivArea                0.4160      0.029     14.308      0.000       0.359       0.473
BsmtFullBath             0.0148      0.007      2.049      0.041       0.001       0.029
HalfBath                -0.0103      0.005     -2.041      0.042      -0.020      -0.000
BedroomAbvGr            -0.0614      0.013     -4.775      0.000      -0.087      -0.036
KitchenAbvGr            -0.1022      0.014     -7.417      0.000      -0.129      -0.075
GarageArea               0.0361      0.008      4.280      0.000       0.020       0.053
WoodDeckSF               0.0137      0.007      1.972      0.049    6.84e-05       0.027
PoolArea                 0.1493      0.030      5.037      0.000       0.091       0.208
Street_Pave              0.0376      0.015      2.509      0.012       0.008       0.067
LotConfig_CulDSac        0.0097      0.004      2.499      0.013       0.002       0.017
LandSlope_Sev           -0.0320      0.014     -2.217      0.027      -0.060      -0.004
Neighborhood_BrkSide     0.0118      0.005      2.360      0.018       0.002       0.022
Neighborhood_Crawfor     0.0367      0.005      6.695      0.000       0.026       0.047
Neighborhood_Mitchel    -0.0158      0.005     -3.178      0.002      -0.026      -0.006
Neighborhood_NPkVill     0.0298      0.013      2.339      0.020       0.005       0.055
Neighborhood_NoRidge     0.0453      0.006      7.757      0.000       0.034       0.057
Neighborhood_NridgHt     0.0257      0.005      5.048      0.000       0.016       0.036
Neighborhood_Somerst     0.0215      0.004      4.834      0.000       0.013       0.030
Neighborhood_StoneBr     0.0363      0.009      4.209      0.000       0.019       0.053
Condition1_Norm          0.0146      0.003      5.365    

In [105]:
X_tr_sm.pop('BsmtFinType2_BLQ')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.937
Model:                            OLS   Adj. R-squared:                  0.933
Method:                 Least Squares   F-statistic:                     231.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:35   Log-Likelihood:                 2221.7
No. Observations:                1021   AIC:                            -4317.
Df Residuals:                     958   BIC:                            -4007.
Df Model:                          62                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -1.1250      0.043    -26.067      0.000      -1.210      -1.040
LotArea                  0.1620      0.027      6.022      0.000       0.109       0.215
OverallQual              0.0798      0.011      7.005      0.000       0.057       0.102
OverallCond              0.0639      0.009      7.462      0.000       0.047       0.081
YearBuilt                0.0896      0.009     10.113      0.000       0.072       0.107
YearRemodAdd             0.0156      0.004      3.791      0.000       0.008       0.024
MasVnrArea               0.0385      0.010      4.039      0.000       0.020       0.057
BsmtFinSF1               0.1797      0.015     12.249      0.000       0.151       0.208
BsmtFinSF2               0.0235      0.009      2.724      0.007       0.007       0.040
BsmtUnfSF                0.0314      0.007      4.669      0.000       0.018       0.045
TotalBsmtSF              0.1836      0.015     12.175      0.000       0.154       0.213
2ndFlrSF                 0.0446      0.011      3.942      0.000       0.022       0.067
GrLivArea                0.4146      0.029     14.250      0.000       0.357       0.472
BsmtFullBath             0.0142      0.007      1.960      0.050   -1.96e-05       0.028
HalfBath                -0.0101      0.005     -1.995      0.046      -0.020      -0.000
BedroomAbvGr            -0.0619      0.013     -4.810      0.000      -0.087      -0.037
KitchenAbvGr            -0.1012      0.014     -7.343      0.000      -0.128      -0.074
GarageArea               0.0357      0.008      4.227      0.000       0.019       0.052
WoodDeckSF               0.0138      0.007      1.984      0.048       0.000       0.027
PoolArea                 0.1504      0.030      5.069      0.000       0.092       0.209
Street_Pave              0.0394      0.015      2.630      0.009       0.010       0.069
LotConfig_CulDSac        0.0099      0.004      2.533      0.011       0.002       0.018
LandSlope_Sev           -0.0325      0.014     -2.250      0.025      -0.061      -0.004
Neighborhood_BrkSide     0.0123      0.005      2.443      0.015       0.002       0.022
Neighborhood_Crawfor     0.0371      0.005      6.760      0.000       0.026       0.048
Neighborhood_Mitchel    -0.0157      0.005     -3.144      0.002      -0.025      -0.006
Neighborhood_NPkVill     0.0299      0.013      2.349      0.019       0.005       0.055
Neighborhood_NoRidge     0.0455      0.006      7.786      0.000       0.034       0.057
Neighborhood_NridgHt     0.0259      0.005      5.080      0.000       0.016       0.036
Neighborhood_Somerst     0.0215      0.004      4.819      0.000       0.013       0.030
Neighborhood_StoneBr     0.0356      0.009      4.127      0.000       0.019       0.053
Condition1_Norm          0.0146      0.003      5.366    

In [106]:

from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data = vif_data[vif_data['VIF'] >5]
vif_data

Feature          VIF
0              const  2365.864180
7         BsmtFinSF1          inf
8         BsmtFinSF2          inf
9          BsmtUnfSF          inf
10       TotalBsmtSF          inf
11          2ndFlrSF     7.235842
12         GrLivArea    10.783335
38  RoofMatl_CompShg    30.949624
42  RoofMatl_Tar&Grv    11.965147
43  RoofMatl_WdShake     8.143293
44  RoofMatl_WdShngl     7.791651
51       BsmtQual_TA     6.164024
56    KitchenQual_Gd     6.702368
57    KitchenQual_TA     9.015753

In [107]:
X_tr_sm.pop('BsmtFinSF1')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.937
Model:                            OLS   Adj. R-squared:                  0.933
Method:                 Least Squares   F-statistic:                     231.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:36   Log-Likelihood:                 2221.7
No. Observations:                1021   AIC:                            -4317.
Df Residuals:                     958   BIC:                            -4007.
Df Model:                          62                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -1.1250      0.043    -26.067      0.000      -1.210      -1.040
LotArea                  0.1620      0.027      6.022      0.000       0.109       0.215
OverallQual              0.0798      0.011      7.005      0.000       0.057       0.102
OverallCond              0.0639      0.009      7.462      0.000       0.047       0.081
YearBuilt                0.0896      0.009     10.113      0.000       0.072       0.107
YearRemodAdd             0.0156      0.004      3.791      0.000       0.008       0.024
MasVnrArea               0.0385      0.010      4.039      0.000       0.020       0.057
BsmtFinSF2              -0.0235      0.009     -2.686      0.007      -0.041      -0.006
BsmtUnfSF               -0.0430      0.008     -5.622      0.000      -0.058      -0.028
TotalBsmtSF              0.3781      0.031     12.293      0.000       0.318       0.438
2ndFlrSF                 0.0446      0.011      3.942      0.000       0.022       0.067
GrLivArea                0.4146      0.029     14.250      0.000       0.357       0.472
BsmtFullBath             0.0142      0.007      1.960      0.050   -1.96e-05       0.028
HalfBath                -0.0101      0.005     -1.995      0.046      -0.020      -0.000
BedroomAbvGr            -0.0619      0.013     -4.810      0.000      -0.087      -0.037
KitchenAbvGr            -0.1012      0.014     -7.343      0.000      -0.128      -0.074
GarageArea               0.0357      0.008      4.227      0.000       0.019       0.052
WoodDeckSF               0.0138      0.007      1.984      0.048       0.000       0.027
PoolArea                 0.1504      0.030      5.069      0.000       0.092       0.209
Street_Pave              0.0394      0.015      2.630      0.009       0.010       0.069
LotConfig_CulDSac        0.0099      0.004      2.533      0.011       0.002       0.018
LandSlope_Sev           -0.0325      0.014     -2.250      0.025      -0.061      -0.004
Neighborhood_BrkSide     0.0123      0.005      2.443      0.015       0.002       0.022
Neighborhood_Crawfor     0.0371      0.005      6.760      0.000       0.026       0.048
Neighborhood_Mitchel    -0.0157      0.005     -3.144      0.002      -0.025      -0.006
Neighborhood_NPkVill     0.0299      0.013      2.349      0.019       0.005       0.055
Neighborhood_NoRidge     0.0455      0.006      7.786      0.000       0.034       0.057
Neighborhood_NridgHt     0.0259      0.005      5.080      0.000       0.016       0.036
Neighborhood_Somerst     0.0215      0.004      4.819      0.000       0.013       0.030
Neighborhood_StoneBr     0.0356      0.009      4.127      0.000       0.019       0.053
Condition1_Norm          0.0146      0.003      5.366      0.000       0.009       0.020
Condition2_PosA          0.0877      0.029      2.982    

In [108]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data = vif_data[vif_data['VIF'] >5]
vif_data

Feature          VIF
0              const  2365.864180
9        TotalBsmtSF     6.777707
10          2ndFlrSF     7.235842
11         GrLivArea    10.783335
37  RoofMatl_CompShg    30.949624
41  RoofMatl_Tar&Grv    11.965147
42  RoofMatl_WdShake     8.143293
43  RoofMatl_WdShngl     7.791651
50       BsmtQual_TA     6.164024
55    KitchenQual_Gd     6.702368
56    KitchenQual_TA     9.015753

In [109]:

X_tr_sm.pop('RoofMatl_CompShg')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.881
Method:                 Least Squares   F-statistic:                     125.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:37   Log-Likelihood:                 1926.6
No. Observations:                1021   AIC:                            -3729.
Df Residuals:                     959   BIC:                            -3424.
Df Model:                          61                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0914      0.028     -3.277      0.001      -0.146      -0.037
LotArea                  0.0966      0.036      2.701      0.007       0.026       0.167
OverallQual              0.1172      0.015      7.765      0.000       0.088       0.147
OverallCond              0.0492      0.011      4.316      0.000       0.027       0.072
YearBuilt                0.0924      0.012      7.816      0.000       0.069       0.116
YearRemodAdd             0.0171      0.006      3.099      0.002       0.006       0.028
MasVnrArea               0.0253      0.013      1.993      0.047       0.000       0.050
BsmtFinSF2               0.0019      0.012      0.167      0.867      -0.021       0.025
BsmtUnfSF               -0.0056      0.010     -0.559      0.576      -0.025       0.014
TotalBsmtSF              0.1303      0.039      3.321      0.001       0.053       0.207
2ndFlrSF                 0.0234      0.015      1.551      0.121      -0.006       0.053
GrLivArea                0.3995      0.039     10.294      0.000       0.323       0.476
BsmtFullBath             0.0388      0.010      4.056      0.000       0.020       0.058
HalfBath                -0.0130      0.007     -1.919      0.055      -0.026       0.000
BedroomAbvGr            -0.0336      0.017     -1.963      0.050      -0.067   -4.91e-06
KitchenAbvGr            -0.0980      0.018     -5.329      0.000      -0.134      -0.062
GarageArea               0.0358      0.011      3.179      0.002       0.014       0.058
WoodDeckSF               0.0188      0.009      2.032      0.042       0.001       0.037
PoolArea                -0.1738      0.036     -4.786      0.000      -0.245      -0.103
Street_Pave              0.0411      0.020      2.057      0.040       0.002       0.080
LotConfig_CulDSac        0.0143      0.005      2.748      0.006       0.004       0.024
LandSlope_Sev           -0.0023      0.019     -0.118      0.906      -0.040       0.035
Neighborhood_BrkSide     0.0099      0.007      1.483      0.138      -0.003       0.023
Neighborhood_Crawfor     0.0431      0.007      5.888      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0119      0.007     -1.783      0.075      -0.025       0.001
Neighborhood_NPkVill     0.0294      0.017      1.726      0.085      -0.004       0.063
Neighborhood_NoRidge     0.0707      0.008      9.187      0.000       0.056       0.086
Neighborhood_NridgHt     0.0428      0.007      6.325      0.000       0.029       0.056
Neighborhood_Somerst     0.0252      0.006      4.244      0.000       0.014       0.037
Neighborhood_StoneBr     0.0441      0.012      3.834      0.000       0.022       0.067
Condition1_Norm          0.0167      0.004      4.591      0.000       0.010       0.024
Condition2_PosA          0.0939      0.039      2.395    

In [110]:
X_tr_sm.pop('BsmtFinSF2')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     127.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:37   Log-Likelihood:                 1926.6
No. Observations:                1021   AIC:                            -3731.
Df Residuals:                     960   BIC:                            -3431.
Df Model:                          60                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0912      0.028     -3.274      0.001      -0.146      -0.037
LotArea                  0.0966      0.036      2.704      0.007       0.026       0.167
OverallQual              0.1172      0.015      7.767      0.000       0.088       0.147
OverallCond              0.0492      0.011      4.317      0.000       0.027       0.072
YearBuilt                0.0924      0.012      7.819      0.000       0.069       0.116
YearRemodAdd             0.0171      0.006      3.102      0.002       0.006       0.028
MasVnrArea               0.0251      0.013      1.987      0.047       0.000       0.050
BsmtUnfSF               -0.0060      0.010     -0.617      0.537      -0.025       0.013
TotalBsmtSF              0.1312      0.039      3.385      0.001       0.055       0.207
2ndFlrSF                 0.0233      0.015      1.548      0.122      -0.006       0.053
GrLivArea                0.3998      0.039     10.315      0.000       0.324       0.476
BsmtFullBath             0.0388      0.010      4.055      0.000       0.020       0.058
HalfBath                -0.0130      0.007     -1.919      0.055      -0.026       0.000
BedroomAbvGr            -0.0336      0.017     -1.963      0.050      -0.067   -3.44e-06
KitchenAbvGr            -0.0981      0.018     -5.346      0.000      -0.134      -0.062
GarageArea               0.0357      0.011      3.178      0.002       0.014       0.058
WoodDeckSF               0.0189      0.009      2.043      0.041       0.001       0.037
PoolArea                -0.1743      0.036     -4.823      0.000      -0.245      -0.103
Street_Pave              0.0409      0.020      2.053      0.040       0.002       0.080
LotConfig_CulDSac        0.0143      0.005      2.749      0.006       0.004       0.024
LandSlope_Sev           -0.0022      0.019     -0.115      0.909      -0.040       0.036
Neighborhood_BrkSide     0.0099      0.007      1.479      0.139      -0.003       0.023
Neighborhood_Crawfor     0.0430      0.007      5.889      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0119      0.007     -1.795      0.073      -0.025       0.001
Neighborhood_NPkVill     0.0294      0.017      1.728      0.084      -0.004       0.063
Neighborhood_NoRidge     0.0707      0.008      9.197      0.000       0.056       0.086
Neighborhood_NridgHt     0.0428      0.007      6.328      0.000       0.029       0.056
Neighborhood_Somerst     0.0252      0.006      4.247      0.000       0.014       0.037
Neighborhood_StoneBr     0.0442      0.012      3.842      0.000       0.022       0.067
Condition1_Norm          0.0167      0.004      4.592      0.000       0.010       0.024
Condition2_PosA          0.0938      0.039      2.394      0.017       0.017       0.171
Condition2_PosN         -0.5129      0.041    -12.608    

In [111]:
X_tr_sm.pop('RoofMatl_Tar&Grv')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     129.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:38   Log-Likelihood:                 1926.6
No. Observations:                1021   AIC:                            -3733.
Df Residuals:                     961   BIC:                            -3438.
Df Model:                          59                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0912      0.028     -3.276      0.001      -0.146      -0.037
LotArea                  0.0965      0.036      2.705      0.007       0.026       0.167
OverallQual              0.1172      0.015      7.774      0.000       0.088       0.147
OverallCond              0.0492      0.011      4.322      0.000       0.027       0.072
YearBuilt                0.0924      0.012      7.822      0.000       0.069       0.116
YearRemodAdd             0.0171      0.006      3.103      0.002       0.006       0.028
MasVnrArea               0.0251      0.013      1.987      0.047       0.000       0.050
BsmtUnfSF               -0.0060      0.010     -0.617      0.537      -0.025       0.013
TotalBsmtSF              0.1312      0.039      3.387      0.001       0.055       0.207
2ndFlrSF                 0.0233      0.015      1.549      0.122      -0.006       0.053
GrLivArea                0.3999      0.039     10.325      0.000       0.324       0.476
BsmtFullBath             0.0388      0.010      4.057      0.000       0.020       0.058
HalfBath                -0.0130      0.007     -1.923      0.055      -0.026       0.000
BedroomAbvGr            -0.0336      0.017     -1.966      0.050      -0.067   -6.44e-05
KitchenAbvGr            -0.0982      0.018     -5.358      0.000      -0.134      -0.062
GarageArea               0.0358      0.011      3.182      0.002       0.014       0.058
WoodDeckSF               0.0189      0.009      2.044      0.041       0.001       0.037
PoolArea                -0.1743      0.036     -4.826      0.000      -0.245      -0.103
Street_Pave              0.0410      0.020      2.059      0.040       0.002       0.080
LotConfig_CulDSac        0.0143      0.005      2.768      0.006       0.004       0.024
LandSlope_Sev           -0.0021      0.019     -0.109      0.913      -0.040       0.035
Neighborhood_BrkSide     0.0099      0.007      1.479      0.140      -0.003       0.023
Neighborhood_Crawfor     0.0430      0.007      5.892      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0119      0.007     -1.799      0.072      -0.025       0.001
Neighborhood_NPkVill     0.0293      0.017      1.727      0.084      -0.004       0.063
Neighborhood_NoRidge     0.0707      0.008      9.202      0.000       0.056       0.086
Neighborhood_NridgHt     0.0428      0.007      6.333      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.250      0.000       0.014       0.037
Neighborhood_StoneBr     0.0442      0.011      3.844      0.000       0.022       0.067
Condition1_Norm          0.0167      0.004      4.604      0.000       0.010       0.024
Condition2_PosA          0.0939      0.039      2.396      0.017       0.017       0.171
Condition2_PosN         -0.5129      0.041    -12.615    

In [112]:
X_tr_sm.pop('LandSlope_Sev')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     132.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:38   Log-Likelihood:                 1926.6
No. Observations:                1021   AIC:                            -3735.
Df Residuals:                     962   BIC:                            -3444.
Df Model:                          58                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0912      0.028     -3.279      0.001      -0.146      -0.037
LotArea                  0.0944      0.030      3.198      0.001       0.036       0.152
OverallQual              0.1171      0.015      7.778      0.000       0.088       0.147
OverallCond              0.0492      0.011      4.326      0.000       0.027       0.072
YearBuilt                0.0924      0.012      7.833      0.000       0.069       0.116
YearRemodAdd             0.0171      0.005      3.103      0.002       0.006       0.028
MasVnrArea               0.0251      0.013      1.989      0.047       0.000       0.050
BsmtUnfSF               -0.0060      0.010     -0.618      0.537      -0.025       0.013
TotalBsmtSF              0.1310      0.039      3.387      0.001       0.055       0.207
2ndFlrSF                 0.0232      0.015      1.547      0.122      -0.006       0.053
GrLivArea                0.4003      0.038     10.404      0.000       0.325       0.476
BsmtFullBath             0.0388      0.010      4.062      0.000       0.020       0.058
HalfBath                -0.0130      0.007     -1.927      0.054      -0.026       0.000
BedroomAbvGr            -0.0335      0.017     -1.965      0.050      -0.067   -4.39e-05
KitchenAbvGr            -0.0982      0.018     -5.365      0.000      -0.134      -0.062
GarageArea               0.0358      0.011      3.185      0.001       0.014       0.058
WoodDeckSF               0.0188      0.009      2.044      0.041       0.001       0.037
PoolArea                -0.1741      0.036     -4.828      0.000      -0.245      -0.103
Street_Pave              0.0411      0.020      2.064      0.039       0.002       0.080
LotConfig_CulDSac        0.0143      0.005      2.768      0.006       0.004       0.024
Neighborhood_BrkSide     0.0099      0.007      1.478      0.140      -0.003       0.023
Neighborhood_Crawfor     0.0430      0.007      5.897      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0119      0.007     -1.797      0.073      -0.025       0.001
Neighborhood_NPkVill     0.0294      0.017      1.736      0.083      -0.004       0.063
Neighborhood_NoRidge     0.0707      0.008      9.206      0.000       0.056       0.086
Neighborhood_NridgHt     0.0428      0.007      6.336      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.251      0.000       0.014       0.037
Neighborhood_StoneBr     0.0442      0.011      3.845      0.000       0.022       0.067
Condition1_Norm          0.0167      0.004      4.610      0.000       0.010       0.024
Condition2_PosA          0.0939      0.039      2.397      0.017       0.017       0.171
Condition2_PosN         -0.5127      0.041    -12.626      0.000      -0.592      -0.433
BldgType_Twnhs          -0.0467      0.007     -6.300    

In [113]:
X_tr_sm.pop('RoofMatl_Metal')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     134.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:38   Log-Likelihood:                 1926.6
No. Observations:                1021   AIC:                            -3737.
Df Residuals:                     963   BIC:                            -3451.
Df Model:                          57                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0913      0.028     -3.283      0.001      -0.146      -0.037
LotArea                  0.0944      0.029      3.200      0.001       0.036       0.152
OverallQual              0.1172      0.015      7.792      0.000       0.088       0.147
OverallCond              0.0492      0.011      4.327      0.000       0.027       0.071
YearBuilt                0.0925      0.012      7.841      0.000       0.069       0.116
YearRemodAdd             0.0171      0.005      3.105      0.002       0.006       0.028
MasVnrArea               0.0251      0.013      1.988      0.047       0.000       0.050
BsmtUnfSF               -0.0060      0.010     -0.618      0.537      -0.025       0.013
TotalBsmtSF              0.1309      0.039      3.387      0.001       0.055       0.207
2ndFlrSF                 0.0232      0.015      1.553      0.121      -0.006       0.053
GrLivArea                0.4002      0.038     10.409      0.000       0.325       0.476
BsmtFullBath             0.0388      0.010      4.065      0.000       0.020       0.058
HalfBath                -0.0130      0.007     -1.933      0.054      -0.026       0.000
BedroomAbvGr            -0.0337      0.017     -1.980      0.048      -0.067      -0.000
KitchenAbvGr            -0.0982      0.018     -5.366      0.000      -0.134      -0.062
GarageArea               0.0358      0.011      3.190      0.001       0.014       0.058
WoodDeckSF               0.0187      0.009      2.042      0.041       0.001       0.037
PoolArea                -0.1741      0.036     -4.829      0.000      -0.245      -0.103
Street_Pave              0.0411      0.020      2.068      0.039       0.002       0.080
LotConfig_CulDSac        0.0144      0.005      2.805      0.005       0.004       0.024
Neighborhood_BrkSide     0.0099      0.007      1.478      0.140      -0.003       0.023
Neighborhood_Crawfor     0.0430      0.007      5.901      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0119      0.007     -1.805      0.071      -0.025       0.001
Neighborhood_NPkVill     0.0294      0.017      1.734      0.083      -0.004       0.063
Neighborhood_NoRidge     0.0707      0.008      9.213      0.000       0.056       0.086
Neighborhood_NridgHt     0.0428      0.007      6.341      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.254      0.000       0.014       0.037
Neighborhood_StoneBr     0.0442      0.011      3.846      0.000       0.022       0.067
Condition1_Norm          0.0167      0.004      4.616      0.000       0.010       0.024
Condition2_PosA          0.0939      0.039      2.398      0.017       0.017       0.171
Condition2_PosN         -0.5127      0.041    -12.632      0.000      -0.592      -0.433
BldgType_Twnhs          -0.0467      0.007     -6.306    

In [114]:
X_tr_sm.pop('RoofMatl_Roll')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     137.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:38   Log-Likelihood:                 1926.6
No. Observations:                1021   AIC:                            -3739.
Df Residuals:                     964   BIC:                            -3458.
Df Model:                          56                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0914      0.028     -3.291      0.001      -0.146      -0.037
LotArea                  0.0945      0.029      3.205      0.001       0.037       0.152
OverallQual              0.1172      0.015      7.794      0.000       0.088       0.147
OverallCond              0.0492      0.011      4.329      0.000       0.027       0.071
YearBuilt                0.0926      0.012      7.857      0.000       0.069       0.116
YearRemodAdd             0.0170      0.005      3.099      0.002       0.006       0.028
MasVnrArea               0.0254      0.013      2.022      0.043       0.001       0.050
BsmtUnfSF               -0.0060      0.010     -0.617      0.537      -0.025       0.013
TotalBsmtSF              0.1312      0.039      3.399      0.001       0.055       0.207
2ndFlrSF                 0.0236      0.015      1.579      0.115      -0.006       0.053
GrLivArea                0.3998      0.038     10.411      0.000       0.324       0.475
BsmtFullBath             0.0388      0.010      4.065      0.000       0.020       0.057
HalfBath                -0.0131      0.007     -1.954      0.051      -0.026    5.52e-05
BedroomAbvGr            -0.0338      0.017     -1.988      0.047      -0.067      -0.000
KitchenAbvGr            -0.0976      0.018     -5.373      0.000      -0.133      -0.062
GarageArea               0.0358      0.011      3.189      0.001       0.014       0.058
WoodDeckSF               0.0187      0.009      2.041      0.042       0.001       0.037
PoolArea                -0.1742      0.036     -4.834      0.000      -0.245      -0.103
Street_Pave              0.0411      0.020      2.070      0.039       0.002       0.080
LotConfig_CulDSac        0.0144      0.005      2.806      0.005       0.004       0.024
Neighborhood_BrkSide     0.0098      0.007      1.477      0.140      -0.003       0.023
Neighborhood_Crawfor     0.0430      0.007      5.904      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0120      0.007     -1.810      0.071      -0.025       0.001
Neighborhood_NPkVill     0.0294      0.017      1.737      0.083      -0.004       0.063
Neighborhood_NoRidge     0.0706      0.008      9.214      0.000       0.056       0.086
Neighborhood_NridgHt     0.0427      0.007      6.341      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.252      0.000       0.014       0.037
Neighborhood_StoneBr     0.0442      0.011      3.848      0.000       0.022       0.067
Condition1_Norm          0.0166      0.004      4.610      0.000       0.010       0.024
Condition2_PosA          0.0939      0.039      2.400      0.017       0.017       0.171
Condition2_PosN         -0.5129      0.041    -12.645      0.000      -0.592      -0.433
BldgType_Twnhs          -0.0467      0.007     -6.313    

In [115]:
X_tr_sm.pop('RoofMatl_WdShake')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     139.7
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:38   Log-Likelihood:                 1926.4
No. Observations:                1021   AIC:                            -3741.
Df Residuals:                     965   BIC:                            -3465.
Df Model:                          55                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0918      0.028     -3.306      0.001      -0.146      -0.037
LotArea                  0.0945      0.029      3.206      0.001       0.037       0.152
OverallQual              0.1174      0.015      7.817      0.000       0.088       0.147
OverallCond              0.0495      0.011      4.365      0.000       0.027       0.072
YearBuilt                0.0926      0.012      7.860      0.000       0.069       0.116
YearRemodAdd             0.0168      0.005      3.071      0.002       0.006       0.028
MasVnrArea               0.0252      0.013      2.006      0.045       0.001       0.050
BsmtUnfSF               -0.0060      0.010     -0.615      0.539      -0.025       0.013
TotalBsmtSF              0.1284      0.038      3.357      0.001       0.053       0.203
2ndFlrSF                 0.0222      0.015      1.510      0.131      -0.007       0.051
GrLivArea                0.4046      0.037     10.834      0.000       0.331       0.478
BsmtFullBath             0.0390      0.010      4.090      0.000       0.020       0.058
HalfBath                -0.0130      0.007     -1.935      0.053      -0.026       0.000
BedroomAbvGr            -0.0348      0.017     -2.061      0.040      -0.068      -0.002
KitchenAbvGr            -0.0980      0.018     -5.405      0.000      -0.134      -0.062
GarageArea               0.0356      0.011      3.175      0.002       0.014       0.058
WoodDeckSF               0.0186      0.009      2.027      0.043       0.001       0.037
PoolArea                -0.1751      0.036     -4.866      0.000      -0.246      -0.104
Street_Pave              0.0412      0.020      2.077      0.038       0.002       0.080
LotConfig_CulDSac        0.0143      0.005      2.785      0.005       0.004       0.024
Neighborhood_BrkSide     0.0098      0.007      1.468      0.142      -0.003       0.023
Neighborhood_Crawfor     0.0428      0.007      5.883      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0119      0.007     -1.800      0.072      -0.025       0.001
Neighborhood_NPkVill     0.0295      0.017      1.741      0.082      -0.004       0.063
Neighborhood_NoRidge     0.0704      0.008      9.201      0.000       0.055       0.085
Neighborhood_NridgHt     0.0427      0.007      6.341      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.250      0.000       0.014       0.037
Neighborhood_StoneBr     0.0440      0.011      3.834      0.000       0.021       0.066
Condition1_Norm          0.0165      0.004      4.590      0.000       0.009       0.024
Condition2_PosA          0.0931      0.039      2.382      0.017       0.016       0.170
Condition2_PosN         -0.5138      0.041    -12.685      0.000      -0.593      -0.434
BldgType_Twnhs          -0.0467      0.007     -6.315    

In [116]:
X_tr_sm.pop('BsmtUnfSF')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     142.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:39   Log-Likelihood:                 1926.2
No. Observations:                1021   AIC:                            -3742.
Df Residuals:                     966   BIC:                            -3471.
Df Model:                          54                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0922      0.028     -3.323      0.001      -0.147      -0.038
LotArea                  0.0948      0.029      3.221      0.001       0.037       0.153
OverallQual              0.1166      0.015      7.797      0.000       0.087       0.146
OverallCond              0.0506      0.011      4.521      0.000       0.029       0.073
YearBuilt                0.0935      0.012      8.000      0.000       0.071       0.116
YearRemodAdd             0.0165      0.005      3.028      0.003       0.006       0.027
MasVnrArea               0.0257      0.013      2.056      0.040       0.001       0.050
TotalBsmtSF              0.1185      0.035      3.416      0.001       0.050       0.187
2ndFlrSF                 0.0221      0.015      1.505      0.133      -0.007       0.051
GrLivArea                0.4054      0.037     10.864      0.000       0.332       0.479
BsmtFullBath             0.0424      0.008      5.525      0.000       0.027       0.057
HalfBath                -0.0128      0.007     -1.906      0.057      -0.026       0.000
BedroomAbvGr            -0.0359      0.017     -2.138      0.033      -0.069      -0.003
KitchenAbvGr            -0.0986      0.018     -5.442      0.000      -0.134      -0.063
GarageArea               0.0356      0.011      3.176      0.002       0.014       0.058
WoodDeckSF               0.0188      0.009      2.055      0.040       0.001       0.037
PoolArea                -0.1707      0.035     -4.842      0.000      -0.240      -0.101
Street_Pave              0.0414      0.020      2.087      0.037       0.002       0.080
LotConfig_CulDSac        0.0143      0.005      2.792      0.005       0.004       0.024
Neighborhood_BrkSide     0.0096      0.007      1.440      0.150      -0.003       0.023
Neighborhood_Crawfor     0.0431      0.007      5.943      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0118      0.007     -1.792      0.074      -0.025       0.001
Neighborhood_NPkVill     0.0297      0.017      1.756      0.079      -0.003       0.063
Neighborhood_NoRidge     0.0704      0.008      9.212      0.000       0.055       0.085
Neighborhood_NridgHt     0.0427      0.007      6.335      0.000       0.029       0.056
Neighborhood_Somerst     0.0252      0.006      4.252      0.000       0.014       0.037
Neighborhood_StoneBr     0.0441      0.011      3.847      0.000       0.022       0.067
Condition1_Norm          0.0165      0.004      4.574      0.000       0.009       0.024
Condition2_PosA          0.0925      0.039      2.368      0.018       0.016       0.169
Condition2_PosN         -0.5126      0.040    -12.675      0.000      -0.592      -0.433
BldgType_Twnhs          -0.0467      0.007     -6.318      0.000      -0.061      -0.032
BldgType_TwnhsE         -0.0293      0.006     -5.307    

In [117]:
X_tr_sm.pop('HouseStyle_1.5Unf')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     145.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:39   Log-Likelihood:                 1925.8
No. Observations:                1021   AIC:                            -3744.
Df Residuals:                     967   BIC:                            -3477.
Df Model:                          53                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0918      0.028     -3.310      0.001      -0.146      -0.037
LotArea                  0.0953      0.029      3.239      0.001       0.038       0.153
OverallQual              0.1180      0.015      7.945      0.000       0.089       0.147
OverallCond              0.0506      0.011      4.522      0.000       0.029       0.073
YearBuilt                0.0931      0.012      7.975      0.000       0.070       0.116
YearRemodAdd             0.0162      0.005      2.977      0.003       0.006       0.027
MasVnrArea               0.0257      0.013      2.052      0.040       0.001       0.050
TotalBsmtSF              0.1191      0.035      3.434      0.001       0.051       0.187
2ndFlrSF                 0.0221      0.015      1.507      0.132      -0.007       0.051
GrLivArea                0.4031      0.037     10.831      0.000       0.330       0.476
BsmtFullBath             0.0421      0.008      5.486      0.000       0.027       0.057
HalfBath                -0.0127      0.007     -1.891      0.059      -0.026       0.000
BedroomAbvGr            -0.0370      0.017     -2.211      0.027      -0.070      -0.004
KitchenAbvGr            -0.0975      0.018     -5.396      0.000      -0.133      -0.062
GarageArea               0.0351      0.011      3.137      0.002       0.013       0.057
WoodDeckSF               0.0186      0.009      2.033      0.042       0.001       0.037
PoolArea                -0.1699      0.035     -4.821      0.000      -0.239      -0.101
Street_Pave              0.0416      0.020      2.094      0.036       0.003       0.081
LotConfig_CulDSac        0.0142      0.005      2.786      0.005       0.004       0.024
Neighborhood_BrkSide     0.0105      0.007      1.594      0.111      -0.002       0.023
Neighborhood_Crawfor     0.0433      0.007      5.970      0.000       0.029       0.058
Neighborhood_Mitchel    -0.0119      0.007     -1.796      0.073      -0.025       0.001
Neighborhood_NPkVill     0.0297      0.017      1.756      0.079      -0.003       0.063
Neighborhood_NoRidge     0.0707      0.008      9.256      0.000       0.056       0.086
Neighborhood_NridgHt     0.0427      0.007      6.335      0.000       0.029       0.056
Neighborhood_Somerst     0.0251      0.006      4.245      0.000       0.014       0.037
Neighborhood_StoneBr     0.0439      0.011      3.834      0.000       0.021       0.066
Condition1_Norm          0.0163      0.004      4.536      0.000       0.009       0.023
Condition2_PosA          0.0919      0.039      2.353      0.019       0.015       0.168
Condition2_PosN         -0.5119      0.040    -12.661      0.000      -0.591      -0.433
BldgType_Twnhs          -0.0469      0.007     -6.345      0.000      -0.061      -0.032
BldgType_TwnhsE         -0.0295      0.006     -5.360    

In [118]:
X_tr_sm.pop('Exterior1st_Plywood')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     147.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:39   Log-Likelihood:                 1925.4
No. Observations:                1021   AIC:                            -3745.
Df Residuals:                     968   BIC:                            -3484.
Df Model:                          52                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0912      0.028     -3.288      0.001      -0.146      -0.037
LotArea                  0.0930      0.029      3.172      0.002       0.035       0.151
OverallQual              0.1194      0.015      8.074      0.000       0.090       0.148
OverallCond              0.0503      0.011      4.498      0.000       0.028       0.072
YearBuilt                0.0927      0.012      7.948      0.000       0.070       0.116
YearRemodAdd             0.0166      0.005      3.061      0.002       0.006       0.027
MasVnrArea               0.0256      0.013      2.045      0.041       0.001       0.050
TotalBsmtSF              0.1233      0.034      3.586      0.000       0.056       0.191
2ndFlrSF                 0.0248      0.014      1.719      0.086      -0.004       0.053
GrLivArea                0.3961      0.036     10.864      0.000       0.325       0.468
BsmtFullBath             0.0417      0.008      5.449      0.000       0.027       0.057
HalfBath                -0.0132      0.007     -1.969      0.049      -0.026   -4.68e-05
BedroomAbvGr            -0.0369      0.017     -2.204      0.028      -0.070      -0.004
KitchenAbvGr            -0.0981      0.018     -5.435      0.000      -0.134      -0.063
GarageArea               0.0348      0.011      3.108      0.002       0.013       0.057
WoodDeckSF               0.0188      0.009      2.053      0.040       0.001       0.037
PoolArea                -0.1686      0.035     -4.789      0.000      -0.238      -0.100
Street_Pave              0.0415      0.020      2.089      0.037       0.003       0.080
LotConfig_CulDSac        0.0141      0.005      2.752      0.006       0.004       0.024
Neighborhood_BrkSide     0.0107      0.007      1.625      0.104      -0.002       0.024
Neighborhood_Crawfor     0.0434      0.007      5.981      0.000       0.029       0.058
Neighborhood_Mitchel    -0.0122      0.007     -1.849      0.065      -0.025       0.001
Neighborhood_NPkVill     0.0251      0.016      1.553      0.121      -0.007       0.057
Neighborhood_NoRidge     0.0713      0.008      9.381      0.000       0.056       0.086
Neighborhood_NridgHt     0.0429      0.007      6.371      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.264      0.000       0.014       0.037
Neighborhood_StoneBr     0.0443      0.011      3.870      0.000       0.022       0.067
Condition1_Norm          0.0164      0.004      4.557      0.000       0.009       0.023
Condition2_PosA          0.0920      0.039      2.356      0.019       0.015       0.169
Condition2_PosN         -0.5103      0.040    -12.634      0.000      -0.590      -0.431
BldgType_Twnhs          -0.0470      0.007     -6.362      0.000      -0.062      -0.033
BldgType_TwnhsE         -0.0298      0.005     -5.411    

In [119]:

X_tr_sm.pop('Exterior2nd_Other')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     147.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:39   Log-Likelihood:                 1925.4
No. Observations:                1021   AIC:                            -3745.
Df Residuals:                     968   BIC:                            -3484.
Df Model:                          52                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0912      0.028     -3.288      0.001      -0.146      -0.037
LotArea                  0.0930      0.029      3.172      0.002       0.035       0.151
OverallQual              0.1194      0.015      8.074      0.000       0.090       0.148
OverallCond              0.0503      0.011      4.498      0.000       0.028       0.072
YearBuilt                0.0927      0.012      7.948      0.000       0.070       0.116
YearRemodAdd             0.0166      0.005      3.061      0.002       0.006       0.027
MasVnrArea               0.0256      0.013      2.045      0.041       0.001       0.050
TotalBsmtSF              0.1233      0.034      3.586      0.000       0.056       0.191
2ndFlrSF                 0.0248      0.014      1.719      0.086      -0.004       0.053
GrLivArea                0.3961      0.036     10.864      0.000       0.325       0.468
BsmtFullBath             0.0417      0.008      5.449      0.000       0.027       0.057
HalfBath                -0.0132      0.007     -1.969      0.049      -0.026   -4.68e-05
BedroomAbvGr            -0.0369      0.017     -2.204      0.028      -0.070      -0.004
KitchenAbvGr            -0.0981      0.018     -5.435      0.000      -0.134      -0.063
GarageArea               0.0348      0.011      3.108      0.002       0.013       0.057
WoodDeckSF               0.0188      0.009      2.053      0.040       0.001       0.037
PoolArea                -0.1686      0.035     -4.789      0.000      -0.238      -0.100
Street_Pave              0.0415      0.020      2.089      0.037       0.003       0.080
LotConfig_CulDSac        0.0141      0.005      2.752      0.006       0.004       0.024
Neighborhood_BrkSide     0.0107      0.007      1.625      0.104      -0.002       0.024
Neighborhood_Crawfor     0.0434      0.007      5.981      0.000       0.029       0.058
Neighborhood_Mitchel    -0.0122      0.007     -1.849      0.065      -0.025       0.001
Neighborhood_NPkVill     0.0251      0.016      1.553      0.121      -0.007       0.057
Neighborhood_NoRidge     0.0713      0.008      9.381      0.000       0.056       0.086
Neighborhood_NridgHt     0.0429      0.007      6.371      0.000       0.030       0.056
Neighborhood_Somerst     0.0252      0.006      4.264      0.000       0.014       0.037
Neighborhood_StoneBr     0.0443      0.011      3.870      0.000       0.022       0.067
Condition1_Norm          0.0164      0.004      4.557      0.000       0.009       0.023
Condition2_PosA          0.0920      0.039      2.356      0.019       0.015       0.169
Condition2_PosN         -0.5103      0.040    -12.634      0.000      -0.590      -0.431
BldgType_Twnhs          -0.0470      0.007     -6.362      0.000      -0.062      -0.033
BldgType_TwnhsE         -0.0298      0.005     -5.411    

In [120]:
X_tr_sm.pop('BsmtCond_Po')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     150.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:39   Log-Likelihood:                 1924.8
No. Observations:                1021   AIC:                            -3746.
Df Residuals:                     969   BIC:                            -3489.
Df Model:                          51                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0879      0.028     -3.192      0.001      -0.142      -0.034
LotArea                  0.0926      0.029      3.159      0.002       0.035       0.150
OverallQual              0.1177      0.015      8.013      0.000       0.089       0.146
OverallCond              0.0492      0.011      4.418      0.000       0.027       0.071
YearBuilt                0.0927      0.012      7.946      0.000       0.070       0.116
YearRemodAdd             0.0167      0.005      3.085      0.002       0.006       0.027
MasVnrArea               0.0259      0.013      2.071      0.039       0.001       0.050
TotalBsmtSF              0.1226      0.034      3.567      0.000       0.055       0.190
2ndFlrSF                 0.0244      0.014      1.692      0.091      -0.004       0.053
GrLivArea                0.3969      0.036     10.887      0.000       0.325       0.468
BsmtFullBath             0.0419      0.008      5.476      0.000       0.027       0.057
HalfBath                -0.0126      0.007     -1.890      0.059      -0.026       0.000
BedroomAbvGr            -0.0376      0.017     -2.251      0.025      -0.070      -0.005
KitchenAbvGr            -0.0989      0.018     -5.484      0.000      -0.134      -0.064
GarageArea               0.0343      0.011      3.068      0.002       0.012       0.056
WoodDeckSF               0.0188      0.009      2.053      0.040       0.001       0.037
PoolArea                -0.1679      0.035     -4.770      0.000      -0.237      -0.099
Street_Pave              0.0420      0.020      2.116      0.035       0.003       0.081
LotConfig_CulDSac        0.0141      0.005      2.765      0.006       0.004       0.024
Neighborhood_BrkSide     0.0105      0.007      1.603      0.109      -0.002       0.023
Neighborhood_Crawfor     0.0435      0.007      6.007      0.000       0.029       0.058
Neighborhood_Mitchel    -0.0121      0.007     -1.843      0.066      -0.025       0.001
Neighborhood_NPkVill     0.0255      0.016      1.575      0.116      -0.006       0.057
Neighborhood_NoRidge     0.0715      0.008      9.405      0.000       0.057       0.086
Neighborhood_NridgHt     0.0432      0.007      6.426      0.000       0.030       0.056
Neighborhood_Somerst     0.0255      0.006      4.306      0.000       0.014       0.037
Neighborhood_StoneBr     0.0445      0.011      3.890      0.000       0.022       0.067
Condition1_Norm          0.0164      0.004      4.564      0.000       0.009       0.023
Condition2_PosA          0.0932      0.039      2.390      0.017       0.017       0.170
Condition2_PosN         -0.5104      0.040    -12.636      0.000      -0.590      -0.431
BldgType_Twnhs          -0.0474      0.007     -6.423      0.000      -0.062      -0.033
BldgType_TwnhsE         -0.0300      0.005     -5.453    

In [121]:
X_tr_sm.pop('SaleType_Con')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     153.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:40   Log-Likelihood:                 1923.7
No. Observations:                1021   AIC:                            -3745.
Df Residuals:                     970   BIC:                            -3494.
Df Model:                          50                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0883      0.028     -3.206      0.001      -0.142      -0.034
LotArea                  0.0911      0.029      3.106      0.002       0.034       0.149
OverallQual              0.1181      0.015      8.037      0.000       0.089       0.147
OverallCond              0.0489      0.011      4.396      0.000       0.027       0.071
YearBuilt                0.0926      0.012      7.932      0.000       0.070       0.115
YearRemodAdd             0.0167      0.005      3.090      0.002       0.006       0.027
MasVnrArea               0.0254      0.013      2.028      0.043       0.001       0.050
TotalBsmtSF              0.1226      0.034      3.563      0.000       0.055       0.190
2ndFlrSF                 0.0245      0.014      1.696      0.090      -0.004       0.053
GrLivArea                0.3970      0.036     10.883      0.000       0.325       0.469
BsmtFullBath             0.0423      0.008      5.529      0.000       0.027       0.057
HalfBath                -0.0122      0.007     -1.825      0.068      -0.025       0.001
BedroomAbvGr            -0.0382      0.017     -2.282      0.023      -0.071      -0.005
KitchenAbvGr            -0.0986      0.018     -5.462      0.000      -0.134      -0.063
GarageArea               0.0342      0.011      3.055      0.002       0.012       0.056
WoodDeckSF               0.0189      0.009      2.065      0.039       0.001       0.037
PoolArea                -0.1676      0.035     -4.758      0.000      -0.237      -0.098
Street_Pave              0.0419      0.020      2.109      0.035       0.003       0.081
LotConfig_CulDSac        0.0147      0.005      2.876      0.004       0.005       0.025
Neighborhood_BrkSide     0.0106      0.007      1.612      0.107      -0.002       0.023
Neighborhood_Crawfor     0.0434      0.007      5.982      0.000       0.029       0.058
Neighborhood_Mitchel    -0.0123      0.007     -1.860      0.063      -0.025       0.001
Neighborhood_NPkVill     0.0252      0.016      1.558      0.120      -0.007       0.057
Neighborhood_NoRidge     0.0713      0.008      9.371      0.000       0.056       0.086
Neighborhood_NridgHt     0.0433      0.007      6.443      0.000       0.030       0.057
Neighborhood_Somerst     0.0261      0.006      4.426      0.000       0.015       0.038
Neighborhood_StoneBr     0.0441      0.011      3.852      0.000       0.022       0.067
Condition1_Norm          0.0165      0.004      4.586      0.000       0.009       0.024
Condition2_PosA          0.0930      0.039      2.383      0.017       0.016       0.170
Condition2_PosN         -0.5100      0.040    -12.619      0.000      -0.589      -0.431
BldgType_Twnhs          -0.0477      0.007     -6.457      0.000      -0.062      -0.033
BldgType_TwnhsE         -0.0297      0.005     -5.397    

In [122]:
X_tr_sm.pop('Neighborhood_NPkVill')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.888
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     156.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:40   Log-Likelihood:                 1922.5
No. Observations:                1021   AIC:                            -3745.
Df Residuals:                     971   BIC:                            -3498.
Df Model:                          49                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0890      0.028     -3.231      0.001      -0.143      -0.035
LotArea                  0.0907      0.029      3.091      0.002       0.033       0.148
OverallQual              0.1184      0.015      8.055      0.000       0.090       0.147
OverallCond              0.0494      0.011      4.436      0.000       0.028       0.071
YearBuilt                0.0921      0.012      7.891      0.000       0.069       0.115
YearRemodAdd             0.0164      0.005      3.020      0.003       0.006       0.027
MasVnrArea               0.0240      0.012      1.922      0.055      -0.001       0.049
TotalBsmtSF              0.1249      0.034      3.631      0.000       0.057       0.192
2ndFlrSF                 0.0248      0.014      1.715      0.087      -0.004       0.053
GrLivArea                0.3957      0.036     10.844      0.000       0.324       0.467
BsmtFullBath             0.0418      0.008      5.467      0.000       0.027       0.057
HalfBath                -0.0119      0.007     -1.786      0.074      -0.025       0.001
BedroomAbvGr            -0.0368      0.017     -2.200      0.028      -0.070      -0.004
KitchenAbvGr            -0.0992      0.018     -5.492      0.000      -0.135      -0.064
GarageArea               0.0353      0.011      3.163      0.002       0.013       0.057
WoodDeckSF               0.0187      0.009      2.041      0.042       0.001       0.037
PoolArea                -0.1685      0.035     -4.781      0.000      -0.238      -0.099
Street_Pave              0.0418      0.020      2.103      0.036       0.003       0.081
LotConfig_CulDSac        0.0147      0.005      2.872      0.004       0.005       0.025
Neighborhood_BrkSide     0.0104      0.007      1.590      0.112      -0.002       0.023
Neighborhood_Crawfor     0.0431      0.007      5.938      0.000       0.029       0.057
Neighborhood_Mitchel    -0.0124      0.007     -1.886      0.060      -0.025       0.001
Neighborhood_NoRidge     0.0713      0.008      9.363      0.000       0.056       0.086
Neighborhood_NridgHt     0.0427      0.007      6.355      0.000       0.030       0.056
Neighborhood_Somerst     0.0255      0.006      4.332      0.000       0.014       0.037
Neighborhood_StoneBr     0.0429      0.011      3.755      0.000       0.021       0.065
Condition1_Norm          0.0166      0.004      4.619      0.000       0.010       0.024
Condition2_PosA          0.0924      0.039      2.364      0.018       0.016       0.169
Condition2_PosN         -0.5094      0.040    -12.596      0.000      -0.589      -0.430
BldgType_Twnhs          -0.0464      0.007     -6.318      0.000      -0.061      -0.032
BldgType_TwnhsE         -0.0274      0.005     -5.166      0.000      -0.038      -0.017
HouseStyle_2.5Fin       -0.0394      0.020     -1.941    

In [123]:
X_tr_sm.pop('Neighborhood_BrkSide')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.887
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     159.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:40   Log-Likelihood:                 1921.1
No. Observations:                1021   AIC:                            -3744.
Df Residuals:                     972   BIC:                            -3503.
Df Model:                          48                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0862      0.028     -3.130      0.002      -0.140      -0.032
LotArea                  0.0892      0.029      3.039      0.002       0.032       0.147
OverallQual              0.1199      0.015      8.169      0.000       0.091       0.149
OverallCond              0.0502      0.011      4.506      0.000       0.028       0.072
YearBuilt                0.0894      0.012      7.735      0.000       0.067       0.112
YearRemodAdd             0.0160      0.005      2.950      0.003       0.005       0.027
MasVnrArea               0.0236      0.012      1.889      0.059      -0.001       0.048
TotalBsmtSF              0.1264      0.034      3.673      0.000       0.059       0.194
2ndFlrSF                 0.0254      0.014      1.761      0.079      -0.003       0.054
GrLivArea                0.3935      0.036     10.783      0.000       0.322       0.465
BsmtFullBath             0.0419      0.008      5.476      0.000       0.027       0.057
HalfBath                -0.0121      0.007     -1.820      0.069      -0.025       0.001
BedroomAbvGr            -0.0380      0.017     -2.277      0.023      -0.071      -0.005
KitchenAbvGr            -0.1007      0.018     -5.581      0.000      -0.136      -0.065
GarageArea               0.0347      0.011      3.105      0.002       0.013       0.057
WoodDeckSF               0.0183      0.009      1.995      0.046       0.000       0.036
PoolArea                -0.1689      0.035     -4.789      0.000      -0.238      -0.100
Street_Pave              0.0423      0.020      2.129      0.033       0.003       0.081
LotConfig_CulDSac        0.0145      0.005      2.839      0.005       0.004       0.025
Neighborhood_Crawfor     0.0421      0.007      5.820      0.000       0.028       0.056
Neighborhood_Mitchel    -0.0125      0.007     -1.894      0.059      -0.025       0.000
Neighborhood_NoRidge     0.0716      0.008      9.402      0.000       0.057       0.087
Neighborhood_NridgHt     0.0429      0.007      6.376      0.000       0.030       0.056
Neighborhood_Somerst     0.0257      0.006      4.359      0.000       0.014       0.037
Neighborhood_StoneBr     0.0427      0.011      3.735      0.000       0.020       0.065
Condition1_Norm          0.0163      0.004      4.530      0.000       0.009       0.023
Condition2_PosA          0.0898      0.039      2.299      0.022       0.013       0.166
Condition2_PosN         -0.5094      0.040    -12.585      0.000      -0.589      -0.430
BldgType_Twnhs          -0.0468      0.007     -6.370      0.000      -0.061      -0.032
BldgType_TwnhsE         -0.0277      0.005     -5.210      0.000      -0.038      -0.017
HouseStyle_2.5Fin       -0.0407      0.020     -2.003      0.045      -0.081      -0.001
RoofMatl_Membran         0.0629      0.040      1.582    

In [124]:
X_tr_sm.pop('RoofMatl_Membran')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.887
Model:                            OLS   Adj. R-squared:                  0.882
Method:                 Least Squares   F-statistic:                     162.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:40   Log-Likelihood:                 1919.8
No. Observations:                1021   AIC:                            -3744.
Df Residuals:                     973   BIC:                            -3507.
Df Model:                          47                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0847      0.028     -3.077      0.002      -0.139      -0.031
LotArea                  0.0924      0.029      3.153      0.002       0.035       0.150
OverallQual              0.1213      0.015      8.273      0.000       0.093       0.150
OverallCond              0.0512      0.011      4.607      0.000       0.029       0.073
YearBuilt                0.0885      0.012      7.663      0.000       0.066       0.111
YearRemodAdd             0.0163      0.005      3.001      0.003       0.006       0.027
MasVnrArea               0.0236      0.013      1.886      0.060      -0.001       0.048
TotalBsmtSF              0.1269      0.034      3.686      0.000       0.059       0.194
2ndFlrSF                 0.0257      0.014      1.775      0.076      -0.003       0.054
GrLivArea                0.3906      0.036     10.708      0.000       0.319       0.462
BsmtFullBath             0.0421      0.008      5.500      0.000       0.027       0.057
HalfBath                -0.0119      0.007     -1.791      0.074      -0.025       0.001
BedroomAbvGr            -0.0380      0.017     -2.270      0.023      -0.071      -0.005
KitchenAbvGr            -0.0999      0.018     -5.532      0.000      -0.135      -0.064
GarageArea               0.0348      0.011      3.113      0.002       0.013       0.057
WoodDeckSF               0.0180      0.009      1.964      0.050    1.27e-05       0.036
PoolArea                -0.1680      0.035     -4.761      0.000      -0.237      -0.099
Street_Pave              0.0431      0.020      2.166      0.031       0.004       0.082
LotConfig_CulDSac        0.0154      0.005      3.026      0.003       0.005       0.025
Neighborhood_Crawfor     0.0420      0.007      5.806      0.000       0.028       0.056
Neighborhood_Mitchel    -0.0127      0.007     -1.915      0.056      -0.026       0.000
Neighborhood_NoRidge     0.0717      0.008      9.405      0.000       0.057       0.087
Neighborhood_NridgHt     0.0430      0.007      6.397      0.000       0.030       0.056
Neighborhood_Somerst     0.0258      0.006      4.369      0.000       0.014       0.037
Neighborhood_StoneBr     0.0426      0.011      3.721      0.000       0.020       0.065
Condition1_Norm          0.0163      0.004      4.536      0.000       0.009       0.023
Condition2_PosA          0.0891      0.039      2.280      0.023       0.012       0.166
Condition2_PosN         -0.5091      0.041    -12.569      0.000      -0.589      -0.430
BldgType_Twnhs          -0.0470      0.007     -6.398      0.000      -0.061      -0.033
BldgType_TwnhsE         -0.0277      0.005     -5.211      0.000      -0.038      -0.017
HouseStyle_2.5Fin       -0.0404      0.020     -1.988      0.047      -0.080      -0.001
RoofMatl_WdShngl         0.1062      0.020      5.329    

In [125]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data = vif_data[vif_data['VIF'] >5]
vif_data


Feature         VIF
0            const  541.158274
8         2ndFlrSF    6.626523
9        GrLivArea    9.530158
36     BsmtQual_TA    5.993641
40  KitchenQual_Gd    6.653782
41  KitchenQual_TA    8.928550

In [126]:
X_tr_sm.pop('GrLivArea')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.874
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     146.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:41   Log-Likelihood:                 1862.9
No. Observations:                1021   AIC:                            -3632.
Df Residuals:                     974   BIC:                            -3400.
Df Model:                          46                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0647      0.029     -2.229      0.026      -0.122      -0.008
LotArea                  0.1238      0.031      4.018      0.000       0.063       0.184
OverallQual              0.1449      0.015      9.456      0.000       0.115       0.175
OverallCond              0.0499      0.012      4.249      0.000       0.027       0.073
YearBuilt                0.0705      0.012      5.836      0.000       0.047       0.094
YearRemodAdd             0.0187      0.006      3.264      0.001       0.007       0.030
MasVnrArea               0.0368      0.013      2.799      0.005       0.011       0.063
TotalBsmtSF              0.3518      0.029     12.199      0.000       0.295       0.408
2ndFlrSF                 0.1314      0.011     11.793      0.000       0.110       0.153
BsmtFullBath             0.0378      0.008      4.671      0.000       0.022       0.054
HalfBath                -0.0092      0.007     -1.303      0.193      -0.023       0.005
BedroomAbvGr             0.0101      0.017      0.593      0.553      -0.023       0.044
KitchenAbvGr            -0.0567      0.019     -3.049      0.002      -0.093      -0.020
GarageArea               0.0571      0.012      4.922      0.000       0.034       0.080
WoodDeckSF               0.0247      0.010      2.553      0.011       0.006       0.044
PoolArea                -0.1181      0.037     -3.194      0.001      -0.191      -0.046
Street_Pave              0.0451      0.021      2.145      0.032       0.004       0.086
LotConfig_CulDSac        0.0170      0.005      3.165      0.002       0.006       0.028
Neighborhood_Crawfor     0.0500      0.008      6.569      0.000       0.035       0.065
Neighborhood_Mitchel    -0.0167      0.007     -2.400      0.017      -0.030      -0.003
Neighborhood_NoRidge     0.0789      0.008      9.835      0.000       0.063       0.095
Neighborhood_NridgHt     0.0375      0.007      5.290      0.000       0.024       0.051
Neighborhood_Somerst     0.0199      0.006      3.201      0.001       0.008       0.032
Neighborhood_StoneBr     0.0450      0.012      3.717      0.000       0.021       0.069
Condition1_Norm          0.0129      0.004      3.400      0.001       0.005       0.020
Condition2_PosA          0.1003      0.041      2.429      0.015       0.019       0.181
Condition2_PosN         -0.4562      0.042    -10.738      0.000      -0.540      -0.373
BldgType_Twnhs          -0.0513      0.008     -6.618      0.000      -0.067      -0.036
BldgType_TwnhsE         -0.0287      0.006     -5.103      0.000      -0.040      -0.018
HouseStyle_2.5Fin       -0.0071      0.021     -0.334      0.738      -0.049       0.035
RoofMatl_WdShngl         0.1091      0.021      5.180      0.000       0.068       0.150
Exterior1st_BrkFace      0.0486      0.008      6.204    

In [127]:
X_tr_sm.pop('HouseStyle_2.5Fin')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.874
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     149.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:41   Log-Likelihood:                 1862.9
No. Observations:                1021   AIC:                            -3634.
Df Residuals:                     975   BIC:                            -3407.
Df Model:                          45                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0646      0.029     -2.228      0.026      -0.122      -0.008
LotArea                  0.1240      0.031      4.026      0.000       0.064       0.184
OverallQual              0.1450      0.015      9.474      0.000       0.115       0.175
OverallCond              0.0499      0.012      4.249      0.000       0.027       0.073
YearBuilt                0.0710      0.012      5.922      0.000       0.047       0.094
YearRemodAdd             0.0185      0.006      3.250      0.001       0.007       0.030
MasVnrArea               0.0370      0.013      2.819      0.005       0.011       0.063
TotalBsmtSF              0.3509      0.029     12.225      0.000       0.295       0.407
2ndFlrSF                 0.1310      0.011     11.851      0.000       0.109       0.153
BsmtFullBath             0.0377      0.008      4.668      0.000       0.022       0.054
HalfBath                -0.0089      0.007     -1.276      0.202      -0.023       0.005
BedroomAbvGr             0.0096      0.017      0.567      0.571      -0.024       0.043
KitchenAbvGr            -0.0565      0.019     -3.042      0.002      -0.093      -0.020
GarageArea               0.0569      0.012      4.914      0.000       0.034       0.080
WoodDeckSF               0.0245      0.010      2.542      0.011       0.006       0.043
PoolArea                -0.1173      0.037     -3.181      0.002      -0.190      -0.045
Street_Pave              0.0451      0.021      2.147      0.032       0.004       0.086
LotConfig_CulDSac        0.0170      0.005      3.166      0.002       0.006       0.028
Neighborhood_Crawfor     0.0499      0.008      6.566      0.000       0.035       0.065
Neighborhood_Mitchel    -0.0167      0.007     -2.403      0.016      -0.030      -0.003
Neighborhood_NoRidge     0.0790      0.008      9.862      0.000       0.063       0.095
Neighborhood_NridgHt     0.0375      0.007      5.299      0.000       0.024       0.051
Neighborhood_Somerst     0.0199      0.006      3.202      0.001       0.008       0.032
Neighborhood_StoneBr     0.0450      0.012      3.722      0.000       0.021       0.069
Condition1_Norm          0.0128      0.004      3.395      0.001       0.005       0.020
Condition2_PosA          0.1007      0.041      2.441      0.015       0.020       0.182
Condition2_PosN         -0.4557      0.042    -10.737      0.000      -0.539      -0.372
BldgType_Twnhs          -0.0514      0.008     -6.638      0.000      -0.067      -0.036
BldgType_TwnhsE         -0.0288      0.006     -5.135      0.000      -0.040      -0.018
RoofMatl_WdShngl         0.1091      0.021      5.182      0.000       0.068       0.150
Exterior1st_BrkFace      0.0486      0.008      6.206      0.000       0.033       0.064
Exterior2nd_CmentBd      0.0183      0.007      2.544    

In [128]:
X_tr_sm.pop('BedroomAbvGr')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.874
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     153.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:41   Log-Likelihood:                 1862.7
No. Observations:                1021   AIC:                            -3635.
Df Residuals:                     976   BIC:                            -3414.
Df Model:                          44                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0639      0.029     -2.205      0.028      -0.121      -0.007
LotArea                  0.1241      0.031      4.032      0.000       0.064       0.185
OverallQual              0.1449      0.015      9.469      0.000       0.115       0.175
OverallCond              0.0502      0.012      4.281      0.000       0.027       0.073
YearBuilt                0.0720      0.012      6.073      0.000       0.049       0.095
YearRemodAdd             0.0184      0.006      3.232      0.001       0.007       0.030
MasVnrArea               0.0373      0.013      2.844      0.005       0.012       0.063
TotalBsmtSF              0.3548      0.028     12.745      0.000       0.300       0.409
2ndFlrSF                 0.1338      0.010     13.635      0.000       0.115       0.153
BsmtFullBath             0.0373      0.008      4.637      0.000       0.022       0.053
HalfBath                -0.0094      0.007     -1.346      0.178      -0.023       0.004
KitchenAbvGr            -0.0543      0.018     -2.991      0.003      -0.090      -0.019
GarageArea               0.0566      0.012      4.894      0.000       0.034       0.079
WoodDeckSF               0.0244      0.010      2.530      0.012       0.005       0.043
PoolArea                -0.1192      0.037     -3.249      0.001      -0.191      -0.047
Street_Pave              0.0451      0.021      2.150      0.032       0.004       0.086
LotConfig_CulDSac        0.0168      0.005      3.137      0.002       0.006       0.027
Neighborhood_Crawfor     0.0499      0.008      6.572      0.000       0.035       0.065
Neighborhood_Mitchel    -0.0169      0.007     -2.433      0.015      -0.031      -0.003
Neighborhood_NoRidge     0.0789      0.008      9.854      0.000       0.063       0.095
Neighborhood_NridgHt     0.0374      0.007      5.289      0.000       0.024       0.051
Neighborhood_Somerst     0.0198      0.006      3.188      0.001       0.008       0.032
Neighborhood_StoneBr     0.0445      0.012      3.691      0.000       0.021       0.068
Condition1_Norm          0.0127      0.004      3.375      0.001       0.005       0.020
Condition2_PosA          0.0999      0.041      2.424      0.016       0.019       0.181
Condition2_PosN         -0.4581      0.042    -10.850      0.000      -0.541      -0.375
BldgType_Twnhs          -0.0522      0.008     -6.857      0.000      -0.067      -0.037
BldgType_TwnhsE         -0.0297      0.005     -5.562      0.000      -0.040      -0.019
RoofMatl_WdShngl         0.1081      0.021      5.156      0.000       0.067       0.149
Exterior1st_BrkFace      0.0488      0.008      6.235      0.000       0.033       0.064
Exterior2nd_CmentBd      0.0185      0.007      2.579      0.010       0.004       0.033
BsmtQual_Fa             -0.0398      0.010     -3.921    

In [129]:

X_tr_sm.pop('Heating_OthW')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.873
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     156.8
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:41   Log-Likelihood:                 1862.1
No. Observations:                1021   AIC:                            -3636.
Df Residuals:                     977   BIC:                            -3419.
Df Model:                          43                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0649      0.029     -2.240      0.025      -0.122      -0.008
LotArea                  0.1246      0.031      4.048      0.000       0.064       0.185
OverallQual              0.1428      0.015      9.405      0.000       0.113       0.173
OverallCond              0.0516      0.012      4.430      0.000       0.029       0.075
YearBuilt                0.0741      0.012      6.333      0.000       0.051       0.097
YearRemodAdd             0.0179      0.006      3.152      0.002       0.007       0.029
MasVnrArea               0.0373      0.013      2.845      0.005       0.012       0.063
TotalBsmtSF              0.3547      0.028     12.740      0.000       0.300       0.409
2ndFlrSF                 0.1334      0.010     13.599      0.000       0.114       0.153
BsmtFullBath             0.0372      0.008      4.623      0.000       0.021       0.053
HalfBath                -0.0091      0.007     -1.303      0.193      -0.023       0.005
KitchenAbvGr            -0.0536      0.018     -2.956      0.003      -0.089      -0.018
GarageArea               0.0574      0.012      4.973      0.000       0.035       0.080
WoodDeckSF               0.0245      0.010      2.539      0.011       0.006       0.043
PoolArea                -0.1182      0.037     -3.221      0.001      -0.190      -0.046
Street_Pave              0.0453      0.021      2.157      0.031       0.004       0.087
LotConfig_CulDSac        0.0167      0.005      3.125      0.002       0.006       0.027
Neighborhood_Crawfor     0.0504      0.008      6.637      0.000       0.035       0.065
Neighborhood_Mitchel    -0.0171      0.007     -2.456      0.014      -0.031      -0.003
Neighborhood_NoRidge     0.0791      0.008      9.884      0.000       0.063       0.095
Neighborhood_NridgHt     0.0376      0.007      5.309      0.000       0.024       0.051
Neighborhood_Somerst     0.0198      0.006      3.198      0.001       0.008       0.032
Neighborhood_StoneBr     0.0448      0.012      3.718      0.000       0.021       0.068
Condition1_Norm          0.0127      0.004      3.355      0.001       0.005       0.020
Condition2_PosA          0.1013      0.041      2.458      0.014       0.020       0.182
Condition2_PosN         -0.4576      0.042    -10.838      0.000      -0.540      -0.375
BldgType_Twnhs          -0.0522      0.008     -6.861      0.000      -0.067      -0.037
BldgType_TwnhsE         -0.0297      0.005     -5.565      0.000      -0.040      -0.019
RoofMatl_WdShngl         0.1082      0.021      5.160      0.000       0.067       0.149
Exterior1st_BrkFace      0.0488      0.008      6.234      0.000       0.033       0.064
Exterior2nd_CmentBd      0.0185      0.007      2.580      0.010       0.004       0.033
BsmtQual_Fa             -0.0394      0.010     -3.882    

In [130]:
X_tr_sm.pop('Functional_Min1')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.873
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     160.5
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:41   Log-Likelihood:                 1861.5
No. Observations:                1021   AIC:                            -3637.
Df Residuals:                     978   BIC:                            -3425.
Df Model:                          42                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0587      0.028     -2.066      0.039      -0.115      -0.003
LotArea                  0.1246      0.031      4.047      0.000       0.064       0.185
OverallQual              0.1428      0.015      9.401      0.000       0.113       0.173
OverallCond              0.0531      0.012      4.586      0.000       0.030       0.076
YearBuilt                0.0744      0.012      6.362      0.000       0.051       0.097
YearRemodAdd             0.0178      0.006      3.127      0.002       0.007       0.029
MasVnrArea               0.0377      0.013      2.872      0.004       0.012       0.063
TotalBsmtSF              0.3529      0.028     12.696      0.000       0.298       0.407
2ndFlrSF                 0.1329      0.010     13.560      0.000       0.114       0.152
BsmtFullBath             0.0374      0.008      4.653      0.000       0.022       0.053
HalfBath                -0.0088      0.007     -1.269      0.205      -0.022       0.005
KitchenAbvGr            -0.0537      0.018     -2.961      0.003      -0.089      -0.018
GarageArea               0.0580      0.012      5.026      0.000       0.035       0.081
WoodDeckSF               0.0253      0.010      2.628      0.009       0.006       0.044
PoolArea                -0.1171      0.037     -3.192      0.001      -0.189      -0.045
Street_Pave              0.0455      0.021      2.167      0.030       0.004       0.087
LotConfig_CulDSac        0.0166      0.005      3.108      0.002       0.006       0.027
Neighborhood_Crawfor     0.0506      0.008      6.675      0.000       0.036       0.066
Neighborhood_Mitchel    -0.0171      0.007     -2.453      0.014      -0.031      -0.003
Neighborhood_NoRidge     0.0793      0.008      9.907      0.000       0.064       0.095
Neighborhood_NridgHt     0.0379      0.007      5.358      0.000       0.024       0.052
Neighborhood_Somerst     0.0201      0.006      3.238      0.001       0.008       0.032
Neighborhood_StoneBr     0.0450      0.012      3.735      0.000       0.021       0.069
Condition1_Norm          0.0124      0.004      3.293      0.001       0.005       0.020
Condition2_PosA          0.1008      0.041      2.447      0.015       0.020       0.182
Condition2_PosN         -0.4572      0.042    -10.828      0.000      -0.540      -0.374
BldgType_Twnhs          -0.0529      0.008     -6.975      0.000      -0.068      -0.038
BldgType_TwnhsE         -0.0297      0.005     -5.560      0.000      -0.040      -0.019
RoofMatl_WdShngl         0.1080      0.021      5.150      0.000       0.067       0.149
Exterior1st_BrkFace      0.0486      0.008      6.211      0.000       0.033       0.064
Exterior2nd_CmentBd      0.0187      0.007      2.598      0.010       0.005       0.033
BsmtQual_Fa             -0.0394      0.010     -3.887    

In [131]:
X_tr_sm.pop('HalfBath')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.873
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     164.3
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:42   Log-Likelihood:                 1860.6
No. Observations:                1021   AIC:                            -3637.
Df Residuals:                     979   BIC:                            -3430.
Df Model:                          41                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0565      0.028     -1.989      0.047      -0.112      -0.001
LotArea                  0.1251      0.031      4.063      0.000       0.065       0.186
OverallQual              0.1439      0.015      9.491      0.000       0.114       0.174
OverallCond              0.0534      0.012      4.613      0.000       0.031       0.076
YearBuilt                0.0707      0.011      6.241      0.000       0.048       0.093
YearRemodAdd             0.0178      0.006      3.130      0.002       0.007       0.029
MasVnrArea               0.0373      0.013      2.845      0.005       0.012       0.063
TotalBsmtSF              0.3522      0.028     12.668      0.000       0.298       0.407
2ndFlrSF                 0.1258      0.008     15.625      0.000       0.110       0.142
BsmtFullBath             0.0367      0.008      4.572      0.000       0.021       0.052
KitchenAbvGr            -0.0508      0.018     -2.823      0.005      -0.086      -0.015
GarageArea               0.0578      0.012      5.015      0.000       0.035       0.080
WoodDeckSF               0.0249      0.010      2.584      0.010       0.006       0.044
PoolArea                -0.1128      0.037     -3.088      0.002      -0.185      -0.041
Street_Pave              0.0444      0.021      2.115      0.035       0.003       0.086
LotConfig_CulDSac        0.0165      0.005      3.085      0.002       0.006       0.027
Neighborhood_Crawfor     0.0505      0.008      6.661      0.000       0.036       0.065
Neighborhood_Mitchel    -0.0165      0.007     -2.376      0.018      -0.030      -0.003
Neighborhood_NoRidge     0.0796      0.008      9.949      0.000       0.064       0.095
Neighborhood_NridgHt     0.0386      0.007      5.481      0.000       0.025       0.052
Neighborhood_Somerst     0.0202      0.006      3.265      0.001       0.008       0.032
Neighborhood_StoneBr     0.0447      0.012      3.709      0.000       0.021       0.068
Condition1_Norm          0.0124      0.004      3.286      0.001       0.005       0.020
Condition2_PosA          0.0984      0.041      2.390      0.017       0.018       0.179
Condition2_PosN         -0.4550      0.042    -10.782      0.000      -0.538      -0.372
BldgType_Twnhs          -0.0536      0.008     -7.074      0.000      -0.068      -0.039
BldgType_TwnhsE         -0.0297      0.005     -5.558      0.000      -0.040      -0.019
RoofMatl_WdShngl         0.1071      0.021      5.107      0.000       0.066       0.148
Exterior1st_BrkFace      0.0476      0.008      6.115      0.000       0.032       0.063
Exterior2nd_CmentBd      0.0193      0.007      2.694      0.007       0.005       0.033
BsmtQual_Fa             -0.0402      0.010     -3.964      0.000      -0.060      -0.020
BsmtQual_Gd             -0.0496      0.005     -9.663    

In [132]:
X_tr_sm.pop('Functional_Typ')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.873
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     168.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:42   Log-Likelihood:                 1859.6
No. Observations:                1021   AIC:                            -3637.
Df Residuals:                     980   BIC:                            -3435.
Df Model:                          40                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0502      0.028     -1.792      0.074      -0.105       0.005
LotArea                  0.1247      0.031      4.047      0.000       0.064       0.185
OverallQual              0.1453      0.015      9.598      0.000       0.116       0.175
OverallCond              0.0559      0.011      4.888      0.000       0.033       0.078
YearBuilt                0.0723      0.011      6.423      0.000       0.050       0.094
YearRemodAdd             0.0171      0.006      3.017      0.003       0.006       0.028
MasVnrArea               0.0378      0.013      2.885      0.004       0.012       0.064
TotalBsmtSF              0.3496      0.028     12.598      0.000       0.295       0.404
2ndFlrSF                 0.1256      0.008     15.597      0.000       0.110       0.141
BsmtFullBath             0.0373      0.008      4.653      0.000       0.022       0.053
KitchenAbvGr            -0.0496      0.018     -2.759      0.006      -0.085      -0.014
GarageArea               0.0577      0.012      4.999      0.000       0.035       0.080
WoodDeckSF               0.0245      0.010      2.546      0.011       0.006       0.043
PoolArea                -0.1109      0.037     -3.036      0.002      -0.183      -0.039
Street_Pave              0.0438      0.021      2.086      0.037       0.003       0.085
LotConfig_CulDSac        0.0164      0.005      3.061      0.002       0.006       0.027
Neighborhood_Crawfor     0.0507      0.008      6.673      0.000       0.036       0.066
Neighborhood_Mitchel    -0.0161      0.007     -2.319      0.021      -0.030      -0.002
Neighborhood_NoRidge     0.0799      0.008      9.981      0.000       0.064       0.096
Neighborhood_NridgHt     0.0392      0.007      5.559      0.000       0.025       0.053
Neighborhood_Somerst     0.0205      0.006      3.316      0.001       0.008       0.033
Neighborhood_StoneBr     0.0450      0.012      3.733      0.000       0.021       0.069
Condition1_Norm          0.0124      0.004      3.290      0.001       0.005       0.020
Condition2_PosA          0.0986      0.041      2.394      0.017       0.018       0.179
Condition2_PosN         -0.4545      0.042    -10.764      0.000      -0.537      -0.372
BldgType_Twnhs          -0.0545      0.008     -7.219      0.000      -0.069      -0.040
BldgType_TwnhsE         -0.0299      0.005     -5.591      0.000      -0.040      -0.019
RoofMatl_WdShngl         0.1077      0.021      5.135      0.000       0.067       0.149
Exterior1st_BrkFace      0.0471      0.008      6.056      0.000       0.032       0.062
Exterior2nd_CmentBd      0.0197      0.007      2.748      0.006       0.006       0.034
BsmtQual_Fa             -0.0407      0.010     -4.017      0.000      -0.061      -0.021
BsmtQual_Gd             -0.0493      0.005     -9.601    

In [133]:


X_tr_sm.pop('Functional_Min2')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.873
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     172.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:42   Log-Likelihood:                 1859.5
No. Observations:                1021   AIC:                            -3639.
Df Residuals:                     981   BIC:                            -3442.
Df Model:                          39                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0494      0.028     -1.766      0.078      -0.104       0.006
LotArea                  0.1247      0.031      4.050      0.000       0.064       0.185
OverallQual              0.1446      0.015      9.609      0.000       0.115       0.174
OverallCond              0.0556      0.011      4.869      0.000       0.033       0.078
YearBuilt                0.0719      0.011      6.411      0.000       0.050       0.094
YearRemodAdd             0.0173      0.006      3.061      0.002       0.006       0.028
MasVnrArea               0.0377      0.013      2.875      0.004       0.012       0.063
TotalBsmtSF              0.3495      0.028     12.601      0.000       0.295       0.404
2ndFlrSF                 0.1258      0.008     15.642      0.000       0.110       0.142
BsmtFullBath             0.0372      0.008      4.644      0.000       0.021       0.053
KitchenAbvGr            -0.0498      0.018     -2.774      0.006      -0.085      -0.015
GarageArea               0.0579      0.012      5.025      0.000       0.035       0.081
WoodDeckSF               0.0249      0.010      2.592      0.010       0.006       0.044
PoolArea                -0.1110      0.037     -3.040      0.002      -0.183      -0.039
Street_Pave              0.0439      0.021      2.092      0.037       0.003       0.085
LotConfig_CulDSac        0.0166      0.005      3.107      0.002       0.006       0.027
Neighborhood_Crawfor     0.0507      0.008      6.679      0.000       0.036       0.066
Neighborhood_Mitchel    -0.0161      0.007     -2.324      0.020      -0.030      -0.003
Neighborhood_NoRidge     0.0798      0.008      9.981      0.000       0.064       0.096
Neighborhood_NridgHt     0.0392      0.007      5.568      0.000       0.025       0.053
Neighborhood_Somerst     0.0206      0.006      3.323      0.001       0.008       0.033
Neighborhood_StoneBr     0.0451      0.012      3.739      0.000       0.021       0.069
Condition1_Norm          0.0125      0.004      3.306      0.001       0.005       0.020
Condition2_PosA          0.0986      0.041      2.394      0.017       0.018       0.179
Condition2_PosN         -0.4544      0.042    -10.767      0.000      -0.537      -0.372
BldgType_Twnhs          -0.0545      0.008     -7.227      0.000      -0.069      -0.040
BldgType_TwnhsE         -0.0299      0.005     -5.593      0.000      -0.040      -0.019
RoofMatl_WdShngl         0.1076      0.021      5.132      0.000       0.066       0.149
Exterior1st_BrkFace      0.0471      0.008      6.062      0.000       0.032       0.062
Exterior2nd_CmentBd      0.0196      0.007      2.741      0.006       0.006       0.034
BsmtQual_Fa             -0.0407      0.010     -4.014      0.000      -0.061      -0.021
BsmtQual_Gd             -0.0493      0.005     -9.608    

In [134]:
X_tr_sm.pop('SaleType_New')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.873
Model:                            OLS   Adj. R-squared:                  0.868
Method:                 Least Squares   F-statistic:                     176.9
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:42   Log-Likelihood:                 1858.4
No. Observations:                1021   AIC:                            -3639.
Df Residuals:                     982   BIC:                            -3447.
Df Model:                          38                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.0480      0.028     -1.717      0.086      -0.103       0.007
LotArea                  0.1254      0.031      4.072      0.000       0.065       0.186
OverallQual              0.1442      0.015      9.578      0.000       0.115       0.174
OverallCond              0.0548      0.011      4.804      0.000       0.032       0.077
YearBuilt                0.0733      0.011      6.563      0.000       0.051       0.095
YearRemodAdd             0.0181      0.006      3.214      0.001       0.007       0.029
MasVnrArea               0.0373      0.013      2.843      0.005       0.012       0.063
TotalBsmtSF              0.3534      0.028     12.794      0.000       0.299       0.408
2ndFlrSF                 0.1255      0.008     15.601      0.000       0.110       0.141
BsmtFullBath             0.0361      0.008      4.527      0.000       0.020       0.052
KitchenAbvGr            -0.0507      0.018     -2.823      0.005      -0.086      -0.015
GarageArea               0.0581      0.012      5.044      0.000       0.036       0.081
WoodDeckSF               0.0242      0.010      2.521      0.012       0.005       0.043
PoolArea                -0.1109      0.037     -3.034      0.002      -0.183      -0.039
Street_Pave              0.0438      0.021      2.086      0.037       0.003       0.085
LotConfig_CulDSac        0.0163      0.005      3.063      0.002       0.006       0.027
Neighborhood_Crawfor     0.0508      0.008      6.697      0.000       0.036       0.066
Neighborhood_Mitchel    -0.0166      0.007     -2.386      0.017      -0.030      -0.003
Neighborhood_NoRidge     0.0789      0.008      9.891      0.000       0.063       0.095
Neighborhood_NridgHt     0.0403      0.007      5.755      0.000       0.027       0.054
Neighborhood_Somerst     0.0224      0.006      3.682      0.000       0.010       0.034
Neighborhood_StoneBr     0.0458      0.012      3.805      0.000       0.022       0.069
Condition1_Norm          0.0123      0.004      3.255      0.001       0.005       0.020
Condition2_PosA          0.0987      0.041      2.396      0.017       0.018       0.180
Condition2_PosN         -0.4505      0.042    -10.690      0.000      -0.533      -0.368
BldgType_Twnhs          -0.0558      0.007     -7.438      0.000      -0.070      -0.041
BldgType_TwnhsE         -0.0305      0.005     -5.729      0.000      -0.041      -0.020
RoofMatl_WdShngl         0.1069      0.021      5.098      0.000       0.066       0.148
Exterior1st_BrkFace      0.0468      0.008      6.011      0.000       0.031       0.062
Exterior2nd_CmentBd      0.0204      0.007      2.855      0.004       0.006       0.034
BsmtQual_Fa             -0.0414      0.010     -4.094      0.000      -0.061      -0.022
BsmtQual_Gd             -0.0506      0.005    -10.002    

In [135]:
vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data = vif_data[vif_data['VIF'] >5]
vif_data


Feature         VIF
0            const  499.464579
32     BsmtQual_TA    5.287330
35  KitchenQual_Gd    6.503783
36  KitchenQual_TA    8.706583

In [136]:
X_tr_sm.pop('KitchenQual_TA')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.866
Model:                            OLS   Adj. R-squared:                  0.861
Method:                 Least Squares   F-statistic:                     172.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:43   Log-Likelihood:                 1834.1
No. Observations:                1021   AIC:                            -3592.
Df Residuals:                     983   BIC:                            -3405.
Df Model:                          37                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1075      0.027     -3.948      0.000      -0.161      -0.054
LotArea                  0.1153      0.031      3.662      0.000       0.054       0.177
OverallQual              0.1661      0.015     11.031      0.000       0.137       0.196
OverallCond              0.0573      0.012      4.909      0.000       0.034       0.080
YearBuilt                0.0736      0.011      6.439      0.000       0.051       0.096
YearRemodAdd             0.0248      0.006      4.383      0.000       0.014       0.036
MasVnrArea               0.0358      0.013      2.672      0.008       0.010       0.062
TotalBsmtSF              0.3814      0.028     13.638      0.000       0.327       0.436
2ndFlrSF                 0.1298      0.008     15.820      0.000       0.114       0.146
BsmtFullBath             0.0406      0.008      4.984      0.000       0.025       0.057
KitchenAbvGr            -0.0582      0.018     -3.170      0.002      -0.094      -0.022
GarageArea               0.0619      0.012      5.250      0.000       0.039       0.085
WoodDeckSF               0.0244      0.010      2.483      0.013       0.005       0.044
PoolArea                -0.1049      0.037     -2.805      0.005      -0.178      -0.031
Street_Pave              0.0439      0.021      2.044      0.041       0.002       0.086
LotConfig_CulDSac        0.0147      0.005      2.689      0.007       0.004       0.025
Neighborhood_Crawfor     0.0506      0.008      6.505      0.000       0.035       0.066
Neighborhood_Mitchel    -0.0205      0.007     -2.897      0.004      -0.034      -0.007
Neighborhood_NoRidge     0.0771      0.008      9.444      0.000       0.061       0.093
Neighborhood_NridgHt     0.0498      0.007      7.087      0.000       0.036       0.064
Neighborhood_Somerst     0.0239      0.006      3.844      0.000       0.012       0.036
Neighborhood_StoneBr     0.0484      0.012      3.923      0.000       0.024       0.073
Condition1_Norm          0.0135      0.004      3.508      0.000       0.006       0.021
Condition2_PosA          0.0891      0.042      2.114      0.035       0.006       0.172
Condition2_PosN         -0.4402      0.043    -10.213      0.000      -0.525      -0.356
BldgType_Twnhs          -0.0591      0.008     -7.716      0.000      -0.074      -0.044
BldgType_TwnhsE         -0.0305      0.005     -5.586      0.000      -0.041      -0.020
RoofMatl_WdShngl         0.1085      0.021      5.057      0.000       0.066       0.151
Exterior1st_BrkFace      0.0512      0.008      6.460      0.000       0.036       0.067
Exterior2nd_CmentBd      0.0238      0.007      3.268      0.001       0.010       0.038
BsmtQual_Fa             -0.0492      0.010     -4.775      0.000      -0.069      -0.029
BsmtQual_Gd             -0.0595      0.005    -11.889    

In [137]:
X_tr_sm.pop('KitchenQual_Fa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.866
Model:                            OLS   Adj. R-squared:                  0.861
Method:                 Least Squares   F-statistic:                     177.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:43   Log-Likelihood:                 1834.0
No. Observations:                1021   AIC:                            -3594.
Df Residuals:                     984   BIC:                            -3412.
Df Model:                          36                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1051      0.027     -3.909      0.000      -0.158      -0.052
LotArea                  0.1149      0.031      3.651      0.000       0.053       0.177
OverallQual              0.1659      0.015     11.025      0.000       0.136       0.195
OverallCond              0.0569      0.012      4.885      0.000       0.034       0.080
YearBuilt                0.0730      0.011      6.418      0.000       0.051       0.095
YearRemodAdd             0.0247      0.006      4.360      0.000       0.014       0.036
MasVnrArea               0.0357      0.013      2.665      0.008       0.009       0.062
TotalBsmtSF              0.3819      0.028     13.667      0.000       0.327       0.437
2ndFlrSF                 0.1299      0.008     15.841      0.000       0.114       0.146
BsmtFullBath             0.0404      0.008      4.972      0.000       0.024       0.056
KitchenAbvGr            -0.0580      0.018     -3.161      0.002      -0.094      -0.022
GarageArea               0.0613      0.012      5.222      0.000       0.038       0.084
WoodDeckSF               0.0243      0.010      2.477      0.013       0.005       0.044
PoolArea                -0.1050      0.037     -2.810      0.005      -0.178      -0.032
Street_Pave              0.0429      0.021      2.004      0.045       0.001       0.085
LotConfig_CulDSac        0.0147      0.005      2.688      0.007       0.004       0.025
Neighborhood_Crawfor     0.0505      0.008      6.501      0.000       0.035       0.066
Neighborhood_Mitchel    -0.0206      0.007     -2.905      0.004      -0.034      -0.007
Neighborhood_NoRidge     0.0772      0.008      9.460      0.000       0.061       0.093
Neighborhood_NridgHt     0.0500      0.007      7.115      0.000       0.036       0.064
Neighborhood_Somerst     0.0240      0.006      3.869      0.000       0.012       0.036
Neighborhood_StoneBr     0.0484      0.012      3.930      0.000       0.024       0.073
Condition1_Norm          0.0134      0.004      3.491      0.001       0.006       0.021
Condition2_PosA          0.0890      0.042      2.113      0.035       0.006       0.172
Condition2_PosN         -0.4402      0.043    -10.215      0.000      -0.525      -0.356
BldgType_Twnhs          -0.0592      0.008     -7.736      0.000      -0.074      -0.044
BldgType_TwnhsE         -0.0305      0.005     -5.595      0.000      -0.041      -0.020
RoofMatl_WdShngl         0.1085      0.021      5.057      0.000       0.066       0.151
Exterior1st_BrkFace      0.0510      0.008      6.443      0.000       0.035       0.067
Exterior2nd_CmentBd      0.0238      0.007      3.264      0.001       0.009       0.038
BsmtQual_Fa             -0.0494      0.010     -4.799      0.000      -0.070      -0.029
BsmtQual_Gd             -0.0596      0.005    -11.927    

In [138]:
vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data = vif_data[vif_data['VIF'] >5]
vif_data

Feature         VIF
0         const  441.253458
32  BsmtQual_TA    5.069134

In [139]:
X_tr_sm.pop('BsmtQual_TA')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.854
Model:                            OLS   Adj. R-squared:                  0.848
Method:                 Least Squares   F-statistic:                     164.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:43   Log-Likelihood:                 1788.0
No. Observations:                1021   AIC:                            -3504.
Df Residuals:                     985   BIC:                            -3326.
Df Model:                          35                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1860      0.027     -6.968      0.000      -0.238      -0.134
LotArea                  0.1226      0.033      3.725      0.000       0.058       0.187
OverallQual              0.1930      0.015     12.482      0.000       0.163       0.223
OverallCond              0.0397      0.012      3.297      0.001       0.016       0.063
YearBuilt                0.0997      0.012      8.651      0.000       0.077       0.122
YearRemodAdd             0.0317      0.006      5.399      0.000       0.020       0.043
MasVnrArea               0.0398      0.014      2.841      0.005       0.012       0.067
TotalBsmtSF              0.3065      0.028     10.928      0.000       0.251       0.362
2ndFlrSF                 0.1224      0.009     14.341      0.000       0.106       0.139
BsmtFullBath             0.0416      0.009      4.897      0.000       0.025       0.058
KitchenAbvGr            -0.0200      0.019     -1.066      0.287      -0.057       0.017
GarageArea               0.0730      0.012      5.986      0.000       0.049       0.097
WoodDeckSF               0.0299      0.010      2.925      0.004       0.010       0.050
PoolArea                -0.0589      0.039     -1.519      0.129      -0.135       0.017
Street_Pave              0.0482      0.022      2.153      0.032       0.004       0.092
LotConfig_CulDSac        0.0175      0.006      3.076      0.002       0.006       0.029
Neighborhood_Crawfor     0.0567      0.008      7.003      0.000       0.041       0.073
Neighborhood_Mitchel    -0.0212      0.007     -2.861      0.004      -0.036      -0.007
Neighborhood_NoRidge     0.0819      0.009      9.622      0.000       0.065       0.099
Neighborhood_NridgHt     0.0652      0.007      9.114      0.000       0.051       0.079
Neighborhood_Somerst     0.0261      0.006      4.031      0.000       0.013       0.039
Neighborhood_StoneBr     0.0549      0.013      4.272      0.000       0.030       0.080
Condition1_Norm          0.0142      0.004      3.533      0.000       0.006       0.022
Condition2_PosA          0.0900      0.044      2.043      0.041       0.004       0.176
Condition2_PosN         -0.4090      0.045     -9.104      0.000      -0.497      -0.321
BldgType_Twnhs          -0.0678      0.008     -8.536      0.000      -0.083      -0.052
BldgType_TwnhsE         -0.0307      0.006     -5.376      0.000      -0.042      -0.019
RoofMatl_WdShngl         0.1182      0.022      5.275      0.000       0.074       0.162
Exterior1st_BrkFace      0.0534      0.008      6.456      0.000       0.037       0.070
Exterior2nd_CmentBd      0.0298      0.008      3.922      0.000       0.015       0.045
BsmtQual_Fa              0.0037      0.009      0.404      0.687      -0.014       0.021
BsmtQual_Gd             -0.0252      0.004     -6.893    

In [140]:
X_tr_sm.pop('PoolQC_Fa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.854
Model:                            OLS   Adj. R-squared:                  0.848
Method:                 Least Squares   F-statistic:                     169.0
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:43   Log-Likelihood:                 1787.4
No. Observations:                1021   AIC:                            -3505.
Df Residuals:                     986   BIC:                            -3332.
Df Model:                          34                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1858      0.027     -6.960      0.000      -0.238      -0.133
LotArea                  0.1215      0.033      3.695      0.000       0.057       0.186
OverallQual              0.1930      0.015     12.487      0.000       0.163       0.223
OverallCond              0.0399      0.012      3.318      0.001       0.016       0.063
YearBuilt                0.1000      0.012      8.681      0.000       0.077       0.123
YearRemodAdd             0.0317      0.006      5.400      0.000       0.020       0.043
MasVnrArea               0.0407      0.014      2.911      0.004       0.013       0.068
TotalBsmtSF              0.3012      0.028     10.939      0.000       0.247       0.355
2ndFlrSF                 0.1211      0.008     14.358      0.000       0.105       0.138
BsmtFullBath             0.0417      0.009      4.900      0.000       0.025       0.058
KitchenAbvGr            -0.0194      0.019     -1.037      0.300      -0.056       0.017
GarageArea               0.0726      0.012      5.957      0.000       0.049       0.097
WoodDeckSF               0.0306      0.010      3.003      0.003       0.011       0.051
PoolArea                -0.0348      0.030     -1.148      0.251      -0.094       0.025
Street_Pave              0.0482      0.022      2.155      0.031       0.004       0.092
LotConfig_CulDSac        0.0176      0.006      3.096      0.002       0.006       0.029
Neighborhood_Crawfor     0.0569      0.008      7.027      0.000       0.041       0.073
Neighborhood_Mitchel    -0.0212      0.007     -2.868      0.004      -0.036      -0.007
Neighborhood_NoRidge     0.0818      0.009      9.612      0.000       0.065       0.099
Neighborhood_NridgHt     0.0656      0.007      9.180      0.000       0.052       0.080
Neighborhood_Somerst     0.0262      0.006      4.044      0.000       0.013       0.039
Neighborhood_StoneBr     0.0552      0.013      4.295      0.000       0.030       0.080
Condition1_Norm          0.0144      0.004      3.587      0.000       0.007       0.022
Condition2_PosA          0.0911      0.044      2.069      0.039       0.005       0.178
Condition2_PosN         -0.4066      0.045     -9.063      0.000      -0.495      -0.319
BldgType_Twnhs          -0.0683      0.008     -8.598      0.000      -0.084      -0.053
BldgType_TwnhsE         -0.0310      0.006     -5.449      0.000      -0.042      -0.020
RoofMatl_WdShngl         0.1188      0.022      5.302      0.000       0.075       0.163
Exterior1st_BrkFace      0.0536      0.008      6.482      0.000       0.037       0.070
Exterior2nd_CmentBd      0.0299      0.008      3.943      0.000       0.015       0.045
BsmtQual_Fa              0.0037      0.009      0.409      0.683      -0.014       0.022
BsmtQual_Gd             -0.0251      0.004     -6.869    

In [141]:
X_tr_sm.pop('BsmtQual_Fa')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.853
Model:                            OLS   Adj. R-squared:                  0.849
Method:                 Least Squares   F-statistic:                     174.2
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:43   Log-Likelihood:                 1787.4
No. Observations:                1021   AIC:                            -3507.
Df Residuals:                     987   BIC:                            -3339.
Df Model:                          33                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1851      0.027     -6.951      0.000      -0.237      -0.133
LotArea                  0.1213      0.033      3.691      0.000       0.057       0.186
OverallQual              0.1930      0.015     12.492      0.000       0.163       0.223
OverallCond              0.0397      0.012      3.306      0.001       0.016       0.063
YearBuilt                0.0991      0.011      8.791      0.000       0.077       0.121
YearRemodAdd             0.0318      0.006      5.433      0.000       0.020       0.043
MasVnrArea               0.0406      0.014      2.904      0.004       0.013       0.068
TotalBsmtSF              0.3007      0.027     10.936      0.000       0.247       0.355
2ndFlrSF                 0.1211      0.008     14.365      0.000       0.105       0.138
BsmtFullBath             0.0416      0.008      4.893      0.000       0.025       0.058
KitchenAbvGr            -0.0193      0.019     -1.032      0.303      -0.056       0.017
GarageArea               0.0731      0.012      6.037      0.000       0.049       0.097
WoodDeckSF               0.0307      0.010      3.006      0.003       0.011       0.051
PoolArea                -0.0350      0.030     -1.153      0.249      -0.094       0.025
Street_Pave              0.0483      0.022      2.158      0.031       0.004       0.092
LotConfig_CulDSac        0.0176      0.006      3.095      0.002       0.006       0.029
Neighborhood_Crawfor     0.0568      0.008      7.021      0.000       0.041       0.073
Neighborhood_Mitchel    -0.0212      0.007     -2.872      0.004      -0.036      -0.007
Neighborhood_NoRidge     0.0819      0.009      9.622      0.000       0.065       0.099
Neighborhood_NridgHt     0.0656      0.007      9.192      0.000       0.052       0.080
Neighborhood_Somerst     0.0263      0.006      4.052      0.000       0.014       0.039
Neighborhood_StoneBr     0.0552      0.013      4.298      0.000       0.030       0.080
Condition1_Norm          0.0144      0.004      3.584      0.000       0.007       0.022
Condition2_PosA          0.0904      0.044      2.055      0.040       0.004       0.177
Condition2_PosN         -0.4064      0.045     -9.064      0.000      -0.494      -0.318
BldgType_Twnhs          -0.0682      0.008     -8.600      0.000      -0.084      -0.053
BldgType_TwnhsE         -0.0309      0.006     -5.442      0.000      -0.042      -0.020
RoofMatl_WdShngl         0.1187      0.022      5.302      0.000       0.075       0.163
Exterior1st_BrkFace      0.0535      0.008      6.474      0.000       0.037       0.070
Exterior2nd_CmentBd      0.0299      0.008      3.941      0.000       0.015       0.045
BsmtQual_Gd             -0.0250      0.004     -6.867      0.000      -0.032      -0.018
BsmtExposure_Gd          0.0345      0.005      6.769    

In [142]:
X_tr_sm.pop('KitchenAbvGr')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.853
Model:                            OLS   Adj. R-squared:                  0.849
Method:                 Least Squares   F-statistic:                     179.6
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:44   Log-Likelihood:                 1786.8
No. Observations:                1021   AIC:                            -3508.
Df Residuals:                     988   BIC:                            -3345.
Df Model:                          32                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1945      0.025     -7.762      0.000      -0.244      -0.145
LotArea                  0.1224      0.033      3.725      0.000       0.058       0.187
OverallQual              0.1953      0.015     12.764      0.000       0.165       0.225
OverallCond              0.0414      0.012      3.479      0.001       0.018       0.065
YearBuilt                0.1001      0.011      8.925      0.000       0.078       0.122
YearRemodAdd             0.0317      0.006      5.412      0.000       0.020       0.043
MasVnrArea               0.0400      0.014      2.865      0.004       0.013       0.067
TotalBsmtSF              0.2993      0.027     10.897      0.000       0.245       0.353
2ndFlrSF                 0.1199      0.008     14.363      0.000       0.103       0.136
BsmtFullBath             0.0418      0.008      4.929      0.000       0.025       0.059
GarageArea               0.0726      0.012      5.997      0.000       0.049       0.096
WoodDeckSF               0.0311      0.010      3.051      0.002       0.011       0.051
PoolArea                -0.0340      0.030     -1.122      0.262      -0.093       0.025
Street_Pave              0.0481      0.022      2.150      0.032       0.004       0.092
LotConfig_CulDSac        0.0179      0.006      3.139      0.002       0.007       0.029
Neighborhood_Crawfor     0.0570      0.008      7.047      0.000       0.041       0.073
Neighborhood_Mitchel    -0.0220      0.007     -2.995      0.003      -0.036      -0.008
Neighborhood_NoRidge     0.0821      0.009      9.648      0.000       0.065       0.099
Neighborhood_NridgHt     0.0655      0.007      9.174      0.000       0.051       0.079
Neighborhood_Somerst     0.0262      0.006      4.047      0.000       0.014       0.039
Neighborhood_StoneBr     0.0549      0.013      4.275      0.000       0.030       0.080
Condition1_Norm          0.0147      0.004      3.687      0.000       0.007       0.023
Condition2_PosA          0.0906      0.044      2.060      0.040       0.004       0.177
Condition2_PosN         -0.4054      0.045     -9.043      0.000      -0.493      -0.317
BldgType_Twnhs          -0.0680      0.008     -8.570      0.000      -0.084      -0.052
BldgType_TwnhsE         -0.0310      0.006     -5.445      0.000      -0.042      -0.020
RoofMatl_WdShngl         0.1188      0.022      5.304      0.000       0.075       0.163
Exterior1st_BrkFace      0.0529      0.008      6.417      0.000       0.037       0.069
Exterior2nd_CmentBd      0.0300      0.008      3.949      0.000       0.015       0.045
BsmtQual_Gd             -0.0250      0.004     -6.857      0.000      -0.032      -0.018
BsmtExposure_Gd          0.0343      0.005      6.740      0.000       0.024       0.044
KitchenQual_Gd          -0.0089      0.003     -2.559    

In [143]:
X_tr_sm.pop('PoolArea')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.853
Model:                            OLS   Adj. R-squared:                  0.849
Method:                 Least Squares   F-statistic:                     185.4
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:44   Log-Likelihood:                 1786.2
No. Observations:                1021   AIC:                            -3508.
Df Residuals:                     989   BIC:                            -3351.
Df Model:                          31                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1937      0.025     -7.732      0.000      -0.243      -0.145
LotArea                  0.1208      0.033      3.679      0.000       0.056       0.185
OverallQual              0.1950      0.015     12.748      0.000       0.165       0.225
OverallCond              0.0418      0.012      3.514      0.000       0.018       0.065
YearBuilt                0.1005      0.011      8.959      0.000       0.078       0.123
YearRemodAdd             0.0315      0.006      5.386      0.000       0.020       0.043
MasVnrArea               0.0411      0.014      2.946      0.003       0.014       0.068
TotalBsmtSF              0.2928      0.027     10.905      0.000       0.240       0.345
2ndFlrSF                 0.1185      0.008     14.350      0.000       0.102       0.135
BsmtFullBath             0.0413      0.008      4.874      0.000       0.025       0.058
GarageArea               0.0722      0.012      5.964      0.000       0.048       0.096
WoodDeckSF               0.0313      0.010      3.069      0.002       0.011       0.051
Street_Pave              0.0480      0.022      2.147      0.032       0.004       0.092
LotConfig_CulDSac        0.0181      0.006      3.188      0.001       0.007       0.029
Neighborhood_Crawfor     0.0573      0.008      7.090      0.000       0.041       0.073
Neighborhood_Mitchel    -0.0219      0.007     -2.976      0.003      -0.036      -0.007
Neighborhood_NoRidge     0.0821      0.009      9.647      0.000       0.065       0.099
Neighborhood_NridgHt     0.0663      0.007      9.330      0.000       0.052       0.080
Neighborhood_Somerst     0.0265      0.006      4.086      0.000       0.014       0.039
Neighborhood_StoneBr     0.0555      0.013      4.325      0.000       0.030       0.081
Condition1_Norm          0.0149      0.004      3.736      0.000       0.007       0.023
Condition2_PosA          0.0922      0.044      2.098      0.036       0.006       0.179
Condition2_PosN         -0.4022      0.045     -8.989      0.000      -0.490      -0.314
BldgType_Twnhs          -0.0685      0.008     -8.651      0.000      -0.084      -0.053
BldgType_TwnhsE         -0.0313      0.006     -5.517      0.000      -0.042      -0.020
RoofMatl_WdShngl         0.1199      0.022      5.357      0.000       0.076       0.164
Exterior1st_BrkFace      0.0533      0.008      6.460      0.000       0.037       0.069
Exterior2nd_CmentBd      0.0302      0.008      3.985      0.000       0.015       0.045
BsmtQual_Gd             -0.0246      0.004     -6.775      0.000      -0.032      -0.017
BsmtExposure_Gd          0.0346      0.005      6.786      0.000       0.025       0.045
KitchenQual_Gd          -0.0089      0.003     -2.559      0.011      -0.016      -0.002
Functional_Sev          -0.0706      0.043     -1.643    

In [144]:
X_tr_sm.pop('Functional_Sev')
model1 = sm.OLS(y_tr,X_tr_sm)
res1 = model1.fit()
res1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              SalePrice   R-squared:                       0.853
Model:                            OLS   Adj. R-squared:                  0.848
Method:                 Least Squares   F-statistic:                     191.1
Date:                Sun, 21 Jan 2024   Prob (F-statistic):               0.00
Time:                        21:13:44   Log-Likelihood:                 1784.8
No. Observations:                1021   AIC:                            -3508.
Df Residuals:                     990   BIC:                            -3355.
Df Model:                          30                                         
Covariance Type:            nonrobust                                         
========================================================================================
                           coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------------
const                   -0.1936      0.025     -7.721      0.000      -0.243      -0.144
LotArea                  0.1196      0.033      3.640      0.000       0.055       0.184
OverallQual              0.1953      0.015     12.758      0.000       0.165       0.225
OverallCond              0.0420      0.012      3.528      0.000       0.019       0.065
YearBuilt                0.1008      0.011      8.982      0.000       0.079       0.123
YearRemodAdd             0.0315      0.006      5.377      0.000       0.020       0.043
MasVnrArea               0.0410      0.014      2.939      0.003       0.014       0.068
TotalBsmtSF              0.2922      0.027     10.875      0.000       0.239       0.345
2ndFlrSF                 0.1180      0.008     14.286      0.000       0.102       0.134
BsmtFullBath             0.0416      0.008      4.907      0.000       0.025       0.058
GarageArea               0.0715      0.012      5.909      0.000       0.048       0.095
WoodDeckSF               0.0317      0.010      3.114      0.002       0.012       0.052
Street_Pave              0.0478      0.022      2.136      0.033       0.004       0.092
LotConfig_CulDSac        0.0182      0.006      3.195      0.001       0.007       0.029
Neighborhood_Crawfor     0.0574      0.008      7.104      0.000       0.042       0.073
Neighborhood_Mitchel    -0.0219      0.007     -2.970      0.003      -0.036      -0.007
Neighborhood_NoRidge     0.0824      0.009      9.675      0.000       0.066       0.099
Neighborhood_NridgHt     0.0664      0.007      9.336      0.000       0.052       0.080
Neighborhood_Somerst     0.0266      0.006      4.109      0.000       0.014       0.039
Neighborhood_StoneBr     0.0556      0.013      4.323      0.000       0.030       0.081
Condition1_Norm          0.0148      0.004      3.697      0.000       0.007       0.023
Condition2_PosA          0.0924      0.044      2.100      0.036       0.006       0.179
Condition2_PosN         -0.4018      0.045     -8.972      0.000      -0.490      -0.314
BldgType_Twnhs          -0.0685      0.008     -8.640      0.000      -0.084      -0.053
BldgType_TwnhsE         -0.0314      0.006     -5.518      0.000      -0.043      -0.020
RoofMatl_WdShngl         0.1198      0.022      5.351      0.000       0.076       0.164
Exterior1st_BrkFace      0.0533      0.008      6.465      0.000       0.037       0.070
Exterior2nd_CmentBd      0.0303      0.008      3.985      0.000       0.015       0.045
BsmtQual_Gd             -0.0249      0.004     -6.866      0.000      -0.032      -0.018
BsmtExposure_Gd          0.0346      0.005      6.790      0.000       0.025       0.045
KitchenQual_Gd          -0.0087      0.003     -2.497      0.013      -0.015      -0.002
=========================================================

In [145]:

vif_data=pd.DataFrame()
vif_data['Feature'] = X_tr_sm.columns

vif_data['VIF']=[variance_inflation_factor(X_tr_sm.values,i) for i in range(len(X_tr_sm.columns))]
vif_data = vif_data[vif_data['VIF'] >5]
vif_data

Feature         VIF
0   const  350.518902

In [146]:
X_tr_sm.head()

const   LotArea  OverallQual  OverallCond  YearBuilt  YearRemodAdd  \
318     1.0  0.040197     0.666667        0.500   0.876812      0.716667   
239     1.0  0.034780     0.555556        0.375   0.528986      0.000000   
986     1.0  0.018743     0.555556        0.875   0.275362      0.883333   
1416    1.0  0.046928     0.333333        0.625   0.094203      0.000000   
390     1.0  0.033209     0.444444        0.875   0.202899      0.000000   

      MasVnrArea  TotalBsmtSF  2ndFlrSF  BsmtFullBath  ...  Condition2_PosA  \
318         0.16     0.220458  0.616949      0.333333  ...              0.0   
239         0.00     0.120295  0.333656      0.000000  ...              0.0   
986         0.00     0.079378  0.307022      0.000000  ...              0.0   
1416        0.00     0.127169  0.505569      0.000000  ...              0.0   
390         0.00     0.140917  0.196610      0.333333  ...              0.0   

      Condition2_PosN  BldgType_Twnhs  BldgType_TwnhsE  RoofMatl_WdShngl  \
318               0.0             0.0              0.0               0.0   
239               0.0             0.0              0.0               0.0   
986               0.0             0.0              0.0               0.0   
1416              0.0             0.0              0.0               0.0   
390               0.0             0.0              0.0               0.0   

      Exterior1st_BrkFace  Exterior2nd_CmentBd  BsmtQual_Gd  BsmtExposure_Gd  \
318                   0.0                  0.0          1.0              1.0   
239                   0.0                  0.0          0.0              0.0   
986                   0.0                  0.0          0.0              0.0   
1416                  0.0                  0.0          0.0              0.0   
390                   0.0                  0.0          0.0              0.0   

      KitchenQual_Gd  
318              1.0  
239              0.0  
986              1.0  
1416             0.0  
390              0.0  

[5 rows x 31 columns]

In [147]:
X_tr = X_tr_sm.pop('const')
X_tr = X_tr_sm
X_te = X_te[X_tr.columns]

In [148]:
#Linear Regression

lm = LinearRegression()

# Fit a line
lm.fit(X_tr, y_tr)
y_pred_train = lm.predict(X_tr)
y_pred_test = lm.predict(X_te)

metric = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric.append(mse_test_lr**0.5)

0.8527538537081485
0.8079629391635267
1.8121967627922027
1.046476172107447
0.0017749233719806098
0.0023837726016114964


In [149]:
from sklearn.model_selection import GridSearchCV

params = {'alpha': [0.0001, 0.001, 0.01, 0.05, 0.1, 
 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 2.0, 3.0, 
 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 20, 50, 100, 500, 1000 ]}

ridge = Ridge()

# cross validation
folds = 5
model_cv = GridSearchCV(estimator = ridge, 
                        param_grid = params, 
                        scoring= 'neg_mean_absolute_error',  
                        cv = folds, 
                        return_train_score=True,
                        verbose = 1)            
model_cv.fit(X_tr, y_tr) 

Fitting 5 folds for each of 28 candidates, totalling 140 fits


GridSearchCV(cv=5, estimator=Ridge(),
             param_grid={'alpha': [0.0001, 0.001, 0.01, 0.05, 0.1, 0.2, 0.3,
                                   0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 2.0, 3.0,
                                   4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 20, 50,
                                   100, 500, 1000]},
             return_train_score=True, scoring='neg_mean_absolute_error',
             verbose=1)

In [150]:
print(model_cv.best_params_)

{'alpha': 0.0001}


In [151]:
alpha = 0.0001
ridge = Ridge(alpha=alpha)

ridge.fit(X_tr, y_tr)
print(ridge.coef_)

[ 0.11955177  0.1953491   0.04199893  0.10082208  0.03147895  0.0409893
  0.29216545  0.11799563  0.04163408  0.07153686  0.03174846  0.04780743
  0.01817156  0.05742918 -0.02186065  0.08235746  0.06637786  0.02663451
  0.05556421  0.01478561  0.09241723 -0.40172057 -0.06846385 -0.03136015
  0.11983852  0.05333309  0.03026974 -0.02487368  0.03460425 -0.00865652]


In [152]:

# Lets calculate some metrics such as R2 score, RSS and RMSE
y_test = y_te
y_train = y_tr
y_pred_train = ridge.predict(X_tr)
y_pred_test = ridge.predict(X_te)

metric2 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric2.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric2.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric2.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric2.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric2.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric2.append(mse_test_lr**0.5)

0.8527538535153367
0.8079685442415017
1.8121967651651887
1.0464456281045447
0.0017749233743047882
0.0023837030252950903


In [153]:
lasso = Lasso()

# cross validation
model_cv = GridSearchCV(estimator = lasso, 
                        param_grid = params, 
                        scoring= 'neg_mean_absolute_error', 
                        cv = folds, 
                        return_train_score=True,
                        verbose = 1)            

model_cv.fit(X_tr, y_tr) 
print(model_cv.best_params_)

Fitting 5 folds for each of 28 candidates, totalling 140 fits
{'alpha': 0.0001}


In [154]:
alpha = 0.0001
lasso = Lasso(alpha=alpha)

lasso.fit(X_tr, y_tr)
print(lasso.coef_)

[ 0.06800817  0.20890446  0.03104815  0.08801348  0.03249014  0.03600423
  0.27120286  0.11138906  0.04033693  0.0774634   0.03134977  0.01370823
  0.01860365  0.05343982 -0.01795687  0.08135871  0.06379272  0.02241813
  0.04444355  0.01375866  0.         -0.28033244 -0.06469419 -0.02957078
  0.10023379  0.05060388  0.02509769 -0.02339904  0.0355977  -0.00668081]


In [155]:
# Lets calculate some metrics such as R2 score, RSS and RMSE

y_pred_train = lasso.predict(X_tr)
y_pred_test = lasso.predict(X_te)

metric3 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric3.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric3.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric3.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric3.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric3.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric3.append(mse_test_lr**0.5)

finalMetric = metric3

0.8495729001133265
0.8164949358639633
1.851345589109891
0.9999823796664704
0.001813266982477856
0.002277864190584215


In [156]:
# Creating a table which contain all the metrics

lr_table = {'Metric': ['R2 Score (Train)','R2 Score (Test)','RSS (Train)','RSS (Test)',
                       'MSE (Train)','MSE (Test)'], 
        'Linear Regression': metric
        }

lr_metric = pd.DataFrame(lr_table ,columns = ['Metric', 'Linear Regression'] )

rg_metric = pd.Series(metric2, name = 'Ridge Regression')
ls_metric = pd.Series(metric3, name = 'Lasso Regression')

final_metric = pd.concat([lr_metric, rg_metric, ls_metric], axis = 1)

final_metric

betas = pd.DataFrame(index=X_tr.columns)
betas.rows = X_tr.columns

betas['Linear'] = lm.coef_
betas['Ridge'] = ridge.coef_
betas['Lasso'] = lasso.coef_

lasso_final = lasso
X_tr_final = X_tr
X_te_final = X_te

pd.set_option('display.max_rows', None)
betas.head(68)

Linear     Ridge     Lasso
LotArea               0.119557  0.119552  0.068008
OverallQual           0.195348  0.195349  0.208904
OverallCond           0.042000  0.041999  0.031048
YearBuilt             0.100823  0.100822  0.088013
YearRemodAdd          0.031479  0.031479  0.032490
MasVnrArea            0.040989  0.040989  0.036004
TotalBsmtSF           0.292177  0.292165  0.271203
2ndFlrSF              0.117998  0.117996  0.111389
BsmtFullBath          0.041634  0.041634  0.040337
GarageArea            0.071535  0.071537  0.077463
WoodDeckSF            0.031748  0.031748  0.031350
Street_Pave           0.047809  0.047807  0.013708
LotConfig_CulDSac     0.018171  0.018172  0.018604
Neighborhood_Crawfor  0.057429  0.057429  0.053440
Neighborhood_Mitchel -0.021861 -0.021861 -0.017957
Neighborhood_NoRidge  0.082357  0.082357  0.081359
Neighborhood_NridgHt  0.066377  0.066378  0.063793
Neighborhood_Somerst  0.026635  0.026635  0.022418
Neighborhood_StoneBr  0.055564  0.055564  0.044444
Condition1_Norm       0.014785  0.014786  0.013759
Condition2_PosA       0.092426  0.092417  0.000000
Condition2_PosN      -0.401767 -0.401721 -0.280332
BldgType_Twnhs       -0.068464 -0.068464 -0.064694
BldgType_TwnhsE      -0.031360 -0.031360 -0.029571
RoofMatl_WdShngl      0.119840  0.119839  0.100234
Exterior1st_BrkFace   0.053333  0.053333  0.050604
Exterior2nd_CmentBd   0.030271  0.030270  0.025098
BsmtQual_Gd          -0.024874 -0.024874 -0.023399
BsmtExposure_Gd       0.034604  0.034604  0.035598
KitchenQual_Gd       -0.008657 -0.008657 -0.006681

In [157]:
lr_table = {'Metric': ['R2 Score (Train)','R2 Score (Test)','RSS (Train)','RSS (Test)',
                       'MSE (Train)','MSE (Test)'], 
        'Linear Regression': metric
        }

lr_metric = pd.DataFrame(lr_table ,columns = ['Metric', 'Linear Regression'] )

rg_metric = pd.Series(metric2, name = 'Ridge Regression')
ls_metric = pd.Series(metric3, name = 'Lasso Regression')

final_metric_all = pd.concat([lr_metric, rg_metric, ls_metric], axis = 1)

final_metric_all

Metric  Linear Regression  Ridge Regression  Lasso Regression
0  R2 Score (Train)           0.852754          0.852754          0.849573
1   R2 Score (Test)           0.807963          0.807969          0.816495
2       RSS (Train)           1.812197          1.812197          1.851346
3        RSS (Test)           1.046476          1.046446          0.999982
4       MSE (Train)           0.042130          0.042130          0.042582
5        MSE (Test)           0.048824          0.048823          0.047727

In [158]:
alpha = 0.0001 * 2
ridge = Ridge(alpha=alpha)

ridge.fit(X_tr, y_tr)
print(ridge.coef_)

y_pred_train = ridge.predict(X_tr)
y_pred_test = ridge.predict(X_te)

metric2 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric2.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric2.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric2.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric2.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric2.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric2.append(mse_test_lr**0.5)

[ 0.11954617  0.19535025  0.0419979   0.10082083  0.03147922  0.04098941
  0.29215382  0.11799354  0.04163456  0.0715384   0.03174913  0.04780573
  0.01817182  0.05742926 -0.02186055  0.08235816  0.06637838  0.02663451
  0.05556418  0.01478577  0.09240835 -0.40167427 -0.06846396 -0.03136039
  0.1198367   0.05333327  0.03026874 -0.0248734   0.03460442 -0.00865635]
0.8527538529370576
0.8079741471634462
1.81219677228222
1.0464150958505951
0.001774923381275436
0.0023836334757416744


In [159]:
alpha = 0.0001*2
lasso = Lasso(alpha=alpha)

lasso.fit(X_tr, y_tr)
print(lasso.coef_)

    
    
y_pred_train = lasso.predict(X_tr)
y_pred_test = lasso.predict(X_te)

metric3 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric3.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric3.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric3.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric3.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric3.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric3.append(mse_test_lr**0.5)

[ 0.02328761  0.21864068  0.01925576  0.07831268  0.03320345  0.03165003
  0.24820434  0.10432207  0.039456    0.08156663  0.03162842  0.
  0.01892051  0.05037322 -0.01459698  0.08103832  0.06184936  0.01868675
  0.03426432  0.01316577  0.         -0.15787684 -0.06135285 -0.02811148
  0.08017276  0.04776383  0.01994737 -0.02186476  0.03691688 -0.00506139]
0.8426771248747098
0.8167186063716918
1.9362136951966544
0.9987635219328559
0.0018963895153738045
0.002275087749277576


In [160]:
betas = pd.DataFrame(index=X_tr.columns)
betas.rows = X_tr.columns

betas['Linear'] = lm.coef_
betas['Ridge'] = ridge.coef_
betas['Lasso'] = lasso.coef_

pd.set_option('display.max_rows', None)
betas.head(68)

Linear     Ridge     Lasso
LotArea               0.119557  0.119546  0.023288
OverallQual           0.195348  0.195350  0.218641
OverallCond           0.042000  0.041998  0.019256
YearBuilt             0.100823  0.100821  0.078313
YearRemodAdd          0.031479  0.031479  0.033203
MasVnrArea            0.040989  0.040989  0.031650
TotalBsmtSF           0.292177  0.292154  0.248204
2ndFlrSF              0.117998  0.117994  0.104322
BsmtFullBath          0.041634  0.041635  0.039456
GarageArea            0.071535  0.071538  0.081567
WoodDeckSF            0.031748  0.031749  0.031628
Street_Pave           0.047809  0.047806  0.000000
LotConfig_CulDSac     0.018171  0.018172  0.018921
Neighborhood_Crawfor  0.057429  0.057429  0.050373
Neighborhood_Mitchel -0.021861 -0.021861 -0.014597
Neighborhood_NoRidge  0.082357  0.082358  0.081038
Neighborhood_NridgHt  0.066377  0.066378  0.061849
Neighborhood_Somerst  0.026635  0.026635  0.018687
Neighborhood_StoneBr  0.055564  0.055564  0.034264
Condition1_Norm       0.014785  0.014786  0.013166
Condition2_PosA       0.092426  0.092408  0.000000
Condition2_PosN      -0.401767 -0.401674 -0.157877
BldgType_Twnhs       -0.068464 -0.068464 -0.061353
BldgType_TwnhsE      -0.031360 -0.031360 -0.028111
RoofMatl_WdShngl      0.119840  0.119837  0.080173
Exterior1st_BrkFace   0.053333  0.053333  0.047764
Exterior2nd_CmentBd   0.030271  0.030269  0.019947
BsmtQual_Gd          -0.024874 -0.024873 -0.021865
BsmtExposure_Gd       0.034604  0.034604  0.036917
KitchenQual_Gd       -0.008657 -0.008656 -0.005061

In [161]:
lr_table = {'Metric': ['R2 Score (Train)','R2 Score (Test)','RSS (Train)','RSS (Test)',
                       'MSE (Train)','MSE (Test)'], 
        'Linear Regression': metric
        }

lr_metric = pd.DataFrame(lr_table ,columns = ['Metric', 'Linear Regression'] )

rg_metric = pd.Series(metric2, name = 'Ridge Regression')
ls_metric = pd.Series(metric3, name = 'Lasso Regression')

final_metric = pd.concat([lr_metric, rg_metric, ls_metric], axis = 1)

final_metric

Metric  Linear Regression  Ridge Regression  Lasso Regression
0  R2 Score (Train)           0.852754          0.852754          0.842677
1   R2 Score (Test)           0.807963          0.807974          0.816719
2       RSS (Train)           1.812197          1.812197          1.936214
3        RSS (Test)           1.046476          1.046415          0.998764
4       MSE (Train)           0.042130          0.042130          0.043548
5        MSE (Test)           0.048824          0.048822          0.047698

In [162]:
#Removing five most predictor variables from lasso Regresson
columns_rem = ['OverallQual','TotalBsmtSF','Condition2_PosN','2ndFlrSF','RoofMatl_WdShngl']
X_tr = X_tr.drop(columns_rem, axis=1)
X_te = X_te.drop(columns_rem, axis=1)

X_tr.head()
X_te.head()

LotArea  OverallCond  YearBuilt  YearRemodAdd  MasVnrArea  \
1436  0.035991        0.625   0.717391      0.350000     0.00000   
57    0.048354        0.500   0.956522      0.900000     0.00000   
780   0.030732        0.500   0.891304      0.766667     0.02375   
382   0.037136        0.500   0.971014      0.933333     0.00000   
1170  0.040104        0.625   0.760870      0.450000     0.00000   

      BsmtFullBath  GarageArea  WoodDeckSF  Street_Pave  LotConfig_CulDSac  \
1436      0.000000    0.372355    0.000000          1.0                0.0   
57        0.000000    0.398449    0.000000          1.0                0.0   
780       0.000000    0.283498    0.256709          1.0                0.0   
382       0.000000    0.450635    0.168028          1.0                0.0   
1170      0.333333    0.252468    0.236873          1.0                0.0   

      ...  Neighborhood_StoneBr  Condition1_Norm  Condition2_PosA  \
1436  ...                   0.0              1.0              0.0   
57    ...                   0.0              1.0              0.0   
780   ...                   0.0              1.0              0.0   
382   ...                   0.0              1.0              0.0   
1170  ...                   0.0              1.0              0.0   

      BldgType_Twnhs  BldgType_TwnhsE  Exterior1st_BrkFace  \
1436             0.0              0.0                  0.0   
57               0.0              0.0                  0.0   
780              0.0              0.0                  0.0   
382              0.0              0.0                  0.0   
1170             0.0              0.0                  0.0   

      Exterior2nd_CmentBd  BsmtQual_Gd  BsmtExposure_Gd  KitchenQual_Gd  
1436                  0.0          0.0              0.0             0.0  
57                    0.0          1.0              0.0             1.0  
780                   0.0          1.0              0.0             0.0  
382                   0.0          1.0              0.0             1.0  
1170                  0.0          0.0              0.0             0.0  

[5 rows x 25 columns]

In [163]:
alpha = 0.0001
lassoNew = Lasso(alpha=alpha)

lassoNew.fit(X_tr, y_tr)
print(lassoNew.coef_)



y_pred_train = lassoNew.predict(X_tr)
y_pred_test = lassoNew.predict(X_te)

metric3 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric3.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric3.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric3.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric3.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric3.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric3.append(mse_test_lr**0.5)

[ 0.17348568  0.02639497  0.107466    0.06166547  0.11268112  0.02440733
  0.16046915  0.05978435  0.05642832  0.0172809   0.08722709 -0.03465625
  0.14195385  0.09922045  0.03713662  0.09668362  0.01046756  0.11615925
 -0.0713437  -0.04120801  0.05632881  0.02868995 -0.01442024  0.04801057
 -0.00152598]
0.736371212253173
0.6968267127231837
3.244548314267637
1.652095797408792
0.0031778142157371566
0.003763316167218205


In [164]:
betas = pd.DataFrame(index=X_tr.columns)
betas.rows = X_tr.columns

betas['LassoRemoved5Col'] = lassoNew.coef_

pd.set_option('display.max_rows', None)
betas.head(68)

LassoRemoved5Col
LotArea                       0.173486
OverallCond                   0.026395
YearBuilt                     0.107466
YearRemodAdd                  0.061665
MasVnrArea                    0.112681
BsmtFullBath                  0.024407
GarageArea                    0.160469
WoodDeckSF                    0.059784
Street_Pave                   0.056428
LotConfig_CulDSac             0.017281
Neighborhood_Crawfor          0.087227
Neighborhood_Mitchel         -0.034656
Neighborhood_NoRidge          0.141954
Neighborhood_NridgHt          0.099220
Neighborhood_Somerst          0.037137
Neighborhood_StoneBr          0.096684
Condition1_Norm               0.010468
Condition2_PosA               0.116159
BldgType_Twnhs               -0.071344
BldgType_TwnhsE              -0.041208
Exterior1st_BrkFace           0.056329
Exterior2nd_CmentBd           0.028690
BsmtQual_Gd                  -0.014420
BsmtExposure_Gd               0.048011
KitchenQual_Gd               -0.001526

In [165]:
# final co-efficients using Lasso method with Alpha = 0.0001 are below.
# R2 square are below
betas = pd.DataFrame(index=X_tr_final.columns)
betas.rows = X_tr_final.columns

betas['LassoRemoved5Col'] = lasso_final.coef_

pd.set_option('display.max_rows', None)
print(betas.head(68))
final_metric_all

                      LassoRemoved5Col
LotArea                       0.068008
OverallQual                   0.208904
OverallCond                   0.031048
YearBuilt                     0.088013
YearRemodAdd                  0.032490
MasVnrArea                    0.036004
TotalBsmtSF                   0.271203
2ndFlrSF                      0.111389
BsmtFullBath                  0.040337
GarageArea                    0.077463
WoodDeckSF                    0.031350
Street_Pave                   0.013708
LotConfig_CulDSac             0.018604
Neighborhood_Crawfor          0.053440
Neighborhood_Mitchel         -0.017957
Neighborhood_NoRidge          0.081359
Neighborhood_NridgHt          0.063793
Neighborhood_Somerst          0.022418
Neighborhood_StoneBr          0.044444
Condition1_Norm               0.013759
Condition2_PosA               0.000000
Condition2_PosN              -0.280332
BldgType_Twnhs               -0.064694
BldgType_TwnhsE              -0.029571
RoofMatl_WdShngl         

Metric  Linear Regression  Ridge Regression  Lasso Regression
0  R2 Score (Train)           0.852754          0.852754          0.849573
1   R2 Score (Test)           0.807963          0.807969          0.816495
2       RSS (Train)           1.812197          1.812197          1.851346
3        RSS (Test)           1.046476          1.046446          0.999982
4       MSE (Train)           0.042130          0.042130          0.042582
5        MSE (Test)           0.048824          0.048823          0.047727